# Default Code

##        
return ['JYW',
 'PLX',
 'QVE',
 'BLR',
 'OGU',
 'BSN',
 'VML',
 'KKG',
 'VND',
 'NDG',
 'PFK',
 'MUF',
 'QRK',
 'GYV',
 'CBT',
 'YHW',
 'HHK',
 'XIT',
 'GYJ',
 'YUZ',
 'DYE',
 'ZEW',
 'ZLX',
 'FRE',
 'GFQ',
 'XPV',
 'YGC',
 'ESY',
 'FUR',
 'IFL',
 'PQS',
 'KRZ',
 'OED',
 'FCY',
 'XCS',
 'IES',
 'QTY',
 'CQD',
 'XYR',
 'LPQ',
 'DUR',
 'XAD',
 'EGV',
 'LKB',
 'VSL',
 'NYO',
 'IUE',
 'AGW',
 'NNA',
 'RGG',
 'XZR',
 'ROP',
 'MAS',
 'PUO',
 'BWU',
 'LDU',
 'UWD',
 'PMS',
 'ZSI',
 'NBQ',
 'KAA',
 'FFA',
 'ILW',
 'WTJ',
 'VTN',
 'XFD',
 'CUN',
 'IUQ',
 'IMC',
 'NSL',
 'JCR',
 'WAG',
 'VG',
 'VKE',
 'UWC',
 'HDK',
 'IWU',
 'IYU',
 'HZT',
 'TGI',
 'AUZ',
 'JSG',
 'OMP',
 'CYD',
 'CHV',
 'UBF',
 'DCO',
 'DVV',
 'WUT',
 'FKI',
 'FFS',
 'AIO',
 'MQK',
 'GGK',
 'KFW']

In [2]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
         return ['AGW']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) / sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-25 09:17:00
2017-01-25 09:18:00
2017-01-25 09:19:00
2017-01-25 09:20:00
2017-01-25 09:21:00
2017-01-25 09:22:00
2017-01-25 09:23:00
2017-01-25 09:24:00
2017-01-25 09:25:00
2017-01-25 09:26:00
2017-01-25 09:27:00
2017-01-25 09:28:00
2017-01-25 09:29:00
2017-01-25 09:30:00
2017-01-25 09:31:00
2017-01-25 09:32:00
2017-01-25 09:33:00
2017-01-25 09:34:00
2017-01-25 09:35:00
2017-01-25 09:36:00
2017-01-25 09:37:00
2017-01-25 09:38:00
2017-01-25 09:39:00
2017-01-25 09:40:00
2017-01-25 09:41:00
2017-01-25 09:42:00
2017-01-25 09:43:00
2017-01-25 09:44:00
2017-01-25 09:45:00
2017-01-25 09:46:00
2017-01-25 09:47:00
2017-01-25 09:48:00
2017-01-25 09:49:00
2017-01-25 09:50:00
2017-01-25 09:51:00
2017-01-25 09:52:00
2017-01-25 09:53:00
2017-01-25 09:54:00
2017-01-25 09:55:00
2017-01-25 09:56:00
2017-01-25 09:57:00
2017-01-25 09:58:00

2017-01-25 15:16:00
2017-01-25 15:17:00
2017-01-25 15:18:00
2017-01-25 15:19:00
2017-01-25 15:20:00
2017-01-25 15:21:00
2017-01-25 15:22:00
2017-01-25 15:23:00
2017-01-25 15:24:00
2017-01-25 15:25:00
2017-01-25 15:26:00
2017-01-25 15:27:00
2017-01-25 15:28:00
2017-01-26 09:17:00
2017-01-26 09:18:00
2017-01-26 09:19:00
2017-01-26 09:20:00
2017-01-26 09:21:00
2017-01-26 09:22:00
2017-01-26 09:23:00
2017-01-26 09:24:00
2017-01-26 09:25:00
2017-01-26 09:26:00
2017-01-26 09:27:00
2017-01-26 09:28:00
2017-01-26 09:29:00
2017-01-26 09:30:00
2017-01-26 09:31:00
2017-01-26 09:32:00
2017-01-26 09:33:00
2017-01-26 09:34:00
2017-01-26 09:35:00
2017-01-26 09:36:00
2017-01-26 09:37:00
2017-01-26 09:38:00
2017-01-26 09:39:00
2017-01-26 09:40:00
2017-01-26 09:41:00
2017-01-26 09:42:00
2017-01-26 09:43:00
2017-01-26 09:44:00
2017-01-26 09:45:00
2017-01-26 09:46:00
2017-01-26 09:47:00
2017-01-26 09:48:00
2017-01-26 09:49:00
2017-01-26 09:50:00
2017-01-26 09:51:00
2017-01-26 09:52:00
2017-01-26 09:53:00


2017-01-26 14:36:00
2017-01-26 14:37:00
2017-01-26 14:38:00
2017-01-26 14:39:00
2017-01-26 14:40:00
2017-01-26 14:41:00
2017-01-26 14:42:00
2017-01-26 14:43:00
2017-01-26 14:44:00
2017-01-26 14:45:00
2017-01-26 14:46:00
2017-01-26 14:47:00
2017-01-26 14:48:00
2017-01-26 14:49:00
2017-01-26 14:50:00
2017-01-26 14:51:00
2017-01-26 14:52:00
2017-01-26 14:53:00
2017-01-26 14:54:00
2017-01-26 14:55:00
2017-01-26 14:56:00
2017-01-26 14:57:00
2017-01-26 14:58:00
2017-01-26 14:59:00
Warn: Not Enough Capital
2017-01-26 15:00:00
Warn: Not Enough Capital
2017-01-26 15:01:00
Warn: Not Enough Capital
2017-01-26 15:02:00
Warn: Not Enough Capital
2017-01-26 15:03:00
Warn: Not Enough Capital
2017-01-26 15:04:00
Warn: Not Enough Capital
2017-01-26 15:05:00
Warn: Not Enough Capital
2017-01-26 15:06:00
Warn: Not Enough Capital
2017-01-26 15:07:00
Warn: Not Enough Capital
2017-01-26 15:08:00
Warn: Not Enough Capital
2017-01-26 15:09:00
Warn: Not Enough Capital
2017-01-26 15:10:00
Warn: Not Enough Capital


2017-01-27 14:13:00
2017-01-27 14:14:00
2017-01-27 14:15:00
2017-01-27 14:16:00
2017-01-27 14:17:00
2017-01-27 14:18:00
2017-01-27 14:19:00
2017-01-27 14:20:00
2017-01-27 14:21:00
2017-01-27 14:22:00
2017-01-27 14:23:00
2017-01-27 14:24:00
2017-01-27 14:25:00
2017-01-27 14:26:00
2017-01-27 14:27:00
2017-01-27 14:28:00
2017-01-27 14:29:00
2017-01-27 14:30:00
2017-01-27 14:31:00
2017-01-27 14:32:00
2017-01-27 14:33:00
2017-01-27 14:34:00
2017-01-27 14:35:00
2017-01-27 14:36:00
2017-01-27 14:37:00
2017-01-27 14:38:00
2017-01-27 14:39:00
2017-01-27 14:40:00
2017-01-27 14:41:00
2017-01-27 14:42:00
2017-01-27 14:43:00
2017-01-27 14:44:00
2017-01-27 14:45:00
2017-01-27 14:46:00
2017-01-27 14:47:00
2017-01-27 14:48:00
2017-01-27 14:49:00
2017-01-27 14:50:00
2017-01-27 14:51:00
2017-01-27 14:52:00
2017-01-27 14:53:00
2017-01-27 14:54:00
2017-01-27 14:55:00
2017-01-27 14:56:00
2017-01-27 14:57:00
2017-01-27 14:58:00
2017-01-27 14:59:00
2017-01-27 15:00:00
2017-01-27 15:01:00
2017-01-27 15:02:00


2017-01-30 14:09:00
2017-01-30 14:10:00
2017-01-30 14:11:00
2017-01-30 14:12:00
2017-01-30 14:13:00
2017-01-30 14:14:00
2017-01-30 14:15:00
2017-01-30 14:16:00
2017-01-30 14:17:00
2017-01-30 14:18:00
2017-01-30 14:19:00
2017-01-30 14:20:00
2017-01-30 14:21:00
2017-01-30 14:22:00
2017-01-30 14:23:00
2017-01-30 14:24:00
2017-01-30 14:25:00
2017-01-30 14:26:00
2017-01-30 14:27:00
2017-01-30 14:28:00
2017-01-30 14:29:00
2017-01-30 14:30:00
2017-01-30 14:31:00
2017-01-30 14:32:00
2017-01-30 14:33:00
2017-01-30 14:34:00
2017-01-30 14:35:00
2017-01-30 14:36:00
2017-01-30 14:37:00
2017-01-30 14:38:00
2017-01-30 14:39:00
2017-01-30 14:40:00
2017-01-30 14:41:00
2017-01-30 14:42:00
2017-01-30 14:43:00
2017-01-30 14:44:00
2017-01-30 14:45:00
2017-01-30 14:46:00
2017-01-30 14:47:00
2017-01-30 14:48:00
2017-01-30 14:49:00
2017-01-30 14:50:00
2017-01-30 14:51:00
2017-01-30 14:52:00
2017-01-30 14:53:00
2017-01-30 14:54:00
2017-01-30 14:55:00
2017-01-30 14:56:00
2017-01-30 14:57:00
2017-01-30 14:58:00


...

2017-03-03 14:23:00
2017-03-03 14:24:00
2017-03-03 14:25:00
2017-03-03 14:26:00
2017-03-03 14:27:00
2017-03-03 14:28:00
2017-03-03 14:29:00
2017-03-03 14:30:00
2017-03-03 14:31:00
2017-03-03 14:32:00
2017-03-03 14:33:00
2017-03-03 14:34:00
2017-03-03 14:35:00
2017-03-03 14:36:00
2017-03-03 14:37:00
2017-03-03 14:38:00
2017-03-03 14:39:00
Warn: Not Enough Capital
2017-03-03 14:40:00
Warn: Not Enough Capital
2017-03-03 14:41:00
Warn: Not Enough Capital
2017-03-03 14:42:00
Warn: Not Enough Capital
2017-03-03 14:43:00
Warn: Not Enough Capital
2017-03-03 14:44:00
Warn: Not Enough Capital
2017-03-03 14:45:00
Warn: Not Enough Capital
2017-03-03 14:46:00
Warn: Not Enough Capital
2017-03-03 14:47:00
Warn: Not Enough Capital
2017-03-03 14:48:00
Warn: Not Enough Capital
2017-03-03 14:49:00
Warn: Not Enough Capital
2017-03-03 14:50:00
Warn: Not Enough Capital
2017-03-03 14:51:00
Warn: Not Enough Capital
2017-03-03 14:52:00
Warn: Not Enough Capital
2017-03-03 14:53:00
Warn: Not Enough Capital
2017-

Warn: Not Enough Capital
2017-03-06 13:08:00
Warn: Not Enough Capital
2017-03-06 13:09:00
Warn: Not Enough Capital
2017-03-06 13:10:00
Warn: Not Enough Capital
2017-03-06 13:11:00
Warn: Not Enough Capital
2017-03-06 13:12:00
Warn: Not Enough Capital
2017-03-06 13:13:00
Warn: Not Enough Capital
2017-03-06 13:14:00
Warn: Not Enough Capital
2017-03-06 13:15:00
Warn: Not Enough Capital
2017-03-06 13:16:00
Warn: Not Enough Capital
2017-03-06 13:17:00
Warn: Not Enough Capital
2017-03-06 13:18:00
Warn: Not Enough Capital
2017-03-06 13:19:00
Warn: Not Enough Capital
2017-03-06 13:20:00
Warn: Not Enough Capital
2017-03-06 13:21:00
2017-03-06 13:22:00
2017-03-06 13:23:00
2017-03-06 13:24:00
2017-03-06 13:25:00
2017-03-06 13:26:00
2017-03-06 13:27:00
2017-03-06 13:28:00
2017-03-06 13:29:00
2017-03-06 13:30:00
2017-03-06 13:31:00
2017-03-06 13:32:00
2017-03-06 13:33:00
2017-03-06 13:34:00
2017-03-06 13:35:00
2017-03-06 13:36:00
2017-03-06 13:37:00
2017-03-06 13:38:00
2017-03-06 13:39:00
2017-03-06

2017-03-07 12:43:00
2017-03-07 12:44:00
2017-03-07 12:45:00
2017-03-07 12:46:00
2017-03-07 12:47:00
2017-03-07 12:48:00
2017-03-07 12:49:00
2017-03-07 12:50:00
2017-03-07 12:51:00
2017-03-07 12:52:00
2017-03-07 12:53:00
2017-03-07 12:54:00
2017-03-07 12:55:00
2017-03-07 12:56:00
2017-03-07 12:57:00
2017-03-07 12:58:00
2017-03-07 12:59:00
2017-03-07 13:00:00
2017-03-07 13:01:00
2017-03-07 13:02:00
2017-03-07 13:03:00
2017-03-07 13:04:00
2017-03-07 13:05:00
2017-03-07 13:06:00
2017-03-07 13:07:00
2017-03-07 13:08:00
2017-03-07 13:09:00
2017-03-07 13:10:00
2017-03-07 13:11:00
2017-03-07 13:12:00
2017-03-07 13:13:00
2017-03-07 13:14:00
2017-03-07 13:15:00
2017-03-07 13:16:00
2017-03-07 13:17:00
2017-03-07 13:18:00
2017-03-07 13:19:00
2017-03-07 13:20:00
2017-03-07 13:21:00
2017-03-07 13:22:00
2017-03-07 13:23:00
2017-03-07 13:24:00
2017-03-07 13:25:00
2017-03-07 13:26:00
2017-03-07 13:27:00
2017-03-07 13:28:00
2017-03-07 13:29:00
2017-03-07 13:30:00
2017-03-07 13:31:00
2017-03-07 13:32:00


2017-03-08 12:09:00
2017-03-08 12:10:00
2017-03-08 12:11:00
2017-03-08 12:12:00
2017-03-08 12:13:00
2017-03-08 12:14:00
2017-03-08 12:15:00
2017-03-08 12:16:00
2017-03-08 12:17:00
2017-03-08 12:18:00
2017-03-08 12:19:00
2017-03-08 12:20:00
2017-03-08 12:21:00
2017-03-08 12:22:00
2017-03-08 12:23:00
2017-03-08 12:24:00
2017-03-08 12:25:00
2017-03-08 12:26:00
2017-03-08 12:27:00
2017-03-08 12:28:00
2017-03-08 12:29:00
2017-03-08 12:30:00
2017-03-08 12:31:00
2017-03-08 12:32:00
2017-03-08 12:33:00
2017-03-08 12:34:00
2017-03-08 12:35:00
2017-03-08 12:36:00
2017-03-08 12:37:00
2017-03-08 12:38:00
2017-03-08 12:39:00
2017-03-08 12:40:00
2017-03-08 12:41:00
2017-03-08 12:42:00
2017-03-08 12:43:00
2017-03-08 12:44:00
2017-03-08 12:45:00
2017-03-08 12:46:00
2017-03-08 12:47:00
2017-03-08 12:48:00
2017-03-08 12:49:00
2017-03-08 12:50:00
2017-03-08 12:51:00
2017-03-08 12:52:00
2017-03-08 12:53:00
2017-03-08 12:54:00
2017-03-08 12:55:00
2017-03-08 12:56:00
2017-03-08 12:57:00
2017-03-08 12:58:00


2017-03-09 11:47:00
2017-03-09 11:48:00
2017-03-09 11:49:00
2017-03-09 11:50:00
2017-03-09 11:51:00
2017-03-09 11:52:00
2017-03-09 11:53:00
Warn: Not Enough Capital
2017-03-09 11:54:00
Warn: Not Enough Capital
2017-03-09 11:55:00
Warn: Not Enough Capital
2017-03-09 11:56:00
Warn: Not Enough Capital
2017-03-09 11:57:00
Warn: Not Enough Capital
2017-03-09 11:58:00
Warn: Not Enough Capital
2017-03-09 11:59:00
Warn: Not Enough Capital
2017-03-09 12:00:00
Warn: Not Enough Capital
2017-03-09 12:01:00
Warn: Not Enough Capital
2017-03-09 12:02:00
Warn: Not Enough Capital
2017-03-09 12:03:00
Warn: Not Enough Capital
2017-03-09 12:04:00
Warn: Not Enough Capital
2017-03-09 12:05:00
Warn: Not Enough Capital
2017-03-09 12:06:00
Warn: Not Enough Capital
2017-03-09 12:07:00
Warn: Not Enough Capital
2017-03-09 12:08:00
Warn: Not Enough Capital
2017-03-09 12:09:00
Warn: Not Enough Capital
2017-03-09 12:10:00
Warn: Not Enough Capital
2017-03-09 12:11:00
Warn: Not Enough Capital
2017-03-09 12:12:00
2017-

In [7]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
         return ['AGW']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 6,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) / sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-25 09:17:00
2017-01-25 09:18:00
2017-01-25 09:19:00
2017-01-25 09:20:00
2017-01-25 09:21:00
2017-01-25 09:22:00
2017-01-25 09:23:00
2017-01-25 09:24:00
2017-01-25 09:25:00
2017-01-25 09:26:00
2017-01-25 09:27:00
2017-01-25 09:28:00
2017-01-25 09:29:00
2017-01-25 09:30:00
2017-01-25 09:31:00
2017-01-25 09:32:00
2017-01-25 09:33:00
2017-01-25 09:34:00
2017-01-25 09:35:00
2017-01-25 09:36:00
2017-01-25 09:37:00
2017-01-25 09:38:00
2017-01-25 09:39:00
2017-01-25 09:40:00
2017-01-25 09:41:00
2017-01-25 09:42:00
2017-01-25 09:43:00
2017-01-25 09:44:00
2017-01-25 09:45:00
2017-01-25 09:46:00
2017-01-25 09:47:00
2017-01-25 09:48:00
2017-01-25 09:49:00
2017-01-25 09:50:00
2017-01-25 09:51:00
2017-01-25 09:52:00
2017-01-25 09:53:00
2017-01-25 09:54:00
2017-01-25 09:55:00
2017-01-25 09:56:00
2017-01-25 09:57:00
2017-01-25 09:58:00

2017-01-26 09:47:00
2017-01-26 09:48:00
2017-01-26 09:49:00
2017-01-26 09:50:00
2017-01-26 09:51:00
2017-01-26 09:52:00
2017-01-26 09:53:00
2017-01-26 09:54:00
2017-01-26 09:55:00
2017-01-26 09:56:00
2017-01-26 09:57:00
2017-01-26 09:58:00
2017-01-26 09:59:00
2017-01-26 10:00:00
2017-01-26 10:01:00
2017-01-26 10:02:00
2017-01-26 10:03:00
2017-01-26 10:04:00
2017-01-26 10:05:00
2017-01-26 10:06:00
2017-01-26 10:07:00
2017-01-26 10:08:00
2017-01-26 10:09:00
2017-01-26 10:10:00
2017-01-26 10:11:00
2017-01-26 10:12:00
2017-01-26 10:13:00
2017-01-26 10:14:00
2017-01-26 10:15:00
2017-01-26 10:16:00
2017-01-26 10:17:00
2017-01-26 10:18:00
2017-01-26 10:19:00
2017-01-26 10:20:00
2017-01-26 10:21:00
2017-01-26 10:22:00
2017-01-26 10:23:00
2017-01-26 10:24:00
2017-01-26 10:25:00
2017-01-26 10:26:00
2017-01-26 10:27:00
2017-01-26 10:28:00
2017-01-26 10:29:00
2017-01-26 10:30:00
2017-01-26 10:31:00
2017-01-26 10:32:00
2017-01-26 10:33:00
2017-01-26 10:34:00
2017-01-26 10:35:00
2017-01-26 10:36:00


2017-01-27 10:26:00
2017-01-27 10:27:00
2017-01-27 10:28:00
2017-01-27 10:29:00
2017-01-27 10:30:00
2017-01-27 10:31:00
2017-01-27 10:32:00
2017-01-27 10:33:00
2017-01-27 10:34:00
2017-01-27 10:35:00
2017-01-27 10:36:00
2017-01-27 10:37:00
2017-01-27 10:38:00
2017-01-27 10:39:00
2017-01-27 10:40:00
2017-01-27 10:41:00
2017-01-27 10:42:00
2017-01-27 10:43:00
2017-01-27 10:44:00
2017-01-27 10:45:00
2017-01-27 10:46:00
2017-01-27 10:47:00
2017-01-27 10:48:00
2017-01-27 10:49:00
2017-01-27 10:50:00
2017-01-27 10:51:00
2017-01-27 10:52:00
2017-01-27 10:53:00
2017-01-27 10:54:00
2017-01-27 10:55:00
2017-01-27 10:56:00
2017-01-27 10:57:00
2017-01-27 10:58:00
2017-01-27 10:59:00
2017-01-27 11:00:00
2017-01-27 11:01:00
2017-01-27 11:02:00
2017-01-27 11:03:00
2017-01-27 11:04:00
2017-01-27 11:05:00
2017-01-27 11:06:00
2017-01-27 11:07:00
2017-01-27 11:08:00
2017-01-27 11:09:00
2017-01-27 11:10:00
2017-01-27 11:11:00
2017-01-27 11:12:00
2017-01-27 11:13:00
2017-01-27 11:14:00
2017-01-27 11:15:00


2017-01-30 11:09:00
2017-01-30 11:10:00
2017-01-30 11:11:00
2017-01-30 11:12:00
2017-01-30 11:13:00
2017-01-30 11:14:00
2017-01-30 11:15:00
2017-01-30 11:16:00
2017-01-30 11:17:00
2017-01-30 11:18:00
2017-01-30 11:19:00
2017-01-30 11:20:00
2017-01-30 11:21:00
2017-01-30 11:22:00
2017-01-30 11:23:00
2017-01-30 11:24:00
2017-01-30 11:25:00
2017-01-30 11:26:00
2017-01-30 11:27:00
2017-01-30 11:28:00
2017-01-30 11:29:00
2017-01-30 11:30:00
2017-01-30 11:31:00
2017-01-30 11:32:00
2017-01-30 11:33:00
2017-01-30 11:34:00
2017-01-30 11:35:00
2017-01-30 11:36:00
2017-01-30 11:37:00
2017-01-30 11:38:00
2017-01-30 11:39:00
2017-01-30 11:40:00
2017-01-30 11:41:00
2017-01-30 11:42:00
2017-01-30 11:43:00
2017-01-30 11:44:00
2017-01-30 11:45:00
2017-01-30 11:46:00
2017-01-30 11:47:00
2017-01-30 11:48:00
2017-01-30 11:49:00
2017-01-30 11:50:00
2017-01-30 11:51:00
2017-01-30 11:52:00
2017-01-30 11:53:00
2017-01-30 11:54:00
2017-01-30 11:55:00
2017-01-30 11:56:00
2017-01-30 11:57:00
2017-01-30 11:58:00


C:\Users\hp\Anaconda2\lib\site-packages\backtester\features\score_logloss_feature.py:35: RuntimeWarning:

divide by zero encountered in log



...

2017-03-02 14:18:00
2017-03-02 14:19:00
2017-03-02 14:20:00
2017-03-02 14:21:00
2017-03-02 14:22:00
2017-03-02 14:23:00
2017-03-02 14:24:00
2017-03-02 14:25:00
2017-03-02 14:26:00
2017-03-02 14:27:00
2017-03-02 14:28:00
2017-03-02 14:29:00
2017-03-02 14:30:00
2017-03-02 14:31:00
2017-03-02 14:32:00
2017-03-02 14:33:00
2017-03-02 14:34:00
2017-03-02 14:35:00
2017-03-02 14:36:00
2017-03-02 14:37:00
2017-03-02 14:38:00
2017-03-02 14:39:00
2017-03-02 14:40:00
2017-03-02 14:41:00
2017-03-02 14:42:00
2017-03-02 14:43:00
2017-03-02 14:44:00
2017-03-02 14:45:00
2017-03-02 14:46:00
2017-03-02 14:47:00
2017-03-02 14:48:00
2017-03-02 14:49:00
2017-03-02 14:50:00
2017-03-02 14:51:00
2017-03-02 14:52:00
2017-03-02 14:53:00
2017-03-02 14:54:00
2017-03-02 14:55:00
2017-03-02 14:56:00
2017-03-02 14:57:00
2017-03-02 14:58:00
2017-03-02 14:59:00
2017-03-02 15:00:00
2017-03-02 15:01:00
2017-03-02 15:02:00
2017-03-02 15:03:00
2017-03-02 15:04:00
2017-03-02 15:05:00
2017-03-02 15:06:00
2017-03-02 15:07:00


2017-03-03 14:58:00
2017-03-03 14:59:00
2017-03-03 15:00:00
2017-03-03 15:01:00
2017-03-03 15:02:00
2017-03-03 15:03:00
2017-03-03 15:04:00
2017-03-03 15:05:00
2017-03-03 15:06:00
2017-03-03 15:07:00
2017-03-03 15:08:00
2017-03-03 15:09:00
2017-03-03 15:10:00
2017-03-03 15:11:00
2017-03-03 15:12:00
2017-03-03 15:13:00
2017-03-03 15:14:00
2017-03-03 15:15:00
2017-03-03 15:16:00
2017-03-03 15:17:00
2017-03-03 15:18:00
2017-03-03 15:19:00
2017-03-03 15:20:00
2017-03-03 15:21:00
2017-03-03 15:22:00
2017-03-03 15:23:00
2017-03-03 15:24:00
2017-03-03 15:25:00
2017-03-03 15:26:00
2017-03-03 15:27:00
2017-03-03 15:28:00
2017-03-06 09:17:00
2017-03-06 09:18:00
2017-03-06 09:19:00
2017-03-06 09:20:00
2017-03-06 09:21:00
2017-03-06 09:22:00
2017-03-06 09:23:00
2017-03-06 09:24:00
2017-03-06 09:25:00
2017-03-06 09:26:00
2017-03-06 09:27:00
2017-03-06 09:28:00
2017-03-06 09:29:00
2017-03-06 09:30:00
2017-03-06 09:31:00
2017-03-06 09:32:00
2017-03-06 09:33:00
2017-03-06 09:34:00
2017-03-06 09:35:00


2017-03-07 09:28:00
2017-03-07 09:29:00
2017-03-07 09:30:00
2017-03-07 09:31:00
2017-03-07 09:32:00
2017-03-07 09:33:00
2017-03-07 09:34:00
2017-03-07 09:35:00
2017-03-07 09:36:00
2017-03-07 09:37:00
2017-03-07 09:38:00
2017-03-07 09:39:00
2017-03-07 09:40:00
2017-03-07 09:41:00
2017-03-07 09:42:00
2017-03-07 09:43:00
2017-03-07 09:44:00
2017-03-07 09:45:00
2017-03-07 09:46:00
2017-03-07 09:47:00
2017-03-07 09:48:00
2017-03-07 09:49:00
2017-03-07 09:50:00
2017-03-07 09:51:00
2017-03-07 09:52:00
2017-03-07 09:53:00
2017-03-07 09:54:00
2017-03-07 09:55:00
2017-03-07 09:56:00
2017-03-07 09:57:00
2017-03-07 09:58:00
2017-03-07 09:59:00
2017-03-07 10:00:00
2017-03-07 10:01:00
2017-03-07 10:02:00
2017-03-07 10:03:00
2017-03-07 10:04:00
2017-03-07 10:05:00
2017-03-07 10:06:00
2017-03-07 10:07:00
2017-03-07 10:08:00
2017-03-07 10:09:00
2017-03-07 10:10:00
2017-03-07 10:11:00
2017-03-07 10:12:00
2017-03-07 10:13:00
2017-03-07 10:14:00
2017-03-07 10:15:00
2017-03-07 10:16:00
2017-03-07 10:17:00


2017-03-08 10:08:00
2017-03-08 10:09:00
2017-03-08 10:10:00
2017-03-08 10:11:00
2017-03-08 10:12:00
2017-03-08 10:13:00
2017-03-08 10:14:00
2017-03-08 10:15:00
2017-03-08 10:16:00
2017-03-08 10:17:00
2017-03-08 10:18:00
2017-03-08 10:19:00
2017-03-08 10:20:00
2017-03-08 10:21:00
2017-03-08 10:22:00
2017-03-08 10:23:00
2017-03-08 10:24:00
2017-03-08 10:25:00
2017-03-08 10:26:00
2017-03-08 10:27:00
2017-03-08 10:28:00
2017-03-08 10:29:00
2017-03-08 10:30:00
2017-03-08 10:31:00
2017-03-08 10:32:00
2017-03-08 10:33:00
2017-03-08 10:34:00
2017-03-08 10:35:00
2017-03-08 10:36:00
2017-03-08 10:37:00
2017-03-08 10:38:00
2017-03-08 10:39:00
2017-03-08 10:40:00
2017-03-08 10:41:00
2017-03-08 10:42:00
2017-03-08 10:43:00
2017-03-08 10:44:00
2017-03-08 10:45:00
2017-03-08 10:46:00
2017-03-08 10:47:00
2017-03-08 10:48:00
2017-03-08 10:49:00
2017-03-08 10:50:00
2017-03-08 10:51:00
2017-03-08 10:52:00
2017-03-08 10:53:00
2017-03-08 10:54:00
2017-03-08 10:55:00
2017-03-08 10:56:00
2017-03-08 10:57:00


2017-03-09 10:48:00
2017-03-09 10:49:00
2017-03-09 10:50:00
2017-03-09 10:51:00
2017-03-09 10:52:00
2017-03-09 10:53:00
2017-03-09 10:54:00
2017-03-09 10:55:00
2017-03-09 10:56:00
2017-03-09 10:57:00
2017-03-09 10:58:00
2017-03-09 10:59:00
2017-03-09 11:00:00
2017-03-09 11:01:00
2017-03-09 11:02:00
2017-03-09 11:03:00
2017-03-09 11:04:00
2017-03-09 11:05:00
2017-03-09 11:06:00
2017-03-09 11:07:00
2017-03-09 11:08:00
2017-03-09 11:09:00
2017-03-09 11:10:00
2017-03-09 11:11:00
2017-03-09 11:12:00
2017-03-09 11:13:00
2017-03-09 11:14:00
2017-03-09 11:15:00
2017-03-09 11:16:00
2017-03-09 11:17:00
2017-03-09 11:18:00
2017-03-09 11:19:00
2017-03-09 11:20:00
2017-03-09 11:21:00
2017-03-09 11:22:00
2017-03-09 11:23:00
2017-03-09 11:24:00
2017-03-09 11:25:00
2017-03-09 11:26:00
2017-03-09 11:27:00
2017-03-09 11:28:00
2017-03-09 11:29:00
2017-03-09 11:30:00
2017-03-09 11:31:00
2017-03-09 11:32:00
2017-03-09 11:33:00
2017-03-09 11:34:00
2017-03-09 11:35:00
2017-03-09 11:36:00
2017-03-09 11:37:00


In [8]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
         return ['AGW']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) / 2*mavg30Df.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-25 09:17:00
2017-01-25 09:18:00
2017-01-25 09:19:00
2017-01-25 09:20:00
2017-01-25 09:21:00
2017-01-25 09:22:00
2017-01-25 09:23:00
2017-01-25 09:24:00
2017-01-25 09:25:00
2017-01-25 09:26:00
2017-01-25 09:27:00
2017-01-25 09:28:00
2017-01-25 09:29:00
2017-01-25 09:30:00
2017-01-25 09:31:00
2017-01-25 09:32:00
2017-01-25 09:33:00
2017-01-25 09:34:00
2017-01-25 09:35:00
2017-01-25 09:36:00
2017-01-25 09:37:00
2017-01-25 09:38:00
2017-01-25 09:39:00
2017-01-25 09:40:00
2017-01-25 09:41:00
2017-01-25 09:42:00
2017-01-25 09:43:00
2017-01-25 09:44:00
2017-01-25 09:45:00
2017-01-25 09:46:00
2017-01-25 09:47:00
2017-01-25 09:48:00
2017-01-25 09:49:00
2017-01-25 09:50:00
2017-01-25 09:51:00
2017-01-25 09:52:00
2017-01-25 09:53:00
2017-01-25 09:54:00
2017-01-25 09:55:00
2017-01-25 09:56:00
2017-01-25 09:57:00
2017-01-25 09:58:00

2017-01-26 09:47:00
2017-01-26 09:48:00
2017-01-26 09:49:00
2017-01-26 09:50:00
2017-01-26 09:51:00
2017-01-26 09:52:00
2017-01-26 09:53:00
2017-01-26 09:54:00
2017-01-26 09:55:00
2017-01-26 09:56:00
2017-01-26 09:57:00
2017-01-26 09:58:00
2017-01-26 09:59:00
2017-01-26 10:00:00
2017-01-26 10:01:00
2017-01-26 10:02:00
2017-01-26 10:03:00
2017-01-26 10:04:00
2017-01-26 10:05:00
2017-01-26 10:06:00
2017-01-26 10:07:00
2017-01-26 10:08:00
2017-01-26 10:09:00
2017-01-26 10:10:00
2017-01-26 10:11:00
2017-01-26 10:12:00
2017-01-26 10:13:00
2017-01-26 10:14:00
2017-01-26 10:15:00
2017-01-26 10:16:00
2017-01-26 10:17:00
2017-01-26 10:18:00
2017-01-26 10:19:00
2017-01-26 10:20:00
2017-01-26 10:21:00
2017-01-26 10:22:00
2017-01-26 10:23:00
2017-01-26 10:24:00
2017-01-26 10:25:00
2017-01-26 10:26:00
2017-01-26 10:27:00
2017-01-26 10:28:00
2017-01-26 10:29:00
2017-01-26 10:30:00
2017-01-26 10:31:00
2017-01-26 10:32:00
2017-01-26 10:33:00
2017-01-26 10:34:00
2017-01-26 10:35:00
2017-01-26 10:36:00


2017-01-27 10:20:00
2017-01-27 10:21:00
2017-01-27 10:22:00
2017-01-27 10:23:00
2017-01-27 10:24:00
2017-01-27 10:25:00
2017-01-27 10:26:00
2017-01-27 10:27:00
2017-01-27 10:28:00
2017-01-27 10:29:00
2017-01-27 10:30:00
2017-01-27 10:31:00
2017-01-27 10:32:00
2017-01-27 10:33:00
2017-01-27 10:34:00
2017-01-27 10:35:00
2017-01-27 10:36:00
2017-01-27 10:37:00
2017-01-27 10:38:00
2017-01-27 10:39:00
2017-01-27 10:40:00
2017-01-27 10:41:00
2017-01-27 10:42:00
2017-01-27 10:43:00
2017-01-27 10:44:00
2017-01-27 10:45:00
2017-01-27 10:46:00
2017-01-27 10:47:00
2017-01-27 10:48:00
2017-01-27 10:49:00
2017-01-27 10:50:00
2017-01-27 10:51:00
2017-01-27 10:52:00
2017-01-27 10:53:00
2017-01-27 10:54:00
2017-01-27 10:55:00
2017-01-27 10:56:00
2017-01-27 10:57:00
2017-01-27 10:58:00
2017-01-27 10:59:00
2017-01-27 11:00:00
2017-01-27 11:01:00
2017-01-27 11:02:00
2017-01-27 11:03:00
2017-01-27 11:04:00
2017-01-27 11:05:00
2017-01-27 11:06:00
2017-01-27 11:07:00
2017-01-27 11:08:00
2017-01-27 11:09:00


2017-01-30 11:01:00
2017-01-30 11:02:00
2017-01-30 11:03:00
2017-01-30 11:04:00
2017-01-30 11:05:00
2017-01-30 11:06:00
2017-01-30 11:07:00
2017-01-30 11:08:00
2017-01-30 11:09:00
2017-01-30 11:10:00
2017-01-30 11:11:00
2017-01-30 11:12:00
2017-01-30 11:13:00
2017-01-30 11:14:00
2017-01-30 11:15:00
2017-01-30 11:16:00
2017-01-30 11:17:00
2017-01-30 11:18:00
2017-01-30 11:19:00
2017-01-30 11:20:00
2017-01-30 11:21:00
2017-01-30 11:22:00
2017-01-30 11:23:00
2017-01-30 11:24:00
2017-01-30 11:25:00
2017-01-30 11:26:00
2017-01-30 11:27:00
2017-01-30 11:28:00
2017-01-30 11:29:00
2017-01-30 11:30:00
2017-01-30 11:31:00
2017-01-30 11:32:00
2017-01-30 11:33:00
2017-01-30 11:34:00
2017-01-30 11:35:00
2017-01-30 11:36:00
2017-01-30 11:37:00
2017-01-30 11:38:00
2017-01-30 11:39:00
2017-01-30 11:40:00
2017-01-30 11:41:00
2017-01-30 11:42:00
2017-01-30 11:43:00
2017-01-30 11:44:00
2017-01-30 11:45:00
2017-01-30 11:46:00
2017-01-30 11:47:00
2017-01-30 11:48:00
2017-01-30 11:49:00
2017-01-30 11:50:00


2017-01-31 11:39:00
2017-01-31 11:40:00
2017-01-31 11:41:00
2017-01-31 11:42:00
2017-01-31 11:43:00
2017-01-31 11:44:00
2017-01-31 11:45:00
2017-01-31 11:46:00
2017-01-31 11:47:00
2017-01-31 11:48:00
2017-01-31 11:49:00
2017-01-31 11:50:00
2017-01-31 11:51:00
2017-01-31 11:52:00
2017-01-31 11:53:00
2017-01-31 11:54:00
2017-01-31 11:55:00
2017-01-31 11:56:00
2017-01-31 11:57:00
2017-01-31 11:58:00
2017-01-31 11:59:00
2017-01-31 12:00:00
2017-01-31 12:01:00
2017-01-31 12:02:00
2017-01-31 12:03:00
2017-01-31 12:04:00
2017-01-31 12:05:00
2017-01-31 12:06:00
2017-01-31 12:07:00
2017-01-31 12:08:00
2017-01-31 12:09:00
2017-01-31 12:10:00
2017-01-31 12:11:00
2017-01-31 12:12:00
2017-01-31 12:13:00
2017-01-31 12:14:00
2017-01-31 12:15:00
2017-01-31 12:16:00
2017-01-31 12:17:00
2017-01-31 12:18:00
2017-01-31 12:19:00
2017-01-31 12:20:00
2017-01-31 12:21:00
2017-01-31 12:22:00
2017-01-31 12:23:00
2017-01-31 12:24:00
2017-01-31 12:25:00
2017-01-31 12:26:00
2017-01-31 12:27:00
2017-01-31 12:28:00


...

2017-03-03 12:31:00
2017-03-03 12:32:00
2017-03-03 12:33:00
2017-03-03 12:34:00
2017-03-03 12:35:00
2017-03-03 12:36:00
2017-03-03 12:37:00
2017-03-03 12:38:00
2017-03-03 12:39:00
2017-03-03 12:40:00
2017-03-03 12:41:00
2017-03-03 12:42:00
2017-03-03 12:43:00
2017-03-03 12:44:00
2017-03-03 12:45:00
2017-03-03 12:46:00
2017-03-03 12:47:00
2017-03-03 12:48:00
2017-03-03 12:49:00
2017-03-03 12:50:00
2017-03-03 12:51:00
2017-03-03 12:52:00
2017-03-03 12:53:00
2017-03-03 12:54:00
2017-03-03 12:55:00
2017-03-03 12:56:00
2017-03-03 12:57:00
2017-03-03 12:58:00
2017-03-03 12:59:00
2017-03-03 13:00:00
2017-03-03 13:01:00
2017-03-03 13:02:00
2017-03-03 13:03:00
2017-03-03 13:04:00
2017-03-03 13:05:00
2017-03-03 13:06:00
2017-03-03 13:07:00
2017-03-03 13:08:00
2017-03-03 13:09:00
2017-03-03 13:10:00
2017-03-03 13:11:00
2017-03-03 13:12:00
2017-03-03 13:13:00
2017-03-03 13:14:00
2017-03-03 13:15:00
2017-03-03 13:16:00
2017-03-03 13:17:00
2017-03-03 13:18:00
2017-03-03 13:19:00
2017-03-03 13:20:00


2017-03-06 13:10:00
2017-03-06 13:11:00
2017-03-06 13:12:00
2017-03-06 13:13:00
2017-03-06 13:14:00
2017-03-06 13:15:00
2017-03-06 13:16:00
2017-03-06 13:17:00
2017-03-06 13:18:00
2017-03-06 13:19:00
2017-03-06 13:20:00
2017-03-06 13:21:00
2017-03-06 13:22:00
2017-03-06 13:23:00
2017-03-06 13:24:00
2017-03-06 13:25:00
2017-03-06 13:26:00
2017-03-06 13:27:00
2017-03-06 13:28:00
2017-03-06 13:29:00
2017-03-06 13:30:00
2017-03-06 13:31:00
2017-03-06 13:32:00
2017-03-06 13:33:00
2017-03-06 13:34:00
2017-03-06 13:35:00
2017-03-06 13:36:00
2017-03-06 13:37:00
2017-03-06 13:38:00
2017-03-06 13:39:00
2017-03-06 13:40:00
2017-03-06 13:41:00
2017-03-06 13:42:00
2017-03-06 13:43:00
2017-03-06 13:44:00
2017-03-06 13:45:00
2017-03-06 13:46:00
2017-03-06 13:47:00
2017-03-06 13:48:00
2017-03-06 13:49:00
2017-03-06 13:50:00
2017-03-06 13:51:00
2017-03-06 13:52:00
2017-03-06 13:53:00
2017-03-06 13:54:00
2017-03-06 13:55:00
2017-03-06 13:56:00
2017-03-06 13:57:00
2017-03-06 13:58:00
2017-03-06 13:59:00


2017-03-07 13:50:00
2017-03-07 13:51:00
2017-03-07 13:52:00
2017-03-07 13:53:00
2017-03-07 13:54:00
2017-03-07 13:55:00
2017-03-07 13:56:00
2017-03-07 13:57:00
2017-03-07 13:58:00
2017-03-07 13:59:00
2017-03-07 14:00:00
2017-03-07 14:01:00
2017-03-07 14:02:00
2017-03-07 14:03:00
2017-03-07 14:04:00
2017-03-07 14:05:00
2017-03-07 14:06:00
2017-03-07 14:07:00
2017-03-07 14:08:00
2017-03-07 14:09:00
2017-03-07 14:10:00
2017-03-07 14:11:00
2017-03-07 14:12:00
2017-03-07 14:13:00
2017-03-07 14:14:00
2017-03-07 14:15:00
2017-03-07 14:16:00
2017-03-07 14:17:00
2017-03-07 14:18:00
2017-03-07 14:19:00
2017-03-07 14:20:00
2017-03-07 14:21:00
2017-03-07 14:22:00
2017-03-07 14:23:00
2017-03-07 14:24:00
2017-03-07 14:25:00
2017-03-07 14:26:00
2017-03-07 14:27:00
2017-03-07 14:28:00
2017-03-07 14:29:00
2017-03-07 14:30:00
2017-03-07 14:31:00
2017-03-07 14:32:00
2017-03-07 14:33:00
2017-03-07 14:34:00
2017-03-07 14:35:00
2017-03-07 14:36:00
2017-03-07 14:37:00
2017-03-07 14:38:00
2017-03-07 14:39:00


2017-03-08 13:49:00
2017-03-08 13:50:00
2017-03-08 13:51:00
2017-03-08 13:52:00
2017-03-08 13:53:00
2017-03-08 13:54:00
2017-03-08 13:55:00
2017-03-08 13:56:00
2017-03-08 13:57:00
2017-03-08 13:58:00
2017-03-08 13:59:00
2017-03-08 14:00:00
2017-03-08 14:01:00
2017-03-08 14:02:00
2017-03-08 14:03:00
2017-03-08 14:04:00
2017-03-08 14:05:00
2017-03-08 14:06:00
2017-03-08 14:07:00
2017-03-08 14:08:00
2017-03-08 14:09:00
2017-03-08 14:10:00
2017-03-08 14:11:00
2017-03-08 14:12:00
2017-03-08 14:13:00
2017-03-08 14:14:00
2017-03-08 14:15:00
2017-03-08 14:16:00
2017-03-08 14:17:00
2017-03-08 14:18:00
2017-03-08 14:19:00
2017-03-08 14:20:00
2017-03-08 14:21:00
2017-03-08 14:22:00
2017-03-08 14:23:00
2017-03-08 14:24:00
2017-03-08 14:25:00
2017-03-08 14:26:00
2017-03-08 14:27:00
2017-03-08 14:28:00
2017-03-08 14:29:00
2017-03-08 14:30:00
2017-03-08 14:31:00
2017-03-08 14:32:00
2017-03-08 14:33:00
2017-03-08 14:34:00
2017-03-08 14:35:00
2017-03-08 14:36:00
2017-03-08 14:37:00
2017-03-08 14:38:00


2017-03-09 14:28:00
2017-03-09 14:29:00
2017-03-09 14:30:00
2017-03-09 14:31:00
2017-03-09 14:32:00
2017-03-09 14:33:00
2017-03-09 14:34:00
2017-03-09 14:35:00
2017-03-09 14:36:00
2017-03-09 14:37:00
2017-03-09 14:38:00
2017-03-09 14:39:00
2017-03-09 14:40:00
2017-03-09 14:41:00
2017-03-09 14:42:00
2017-03-09 14:43:00
2017-03-09 14:44:00
2017-03-09 14:45:00
2017-03-09 14:46:00
2017-03-09 14:47:00
2017-03-09 14:48:00
2017-03-09 14:49:00
2017-03-09 14:50:00
2017-03-09 14:51:00
2017-03-09 14:52:00
2017-03-09 14:53:00
2017-03-09 14:54:00
2017-03-09 14:55:00
2017-03-09 14:56:00
2017-03-09 14:57:00
2017-03-09 14:58:00
2017-03-09 14:59:00
2017-03-09 15:00:00
2017-03-09 15:01:00
2017-03-09 15:02:00
2017-03-09 15:03:00
2017-03-09 15:04:00
2017-03-09 15:05:00
2017-03-09 15:06:00
2017-03-09 15:07:00
2017-03-09 15:08:00
2017-03-09 15:09:00
2017-03-09 15:10:00
2017-03-09 15:11:00
2017-03-09 15:12:00
2017-03-09 15:13:00
2017-03-09 15:14:00
2017-03-09 15:15:00
2017-03-09 15:16:00
2017-03-09 15:17:00


In [32]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
         return ['AGW']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) / sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-25 09:17:00
2017-01-25 09:18:00
2017-01-25 09:19:00
2017-01-25 09:20:00
2017-01-25 09:21:00
2017-01-25 09:22:00
2017-01-25 09:23:00
2017-01-25 09:24:00
2017-01-25 09:25:00
2017-01-25 09:26:00
2017-01-25 09:27:00
2017-01-25 09:28:00
2017-01-25 09:29:00
2017-01-25 09:30:00
2017-01-25 09:31:00
2017-01-25 09:32:00
2017-01-25 09:33:00
2017-01-25 09:34:00
2017-01-25 09:35:00
2017-01-25 09:36:00
2017-01-25 09:37:00
2017-01-25 09:38:00
2017-01-25 09:39:00
2017-01-25 09:40:00
2017-01-25 09:41:00
2017-01-25 09:42:00
2017-01-25 09:43:00
2017-01-25 09:44:00
2017-01-25 09:45:00
2017-01-25 09:46:00
2017-01-25 09:47:00
2017-01-25 09:48:00
2017-01-25 09:49:00
2017-01-25 09:50:00
2017-01-25 09:51:00
2017-01-25 09:52:00
2017-01-25 09:53:00
2017-01-25 09:54:00
2017-01-25 09:55:00
2017-01-25 09:56:00
2017-01-25 09:57:00
2017-01-25 09:58:00

2017-01-25 13:48:00
2017-01-25 13:49:00
2017-01-25 13:50:00
2017-01-25 13:51:00
2017-01-25 13:52:00
2017-01-25 13:53:00
2017-01-25 13:54:00
2017-01-25 13:55:00
2017-01-25 13:56:00
2017-01-25 13:57:00
2017-01-25 13:58:00
2017-01-25 13:59:00
2017-01-25 14:00:00
2017-01-25 14:01:00
2017-01-25 14:02:00
2017-01-25 14:03:00
2017-01-25 14:04:00
2017-01-25 14:05:00
2017-01-25 14:06:00
2017-01-25 14:07:00
2017-01-25 14:08:00
2017-01-25 14:09:00
2017-01-25 14:10:00
2017-01-25 14:11:00
2017-01-25 14:12:00
2017-01-25 14:13:00
2017-01-25 14:14:00
2017-01-25 14:15:00
2017-01-25 14:16:00
2017-01-25 14:17:00
2017-01-25 14:18:00
2017-01-25 14:19:00
2017-01-25 14:20:00
2017-01-25 14:21:00
2017-01-25 14:22:00
2017-01-25 14:23:00
2017-01-25 14:24:00
2017-01-25 14:25:00
2017-01-25 14:26:00
2017-01-25 14:27:00
2017-01-25 14:28:00
2017-01-25 14:29:00
2017-01-25 14:30:00
2017-01-25 14:31:00
2017-01-25 14:32:00
2017-01-25 14:33:00
2017-01-25 14:34:00
2017-01-25 14:35:00
2017-01-25 14:36:00
2017-01-25 14:37:00


Warn: Not Enough Capital
2017-01-26 12:58:00
Warn: Not Enough Capital
2017-01-26 12:59:00
Warn: Not Enough Capital
2017-01-26 13:00:00
Warn: Not Enough Capital
2017-01-26 13:01:00
Warn: Not Enough Capital
2017-01-26 13:02:00
Warn: Not Enough Capital
2017-01-26 13:03:00
Warn: Not Enough Capital
2017-01-26 13:04:00
Warn: Not Enough Capital
2017-01-26 13:05:00
Warn: Not Enough Capital
2017-01-26 13:06:00
Warn: Not Enough Capital
2017-01-26 13:07:00
Warn: Not Enough Capital
2017-01-26 13:08:00
Warn: Not Enough Capital
2017-01-26 13:09:00
Warn: Not Enough Capital
2017-01-26 13:10:00
Warn: Not Enough Capital
2017-01-26 13:11:00
Warn: Not Enough Capital
2017-01-26 13:12:00
Warn: Not Enough Capital
2017-01-26 13:13:00
Warn: Not Enough Capital
2017-01-26 13:14:00
Warn: Not Enough Capital
2017-01-26 13:15:00
Warn: Not Enough Capital
2017-01-26 13:16:00
Warn: Not Enough Capital
2017-01-26 13:17:00
Warn: Not Enough Capital
2017-01-26 13:18:00
Warn: Not Enough Capital
2017-01-26 13:19:00
Warn: Not 

2017-01-27 11:38:00
2017-01-27 11:39:00
2017-01-27 11:40:00
2017-01-27 11:41:00
2017-01-27 11:42:00
2017-01-27 11:43:00
2017-01-27 11:44:00
2017-01-27 11:45:00
2017-01-27 11:46:00
2017-01-27 11:47:00
2017-01-27 11:48:00
2017-01-27 11:49:00
2017-01-27 11:50:00
2017-01-27 11:51:00
2017-01-27 11:52:00
2017-01-27 11:53:00
2017-01-27 11:54:00
2017-01-27 11:55:00
2017-01-27 11:56:00
2017-01-27 11:57:00
2017-01-27 11:58:00
2017-01-27 11:59:00
2017-01-27 12:00:00
2017-01-27 12:01:00
2017-01-27 12:02:00
2017-01-27 12:03:00
2017-01-27 12:04:00
2017-01-27 12:05:00
2017-01-27 12:06:00
2017-01-27 12:07:00
2017-01-27 12:08:00
2017-01-27 12:09:00
2017-01-27 12:10:00
2017-01-27 12:11:00
2017-01-27 12:12:00
2017-01-27 12:13:00
2017-01-27 12:14:00
2017-01-27 12:15:00
Warn: Not Enough Capital
2017-01-27 12:16:00
Warn: Not Enough Capital
2017-01-27 12:17:00
Warn: Not Enough Capital
2017-01-27 12:18:00
Warn: Not Enough Capital
2017-01-27 12:19:00
Warn: Not Enough Capital
2017-01-27 12:20:00
Warn: Not Enoug

2017-01-30 11:07:00
2017-01-30 11:08:00
2017-01-30 11:09:00
2017-01-30 11:10:00
2017-01-30 11:11:00
2017-01-30 11:12:00
2017-01-30 11:13:00
2017-01-30 11:14:00
2017-01-30 11:15:00
2017-01-30 11:16:00
2017-01-30 11:17:00
2017-01-30 11:18:00
2017-01-30 11:19:00
2017-01-30 11:20:00
2017-01-30 11:21:00
2017-01-30 11:22:00
2017-01-30 11:23:00
2017-01-30 11:24:00
2017-01-30 11:25:00
2017-01-30 11:26:00
2017-01-30 11:27:00
2017-01-30 11:28:00
2017-01-30 11:29:00
2017-01-30 11:30:00
Warn: Not Enough Capital
2017-01-30 11:31:00
Warn: Not Enough Capital
2017-01-30 11:32:00
Warn: Not Enough Capital
2017-01-30 11:33:00
Warn: Not Enough Capital
2017-01-30 11:34:00
Warn: Not Enough Capital
2017-01-30 11:35:00
Warn: Not Enough Capital
2017-01-30 11:36:00
Warn: Not Enough Capital
2017-01-30 11:37:00
Warn: Not Enough Capital
2017-01-30 11:38:00
Warn: Not Enough Capital
2017-01-30 11:39:00
Warn: Not Enough Capital
2017-01-30 11:40:00
Warn: Not Enough Capital
2017-01-30 11:41:00
Warn: Not Enough Capital


...

2017-03-03 11:11:00
2017-03-03 11:12:00
2017-03-03 11:13:00
2017-03-03 11:14:00
2017-03-03 11:15:00
2017-03-03 11:16:00
2017-03-03 11:17:00
2017-03-03 11:18:00
2017-03-03 11:19:00
2017-03-03 11:20:00
2017-03-03 11:21:00
2017-03-03 11:22:00
2017-03-03 11:23:00
2017-03-03 11:24:00
2017-03-03 11:25:00
2017-03-03 11:26:00
2017-03-03 11:27:00
2017-03-03 11:28:00
2017-03-03 11:29:00
2017-03-03 11:30:00
2017-03-03 11:31:00
2017-03-03 11:32:00
2017-03-03 11:33:00
2017-03-03 11:34:00
2017-03-03 11:35:00
2017-03-03 11:36:00
2017-03-03 11:37:00
2017-03-03 11:38:00
2017-03-03 11:39:00
Warn: Not Enough Capital
2017-03-03 11:40:00
Warn: Not Enough Capital
2017-03-03 11:41:00
Warn: Not Enough Capital
2017-03-03 11:42:00
Warn: Not Enough Capital
2017-03-03 11:43:00
Warn: Not Enough Capital
2017-03-03 11:44:00
Warn: Not Enough Capital
2017-03-03 11:45:00
Warn: Not Enough Capital
2017-03-03 11:46:00
Warn: Not Enough Capital
2017-03-03 11:47:00
Warn: Not Enough Capital
2017-03-03 11:48:00
Warn: Not Enoug

2017-03-06 14:49:00
2017-03-06 14:50:00
2017-03-06 14:51:00
2017-03-06 14:52:00
2017-03-06 14:53:00
2017-03-06 14:54:00
2017-03-06 14:55:00
2017-03-06 14:56:00
2017-03-06 14:57:00
2017-03-06 14:58:00
2017-03-06 14:59:00
2017-03-06 15:00:00
2017-03-06 15:01:00
2017-03-06 15:02:00
2017-03-06 15:03:00
2017-03-06 15:04:00
2017-03-06 15:05:00
2017-03-06 15:06:00
2017-03-06 15:07:00
2017-03-06 15:08:00
2017-03-06 15:09:00
2017-03-06 15:10:00
Warn: Not Enough Capital
2017-03-06 15:11:00
Warn: Not Enough Capital
2017-03-06 15:12:00
2017-03-06 15:13:00
2017-03-06 15:14:00
2017-03-06 15:15:00
2017-03-06 15:16:00
2017-03-06 15:17:00
2017-03-06 15:18:00
2017-03-06 15:19:00
2017-03-06 15:20:00
2017-03-06 15:21:00
2017-03-06 15:22:00
2017-03-06 15:23:00
2017-03-06 15:24:00
2017-03-06 15:25:00
2017-03-06 15:26:00
2017-03-06 15:27:00
2017-03-06 15:28:00
2017-03-07 09:17:00
2017-03-07 09:18:00
2017-03-07 09:19:00
2017-03-07 09:20:00
2017-03-07 09:21:00
2017-03-07 09:22:00
2017-03-07 09:23:00
2017-03-07

Warn: Not Enough Capital
2017-03-07 13:47:00
Warn: Not Enough Capital
2017-03-07 13:48:00
Warn: Not Enough Capital
2017-03-07 13:49:00
Warn: Not Enough Capital
2017-03-07 13:50:00
Warn: Not Enough Capital
2017-03-07 13:51:00
Warn: Not Enough Capital
2017-03-07 13:52:00
Warn: Not Enough Capital
2017-03-07 13:53:00
Warn: Not Enough Capital
2017-03-07 13:54:00
Warn: Not Enough Capital
2017-03-07 13:55:00
Warn: Not Enough Capital
2017-03-07 13:56:00
Warn: Not Enough Capital
2017-03-07 13:57:00
Warn: Not Enough Capital
2017-03-07 13:58:00
Warn: Not Enough Capital
2017-03-07 13:59:00
Warn: Not Enough Capital
2017-03-07 14:00:00
Warn: Not Enough Capital
2017-03-07 14:01:00
Warn: Not Enough Capital
2017-03-07 14:02:00
Warn: Not Enough Capital
2017-03-07 14:03:00
Warn: Not Enough Capital
2017-03-07 14:04:00
Warn: Not Enough Capital
2017-03-07 14:05:00
Warn: Not Enough Capital
2017-03-07 14:06:00
Warn: Not Enough Capital
2017-03-07 14:07:00
Warn: Not Enough Capital
2017-03-07 14:08:00
Warn: Not 

2017-03-08 13:01:00
2017-03-08 13:02:00
2017-03-08 13:03:00
2017-03-08 13:04:00
2017-03-08 13:05:00
2017-03-08 13:06:00
2017-03-08 13:07:00
2017-03-08 13:08:00
2017-03-08 13:09:00
2017-03-08 13:10:00
2017-03-08 13:11:00
2017-03-08 13:12:00
2017-03-08 13:13:00
2017-03-08 13:14:00
2017-03-08 13:15:00
2017-03-08 13:16:00
2017-03-08 13:17:00
2017-03-08 13:18:00
2017-03-08 13:19:00
2017-03-08 13:20:00
2017-03-08 13:21:00
2017-03-08 13:22:00
2017-03-08 13:23:00
2017-03-08 13:24:00
Warn: Not Enough Capital
2017-03-08 13:25:00
Warn: Not Enough Capital
2017-03-08 13:26:00
2017-03-08 13:27:00
2017-03-08 13:28:00
2017-03-08 13:29:00
2017-03-08 13:30:00
2017-03-08 13:31:00
2017-03-08 13:32:00
2017-03-08 13:33:00
2017-03-08 13:34:00
2017-03-08 13:35:00
2017-03-08 13:36:00
2017-03-08 13:37:00
2017-03-08 13:38:00
2017-03-08 13:39:00
2017-03-08 13:40:00
2017-03-08 13:41:00
2017-03-08 13:42:00
2017-03-08 13:43:00
2017-03-08 13:44:00
2017-03-08 13:45:00
2017-03-08 13:46:00
2017-03-08 13:47:00
2017-03-08

2017-03-09 11:46:00
2017-03-09 11:47:00
2017-03-09 11:48:00
2017-03-09 11:49:00
2017-03-09 11:50:00
2017-03-09 11:51:00
2017-03-09 11:52:00
2017-03-09 11:53:00
2017-03-09 11:54:00
Warn: Not Enough Capital
2017-03-09 11:55:00
Warn: Not Enough Capital
2017-03-09 11:56:00
Warn: Not Enough Capital
2017-03-09 11:57:00
Warn: Not Enough Capital
2017-03-09 11:58:00
Warn: Not Enough Capital
2017-03-09 11:59:00
Warn: Not Enough Capital
2017-03-09 12:00:00
Warn: Not Enough Capital
2017-03-09 12:01:00
Warn: Not Enough Capital
2017-03-09 12:02:00
Warn: Not Enough Capital
2017-03-09 12:03:00
Warn: Not Enough Capital
2017-03-09 12:04:00
Warn: Not Enough Capital
2017-03-09 12:05:00
Warn: Not Enough Capital
2017-03-09 12:06:00
Warn: Not Enough Capital
2017-03-09 12:07:00
Warn: Not Enough Capital
2017-03-09 12:08:00
Warn: Not Enough Capital
2017-03-09 12:09:00
Warn: Not Enough Capital
2017-03-09 12:10:00
Warn: Not Enough Capital
2017-03-09 12:11:00
Warn: Not Enough Capital
2017-03-09 12:12:00
2017-03-09

In [33]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
         return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) / sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: VKE
Processing data for stock: UWC
Processing data for stock: HDK
Processing data for stock: IWU
Processing data for stock: IYU
Processing data for stock: HZT
Processing data for stock: TGI
Processing data for stock: AUZ
Processing data for stock: JSG
Processing data for stock: OMP
Processing data for stock: CYD
Processing data for stock: CHV
Processing data for stock: UBF
Processing data for stock: DCO
Processing data for stock: DVV
Processing data for stock: WUT
Processing data for stock: FKI
Processing data for stock: FFS
Processing data for stock: AIO
Processing data for stock: MQK
Processing data for stock: GGK
Processing data for stock: KFW
Processing data for stock: JYW
Processing data for stock: PLX
Processing data for stock: QVE
Processing data for stock: BLR
Processing data for stock: OGU
Processing data for stock: BSN
Processing data for stock: VML
Processing data for stock: KKG
Processing data for stock: VND
Processing data for stock: NDG
Processi

Warn: Not Enough Capital
2017-01-25 13:10:00
Warn: Not Enough Capital
2017-01-25 13:11:00
Warn: Not Enough Capital
2017-01-25 13:12:00
Warn: Not Enough Capital
2017-01-25 13:13:00
Warn: Not Enough Capital
2017-01-25 13:14:00
Warn: Not Enough Capital
2017-01-25 13:15:00
Warn: Not Enough Capital
2017-01-25 13:16:00
Warn: Not Enough Capital
2017-01-25 13:17:00
Warn: Not Enough Capital
2017-01-25 13:18:00
2017-01-25 13:19:00
2017-01-25 13:20:00
2017-01-25 13:21:00
2017-01-25 13:22:00
2017-01-25 13:23:00
2017-01-25 13:24:00
2017-01-25 13:25:00
2017-01-25 13:26:00
2017-01-25 13:27:00
2017-01-25 13:28:00
2017-01-25 13:29:00
2017-01-25 13:30:00
2017-01-25 13:31:00
2017-01-25 13:32:00
2017-01-25 13:33:00
2017-01-25 13:34:00
2017-01-25 13:35:00
2017-01-25 13:36:00
2017-01-25 13:37:00
2017-01-25 13:38:00
2017-01-25 13:39:00
2017-01-25 13:40:00
2017-01-25 13:41:00
2017-01-25 13:42:00
2017-01-25 13:43:00
2017-01-25 13:44:00
2017-01-25 13:45:00
2017-01-25 13:46:00
2017-01-25 13:47:00
2017-01-25 13:4

Warn: Not Enough Capital
2017-01-26 12:47:00
Warn: Not Enough Capital
2017-01-26 12:48:00
Warn: Not Enough Capital
2017-01-26 12:49:00
2017-01-26 12:50:00
2017-01-26 12:51:00
2017-01-26 12:52:00
2017-01-26 12:53:00
2017-01-26 12:54:00
Warn: Not Enough Capital
2017-01-26 12:55:00
Warn: Not Enough Capital
2017-01-26 12:56:00
2017-01-26 12:57:00
2017-01-26 12:58:00
2017-01-26 12:59:00
2017-01-26 13:00:00
2017-01-26 13:01:00
2017-01-26 13:02:00
2017-01-26 13:03:00
2017-01-26 13:04:00
2017-01-26 13:05:00
2017-01-26 13:06:00
2017-01-26 13:07:00
2017-01-26 13:08:00
2017-01-26 13:09:00
2017-01-26 13:10:00
Warn: Not Enough Capital
2017-01-26 13:11:00
Warn: Not Enough Capital
2017-01-26 13:12:00
Warn: Not Enough Capital
2017-01-26 13:13:00
Warn: Not Enough Capital
2017-01-26 13:14:00
Warn: Not Enough Capital
2017-01-26 13:15:00
Warn: Not Enough Capital
2017-01-26 13:16:00
2017-01-26 13:17:00
2017-01-26 13:18:00
2017-01-26 13:19:00
2017-01-26 13:20:00
2017-01-26 13:21:00
2017-01-26 13:22:00
2017-

2017-01-27 12:00:00
2017-01-27 12:01:00
2017-01-27 12:02:00
2017-01-27 12:03:00
2017-01-27 12:04:00
2017-01-27 12:05:00
2017-01-27 12:06:00
2017-01-27 12:07:00
2017-01-27 12:08:00
2017-01-27 12:09:00
2017-01-27 12:10:00
2017-01-27 12:11:00
Warn: Not Enough Capital
2017-01-27 12:12:00
Warn: Not Enough Capital
2017-01-27 12:13:00
Warn: Not Enough Capital
2017-01-27 12:14:00
Warn: Not Enough Capital
2017-01-27 12:15:00
Warn: Not Enough Capital
2017-01-27 12:16:00
Warn: Not Enough Capital
2017-01-27 12:17:00
Warn: Not Enough Capital
2017-01-27 12:18:00
Warn: Not Enough Capital
2017-01-27 12:19:00
Warn: Not Enough Capital
2017-01-27 12:20:00
Warn: Not Enough Capital
2017-01-27 12:21:00
Warn: Not Enough Capital
2017-01-27 12:22:00
Warn: Not Enough Capital
2017-01-27 12:23:00
Warn: Not Enough Capital
2017-01-27 12:24:00
2017-01-27 12:25:00
2017-01-27 12:26:00
2017-01-27 12:27:00
2017-01-27 12:28:00
2017-01-27 12:29:00
2017-01-27 12:30:00
2017-01-27 12:31:00
2017-01-27 12:32:00
2017-01-27 12:3

Warn: Not Enough Capital
2017-01-30 11:48:00
Warn: Not Enough Capital
2017-01-30 11:49:00
Warn: Not Enough Capital
2017-01-30 11:50:00
Warn: Not Enough Capital
2017-01-30 11:51:00
Warn: Not Enough Capital
2017-01-30 11:52:00
2017-01-30 11:53:00
2017-01-30 11:54:00
2017-01-30 11:55:00
2017-01-30 11:56:00
2017-01-30 11:57:00
2017-01-30 11:58:00
2017-01-30 11:59:00
2017-01-30 12:00:00
2017-01-30 12:01:00
2017-01-30 12:02:00
2017-01-30 12:03:00
2017-01-30 12:04:00
2017-01-30 12:05:00
2017-01-30 12:06:00
2017-01-30 12:07:00
2017-01-30 12:08:00
2017-01-30 12:09:00
2017-01-30 12:10:00
2017-01-30 12:11:00
2017-01-30 12:12:00
2017-01-30 12:13:00
2017-01-30 12:14:00
2017-01-30 12:15:00
2017-01-30 12:16:00
2017-01-30 12:17:00
2017-01-30 12:18:00
2017-01-30 12:19:00
2017-01-30 12:20:00
2017-01-30 12:21:00
2017-01-30 12:22:00
2017-01-30 12:23:00
2017-01-30 12:24:00
2017-01-30 12:25:00
2017-01-30 12:26:00
2017-01-30 12:27:00
2017-01-30 12:28:00
2017-01-30 12:29:00
2017-01-30 12:30:00
2017-01-30 12:3

...

Warn: Not Enough Capital
2017-03-06 12:11:00
Warn: Not Enough Capital
2017-03-06 12:12:00
Warn: Not Enough Capital
2017-03-06 12:13:00
Warn: Not Enough Capital
2017-03-06 12:14:00
Warn: Not Enough Capital
2017-03-06 12:15:00
Warn: Not Enough Capital
2017-03-06 12:16:00
Warn: Not Enough Capital
2017-03-06 12:17:00
Warn: Not Enough Capital
2017-03-06 12:18:00
Warn: Not Enough Capital
2017-03-06 12:19:00
Warn: Not Enough Capital
2017-03-06 12:20:00
Warn: Not Enough Capital
2017-03-06 12:21:00
Warn: Not Enough Capital
2017-03-06 12:22:00
Warn: Not Enough Capital
2017-03-06 12:23:00
2017-03-06 12:24:00
2017-03-06 12:25:00
2017-03-06 12:26:00
2017-03-06 12:27:00
2017-03-06 12:28:00
2017-03-06 12:29:00
2017-03-06 12:30:00
2017-03-06 12:31:00
2017-03-06 12:32:00
2017-03-06 12:33:00
2017-03-06 12:34:00
2017-03-06 12:35:00
2017-03-06 12:36:00
2017-03-06 12:37:00
2017-03-06 12:38:00
2017-03-06 12:39:00
2017-03-06 12:40:00
2017-03-06 12:41:00
2017-03-06 12:42:00
2017-03-06 12:43:00
2017-03-06 12:4

Warn: Not Enough Capital
2017-03-07 11:45:00
Warn: Not Enough Capital
2017-03-07 11:46:00
Warn: Not Enough Capital
2017-03-07 11:47:00
Warn: Not Enough Capital
2017-03-07 11:48:00
Warn: Not Enough Capital
2017-03-07 11:49:00
Warn: Not Enough Capital
2017-03-07 11:50:00
Warn: Not Enough Capital
2017-03-07 11:51:00
Warn: Not Enough Capital
2017-03-07 11:52:00
Warn: Not Enough Capital
2017-03-07 11:53:00
Warn: Not Enough Capital
2017-03-07 11:54:00
Warn: Not Enough Capital
2017-03-07 11:55:00
Warn: Not Enough Capital
2017-03-07 11:56:00
2017-03-07 11:57:00
2017-03-07 11:58:00
2017-03-07 11:59:00
2017-03-07 12:00:00
2017-03-07 12:01:00
2017-03-07 12:02:00
2017-03-07 12:03:00
2017-03-07 12:04:00
2017-03-07 12:05:00
2017-03-07 12:06:00
2017-03-07 12:07:00
2017-03-07 12:08:00
2017-03-07 12:09:00
2017-03-07 12:10:00
2017-03-07 12:11:00
2017-03-07 12:12:00
2017-03-07 12:13:00
2017-03-07 12:14:00
2017-03-07 12:15:00
2017-03-07 12:16:00
2017-03-07 12:17:00
2017-03-07 12:18:00
2017-03-07 12:19:00


2017-03-08 11:31:00
2017-03-08 11:32:00
2017-03-08 11:33:00
2017-03-08 11:34:00
2017-03-08 11:35:00
2017-03-08 11:36:00
2017-03-08 11:37:00
2017-03-08 11:38:00
2017-03-08 11:39:00
2017-03-08 11:40:00
2017-03-08 11:41:00
2017-03-08 11:42:00
2017-03-08 11:43:00
2017-03-08 11:44:00
2017-03-08 11:45:00
2017-03-08 11:46:00
2017-03-08 11:47:00
2017-03-08 11:48:00
2017-03-08 11:49:00
2017-03-08 11:50:00
2017-03-08 11:51:00
2017-03-08 11:52:00
2017-03-08 11:53:00
Warn: Not Enough Capital
2017-03-08 11:54:00
Warn: Not Enough Capital
2017-03-08 11:55:00
Warn: Not Enough Capital
2017-03-08 11:56:00
2017-03-08 11:57:00
2017-03-08 11:58:00
2017-03-08 11:59:00
2017-03-08 12:00:00
2017-03-08 12:01:00
2017-03-08 12:02:00
2017-03-08 12:03:00
2017-03-08 12:04:00
2017-03-08 12:05:00
2017-03-08 12:06:00
2017-03-08 12:07:00
2017-03-08 12:08:00
2017-03-08 12:09:00
2017-03-08 12:10:00
2017-03-08 12:11:00
2017-03-08 12:12:00
2017-03-08 12:13:00
2017-03-08 12:14:00
2017-03-08 12:15:00
2017-03-08 12:16:00
2017-

2017-03-09 11:16:00
2017-03-09 11:17:00
2017-03-09 11:18:00
2017-03-09 11:19:00
2017-03-09 11:20:00
2017-03-09 11:21:00
2017-03-09 11:22:00
2017-03-09 11:23:00
2017-03-09 11:24:00
2017-03-09 11:25:00
2017-03-09 11:26:00
2017-03-09 11:27:00
2017-03-09 11:28:00
2017-03-09 11:29:00
2017-03-09 11:30:00
2017-03-09 11:31:00
2017-03-09 11:32:00
2017-03-09 11:33:00
2017-03-09 11:34:00
2017-03-09 11:35:00
2017-03-09 11:36:00
2017-03-09 11:37:00
2017-03-09 11:38:00
2017-03-09 11:39:00
2017-03-09 11:40:00
2017-03-09 11:41:00
2017-03-09 11:42:00
2017-03-09 11:43:00
2017-03-09 11:44:00
2017-03-09 11:45:00
2017-03-09 11:46:00
2017-03-09 11:47:00
2017-03-09 11:48:00
2017-03-09 11:49:00
2017-03-09 11:50:00
2017-03-09 11:51:00
2017-03-09 11:52:00
2017-03-09 11:53:00
2017-03-09 11:54:00
2017-03-09 11:55:00
2017-03-09 11:56:00
2017-03-09 11:57:00
2017-03-09 11:58:00
2017-03-09 11:59:00
2017-03-09 12:00:00
2017-03-09 12:01:00
2017-03-09 12:02:00
2017-03-09 12:03:00
2017-03-09 12:04:00
2017-03-09 12:05:00


Info: IFL:  Total Pnl: 0.26%  Profit/Loss Ratio: 1.02  Accuracy: 0.47  Score: nan 
Info: HDK:  Total Pnl: -0.27%  Profit/Loss Ratio: 0.70  Accuracy: 0.33  Score: nan 
Info: ZLX:  Total Pnl: -0.11%  Profit/Loss Ratio: 0.94  Accuracy: 0.43  Score: nan 
Info: QVE:  Total Pnl: -0.23%  Profit/Loss Ratio: 0.79  Accuracy: 0.34  Score: nan 
Info: IUE:  Total Pnl: -0.34%  Profit/Loss Ratio: 0.88  Accuracy: 0.45  Score: nan 
Info: LDU:  Total Pnl: -0.17%  Profit/Loss Ratio: 0.98  Accuracy: 0.48  Score: nan 
Info: ROP:  Total Pnl: -0.35%  Profit/Loss Ratio: 0.97  Accuracy: 0.49  Score: nan 
Info: BLR:  Total Pnl: -0.23%  Profit/Loss Ratio: 0.83  Accuracy: 0.41  Score: nan 
Info: XCS:  Total Pnl: -0.38%  Profit/Loss Ratio: 0.83  Accuracy: 0.44  Score: nan 
Info: CBT:  Total Pnl: 0.01%  Profit/Loss Ratio: 1.00  Accuracy: 0.47  Score: nan 
Info: UWC:  Total Pnl: 0.22%  Profit/Loss Ratio: 1.02  Accuracy: 0.49  Score: nan 
Info: KKG:  Total Pnl: -0.26%  Profit/Loss Ratio: 0.81  Accuracy: 0.38  Score: 

In [34]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['AGW']
#          return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-25 09:17:00
2017-01-25 09:18:00
2017-01-25 09:19:00
2017-01-25 09:20:00
2017-01-25 09:21:00
2017-01-25 09:22:00
2017-01-25 09:23:00
2017-01-25 09:24:00
2017-01-25 09:25:00
2017-01-25 09:26:00
2017-01-25 09:27:00
2017-01-25 09:28:00
2017-01-25 09:29:00
2017-01-25 09:30:00
2017-01-25 09:31:00
2017-01-25 09:32:00
2017-01-25 09:33:00
2017-01-25 09:34:00
2017-01-25 09:35:00
2017-01-25 09:36:00
2017-01-25 09:37:00
2017-01-25 09:38:00
2017-01-25 09:39:00
2017-01-25 09:40:00
2017-01-25 09:41:00
2017-01-25 09:42:00
2017-01-25 09:43:00
2017-01-25 09:44:00
2017-01-25 09:45:00
2017-01-25 09:46:00
2017-01-25 09:47:00
2017-01-25 09:48:00
2017-01-25 09:49:00
2017-01-25 09:50:00
2017-01-25 09:51:00
2017-01-25 09:52:00
2017-01-25 09:53:00
2017-01-25 09:54:00
2017-01-25 09:55:00
2017-01-25 09:56:00
2017-01-25 09:57:00
2017-01-25 09:58:00

2017-01-26 09:51:00
2017-01-26 09:52:00
2017-01-26 09:53:00
2017-01-26 09:54:00
2017-01-26 09:55:00
2017-01-26 09:56:00
2017-01-26 09:57:00
2017-01-26 09:58:00
2017-01-26 09:59:00
2017-01-26 10:00:00
2017-01-26 10:01:00
2017-01-26 10:02:00
2017-01-26 10:03:00
2017-01-26 10:04:00
2017-01-26 10:05:00
2017-01-26 10:06:00
2017-01-26 10:07:00
2017-01-26 10:08:00
2017-01-26 10:09:00
2017-01-26 10:10:00
2017-01-26 10:11:00
2017-01-26 10:12:00
2017-01-26 10:13:00
2017-01-26 10:14:00
2017-01-26 10:15:00
2017-01-26 10:16:00
2017-01-26 10:17:00
2017-01-26 10:18:00
2017-01-26 10:19:00
2017-01-26 10:20:00
2017-01-26 10:21:00
2017-01-26 10:22:00
2017-01-26 10:23:00
2017-01-26 10:24:00
2017-01-26 10:25:00
2017-01-26 10:26:00
2017-01-26 10:27:00
2017-01-26 10:28:00
2017-01-26 10:29:00
2017-01-26 10:30:00
2017-01-26 10:31:00
2017-01-26 10:32:00
2017-01-26 10:33:00
2017-01-26 10:34:00
2017-01-26 10:35:00
2017-01-26 10:36:00
2017-01-26 10:37:00
2017-01-26 10:38:00
2017-01-26 10:39:00
2017-01-26 10:40:00


2017-01-27 10:13:00
2017-01-27 10:14:00
2017-01-27 10:15:00
2017-01-27 10:16:00
2017-01-27 10:17:00
2017-01-27 10:18:00
2017-01-27 10:19:00
2017-01-27 10:20:00
2017-01-27 10:21:00
2017-01-27 10:22:00
2017-01-27 10:23:00
2017-01-27 10:24:00
2017-01-27 10:25:00
2017-01-27 10:26:00
2017-01-27 10:27:00
2017-01-27 10:28:00
2017-01-27 10:29:00
2017-01-27 10:30:00
2017-01-27 10:31:00
2017-01-27 10:32:00
2017-01-27 10:33:00
2017-01-27 10:34:00
2017-01-27 10:35:00
2017-01-27 10:36:00
2017-01-27 10:37:00
2017-01-27 10:38:00
2017-01-27 10:39:00
2017-01-27 10:40:00
2017-01-27 10:41:00
2017-01-27 10:42:00
2017-01-27 10:43:00
2017-01-27 10:44:00
2017-01-27 10:45:00
2017-01-27 10:46:00
2017-01-27 10:47:00
2017-01-27 10:48:00
2017-01-27 10:49:00
2017-01-27 10:50:00
2017-01-27 10:51:00
2017-01-27 10:52:00
2017-01-27 10:53:00
2017-01-27 10:54:00
2017-01-27 10:55:00
2017-01-27 10:56:00
2017-01-27 10:57:00
2017-01-27 10:58:00
2017-01-27 10:59:00
2017-01-27 11:00:00
2017-01-27 11:01:00
2017-01-27 11:02:00


2017-01-30 10:53:00
2017-01-30 10:54:00
2017-01-30 10:55:00
2017-01-30 10:56:00
2017-01-30 10:57:00
2017-01-30 10:58:00
2017-01-30 10:59:00
2017-01-30 11:00:00
2017-01-30 11:01:00
2017-01-30 11:02:00
2017-01-30 11:03:00
2017-01-30 11:04:00
2017-01-30 11:05:00
2017-01-30 11:06:00
2017-01-30 11:07:00
2017-01-30 11:08:00
2017-01-30 11:09:00
2017-01-30 11:10:00
2017-01-30 11:11:00
2017-01-30 11:12:00
2017-01-30 11:13:00
2017-01-30 11:14:00
2017-01-30 11:15:00
2017-01-30 11:16:00
2017-01-30 11:17:00
2017-01-30 11:18:00
2017-01-30 11:19:00
2017-01-30 11:20:00
2017-01-30 11:21:00
2017-01-30 11:22:00
2017-01-30 11:23:00
2017-01-30 11:24:00
2017-01-30 11:25:00
2017-01-30 11:26:00
2017-01-30 11:27:00
2017-01-30 11:28:00
2017-01-30 11:29:00
2017-01-30 11:30:00
2017-01-30 11:31:00
2017-01-30 11:32:00
2017-01-30 11:33:00
2017-01-30 11:34:00
2017-01-30 11:35:00
2017-01-30 11:36:00
2017-01-30 11:37:00
2017-01-30 11:38:00
2017-01-30 11:39:00
2017-01-30 11:40:00
2017-01-30 11:41:00
2017-01-30 11:42:00


2017-01-31 11:34:00
2017-01-31 11:35:00
2017-01-31 11:36:00
2017-01-31 11:37:00
2017-01-31 11:38:00
2017-01-31 11:39:00
2017-01-31 11:40:00
2017-01-31 11:41:00
2017-01-31 11:42:00
2017-01-31 11:43:00
2017-01-31 11:44:00
2017-01-31 11:45:00
2017-01-31 11:46:00
2017-01-31 11:47:00
2017-01-31 11:48:00
2017-01-31 11:49:00
2017-01-31 11:50:00
2017-01-31 11:51:00
2017-01-31 11:52:00
2017-01-31 11:53:00
2017-01-31 11:54:00
2017-01-31 11:55:00
2017-01-31 11:56:00
2017-01-31 11:57:00
2017-01-31 11:58:00
2017-01-31 11:59:00
2017-01-31 12:00:00
2017-01-31 12:01:00
2017-01-31 12:02:00
2017-01-31 12:03:00
2017-01-31 12:04:00
2017-01-31 12:05:00
2017-01-31 12:06:00
2017-01-31 12:07:00
2017-01-31 12:08:00
2017-01-31 12:09:00
2017-01-31 12:10:00
2017-01-31 12:11:00
2017-01-31 12:12:00
2017-01-31 12:13:00
2017-01-31 12:14:00
2017-01-31 12:15:00
2017-01-31 12:16:00
2017-01-31 12:17:00
2017-01-31 12:18:00
2017-01-31 12:19:00
2017-01-31 12:20:00
2017-01-31 12:21:00
2017-01-31 12:22:00
2017-01-31 12:23:00


...

2017-03-03 12:48:00
2017-03-03 12:49:00
2017-03-03 12:50:00
2017-03-03 12:51:00
2017-03-03 12:52:00
2017-03-03 12:53:00
2017-03-03 12:54:00
2017-03-03 12:55:00
2017-03-03 12:56:00
2017-03-03 12:57:00
2017-03-03 12:58:00
2017-03-03 12:59:00
2017-03-03 13:00:00
2017-03-03 13:01:00
2017-03-03 13:02:00
2017-03-03 13:03:00
2017-03-03 13:04:00
2017-03-03 13:05:00
2017-03-03 13:06:00
2017-03-03 13:07:00
2017-03-03 13:08:00
2017-03-03 13:09:00
2017-03-03 13:10:00
2017-03-03 13:11:00
2017-03-03 13:12:00
2017-03-03 13:13:00
2017-03-03 13:14:00
2017-03-03 13:15:00
2017-03-03 13:16:00
2017-03-03 13:17:00
2017-03-03 13:18:00
2017-03-03 13:19:00
2017-03-03 13:20:00
2017-03-03 13:21:00
2017-03-03 13:22:00
2017-03-03 13:23:00
2017-03-03 13:24:00
2017-03-03 13:25:00
2017-03-03 13:26:00
2017-03-03 13:27:00
2017-03-03 13:28:00
2017-03-03 13:29:00
2017-03-03 13:30:00
2017-03-03 13:31:00
2017-03-03 13:32:00
2017-03-03 13:33:00
2017-03-03 13:34:00
2017-03-03 13:35:00
2017-03-03 13:36:00
2017-03-03 13:37:00


2017-03-06 13:31:00
2017-03-06 13:32:00
2017-03-06 13:33:00
2017-03-06 13:34:00
2017-03-06 13:35:00
2017-03-06 13:36:00
2017-03-06 13:37:00
2017-03-06 13:38:00
2017-03-06 13:39:00
2017-03-06 13:40:00
2017-03-06 13:41:00
2017-03-06 13:42:00
2017-03-06 13:43:00
2017-03-06 13:44:00
2017-03-06 13:45:00
2017-03-06 13:46:00
2017-03-06 13:47:00
2017-03-06 13:48:00
2017-03-06 13:49:00
2017-03-06 13:50:00
2017-03-06 13:51:00
2017-03-06 13:52:00
2017-03-06 13:53:00
2017-03-06 13:54:00
2017-03-06 13:55:00
2017-03-06 13:56:00
2017-03-06 13:57:00
2017-03-06 13:58:00
2017-03-06 13:59:00
2017-03-06 14:00:00
2017-03-06 14:01:00
2017-03-06 14:02:00
2017-03-06 14:03:00
2017-03-06 14:04:00
2017-03-06 14:05:00
2017-03-06 14:06:00
2017-03-06 14:07:00
2017-03-06 14:08:00
2017-03-06 14:09:00
2017-03-06 14:10:00
2017-03-06 14:11:00
2017-03-06 14:12:00
2017-03-06 14:13:00
2017-03-06 14:14:00
2017-03-06 14:15:00
2017-03-06 14:16:00
2017-03-06 14:17:00
2017-03-06 14:18:00
2017-03-06 14:19:00
2017-03-06 14:20:00


2017-03-07 14:11:00
2017-03-07 14:12:00
2017-03-07 14:13:00
2017-03-07 14:14:00
2017-03-07 14:15:00
2017-03-07 14:16:00
2017-03-07 14:17:00
2017-03-07 14:18:00
2017-03-07 14:19:00
2017-03-07 14:20:00
2017-03-07 14:21:00
2017-03-07 14:22:00
2017-03-07 14:23:00
2017-03-07 14:24:00
2017-03-07 14:25:00
2017-03-07 14:26:00
2017-03-07 14:27:00
2017-03-07 14:28:00
2017-03-07 14:29:00
2017-03-07 14:30:00
2017-03-07 14:31:00
2017-03-07 14:32:00
2017-03-07 14:33:00
2017-03-07 14:34:00
2017-03-07 14:35:00
2017-03-07 14:36:00
2017-03-07 14:37:00
2017-03-07 14:38:00
2017-03-07 14:39:00
2017-03-07 14:40:00
2017-03-07 14:41:00
2017-03-07 14:42:00
2017-03-07 14:43:00
2017-03-07 14:44:00
2017-03-07 14:45:00
2017-03-07 14:46:00
2017-03-07 14:47:00
2017-03-07 14:48:00
2017-03-07 14:49:00
2017-03-07 14:50:00
2017-03-07 14:51:00
2017-03-07 14:52:00
2017-03-07 14:53:00
2017-03-07 14:54:00
2017-03-07 14:55:00
2017-03-07 14:56:00
2017-03-07 14:57:00
2017-03-07 14:58:00
2017-03-07 14:59:00
2017-03-07 15:00:00


2017-03-08 14:31:00
2017-03-08 14:32:00
2017-03-08 14:33:00
2017-03-08 14:34:00
2017-03-08 14:35:00
2017-03-08 14:36:00
2017-03-08 14:37:00
2017-03-08 14:38:00
2017-03-08 14:39:00
2017-03-08 14:40:00
2017-03-08 14:41:00
2017-03-08 14:42:00
2017-03-08 14:43:00
2017-03-08 14:44:00
2017-03-08 14:45:00
2017-03-08 14:46:00
2017-03-08 14:47:00
2017-03-08 14:48:00
2017-03-08 14:49:00
2017-03-08 14:50:00
2017-03-08 14:51:00
2017-03-08 14:52:00
2017-03-08 14:53:00
2017-03-08 14:54:00
2017-03-08 14:55:00
2017-03-08 14:56:00
2017-03-08 14:57:00
2017-03-08 14:58:00
2017-03-08 14:59:00
2017-03-08 15:00:00
2017-03-08 15:01:00
2017-03-08 15:02:00
2017-03-08 15:03:00
2017-03-08 15:04:00
2017-03-08 15:05:00
2017-03-08 15:06:00
2017-03-08 15:07:00
2017-03-08 15:08:00
2017-03-08 15:09:00
2017-03-08 15:10:00
2017-03-08 15:11:00
2017-03-08 15:12:00
2017-03-08 15:13:00
2017-03-08 15:14:00
2017-03-08 15:15:00
2017-03-08 15:16:00
2017-03-08 15:17:00
2017-03-08 15:18:00
2017-03-08 15:19:00
2017-03-08 15:20:00


2017-03-09 15:12:00
2017-03-09 15:13:00
2017-03-09 15:14:00
2017-03-09 15:15:00
2017-03-09 15:16:00
2017-03-09 15:17:00
2017-03-09 15:18:00
2017-03-09 15:19:00
2017-03-09 15:20:00
2017-03-09 15:21:00
2017-03-09 15:22:00
2017-03-09 15:23:00
2017-03-09 15:24:00
2017-03-09 15:25:00
2017-03-09 15:26:00
2017-03-09 15:27:00
2017-03-09 15:28:00
Info: AGW:  Total Pnl: -2.04%  Profit/Loss Ratio: 0.72  Accuracy: 0.47  Score: 0.71 
Info:  Total Pnl: -2.04%  Score: 0.71  Max Drawdown: 2.64%  RoC: -1.85%  P/L Ratio: 0.72  Accuracy: 0.47  Score: 0.71 


In [35]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
       # return ['AGW']
         return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: VKE
Processing data for stock: UWC
Processing data for stock: HDK
Processing data for stock: IWU
Processing data for stock: IYU
Processing data for stock: HZT
Processing data for stock: TGI
Processing data for stock: AUZ
Processing data for stock: JSG
Processing data for stock: OMP
Processing data for stock: CYD
Processing data for stock: CHV
Processing data for stock: UBF
Processing data for stock: DCO
Processing data for stock: DVV
Processing data for stock: WUT
Processing data for stock: FKI
Processing data for stock: FFS
Processing data for stock: AIO
Processing data for stock: MQK
Processing data for stock: GGK
Processing data for stock: KFW
Processing data for stock: JYW
Processing data for stock: PLX
Processing data for stock: QVE
Processing data for stock: BLR
Processing data for stock: OGU
Processing data for stock: BSN
Processing data for stock: VML
Processing data for stock: KKG
Processing data for stock: VND
Processing data for stock: NDG
Processi

2017-01-25 13:34:00
2017-01-25 13:35:00
2017-01-25 13:36:00
2017-01-25 13:37:00
2017-01-25 13:38:00
2017-01-25 13:39:00
2017-01-25 13:40:00
2017-01-25 13:41:00
2017-01-25 13:42:00
2017-01-25 13:43:00
2017-01-25 13:44:00
2017-01-25 13:45:00
2017-01-25 13:46:00
2017-01-25 13:47:00
2017-01-25 13:48:00
2017-01-25 13:49:00
2017-01-25 13:50:00
2017-01-25 13:51:00
2017-01-25 13:52:00
2017-01-25 13:53:00
2017-01-25 13:54:00
2017-01-25 13:55:00
2017-01-25 13:56:00
2017-01-25 13:57:00
2017-01-25 13:58:00
2017-01-25 13:59:00
2017-01-25 14:00:00
2017-01-25 14:01:00
2017-01-25 14:02:00
2017-01-25 14:03:00
2017-01-25 14:04:00
2017-01-25 14:05:00
2017-01-25 14:06:00
2017-01-25 14:07:00
2017-01-25 14:08:00
2017-01-25 14:09:00
2017-01-25 14:10:00
2017-01-25 14:11:00
2017-01-25 14:12:00
2017-01-25 14:13:00
2017-01-25 14:14:00
2017-01-25 14:15:00
2017-01-25 14:16:00
2017-01-25 14:17:00
2017-01-25 14:18:00
2017-01-25 14:19:00
2017-01-25 14:20:00
2017-01-25 14:21:00
2017-01-25 14:22:00
2017-01-25 14:23:00


2017-01-26 13:58:00
2017-01-26 13:59:00
2017-01-26 14:00:00
2017-01-26 14:01:00
2017-01-26 14:02:00
2017-01-26 14:03:00
2017-01-26 14:04:00
2017-01-26 14:05:00
2017-01-26 14:06:00
2017-01-26 14:07:00
2017-01-26 14:08:00
2017-01-26 14:09:00
2017-01-26 14:10:00
2017-01-26 14:11:00
2017-01-26 14:12:00
2017-01-26 14:13:00
2017-01-26 14:14:00
2017-01-26 14:15:00
2017-01-26 14:16:00
2017-01-26 14:17:00
2017-01-26 14:18:00
2017-01-26 14:19:00
2017-01-26 14:20:00
2017-01-26 14:21:00
2017-01-26 14:22:00
2017-01-26 14:23:00
2017-01-26 14:24:00
2017-01-26 14:25:00
2017-01-26 14:26:00
2017-01-26 14:27:00
2017-01-26 14:28:00
2017-01-26 14:29:00
2017-01-26 14:30:00
2017-01-26 14:31:00
2017-01-26 14:32:00
2017-01-26 14:33:00
2017-01-26 14:34:00
2017-01-26 14:35:00
2017-01-26 14:36:00
2017-01-26 14:37:00
2017-01-26 14:38:00
2017-01-26 14:39:00
2017-01-26 14:40:00
2017-01-26 14:41:00
2017-01-26 14:42:00
2017-01-26 14:43:00
2017-01-26 14:44:00
2017-01-26 14:45:00
2017-01-26 14:46:00
2017-01-26 14:47:00


2017-01-27 14:12:00
2017-01-27 14:13:00
2017-01-27 14:14:00
2017-01-27 14:15:00
2017-01-27 14:16:00
2017-01-27 14:17:00
2017-01-27 14:18:00
2017-01-27 14:19:00
2017-01-27 14:20:00
2017-01-27 14:21:00
2017-01-27 14:22:00
2017-01-27 14:23:00
2017-01-27 14:24:00
2017-01-27 14:25:00
2017-01-27 14:26:00
2017-01-27 14:27:00
2017-01-27 14:28:00
2017-01-27 14:29:00
2017-01-27 14:30:00
2017-01-27 14:31:00
2017-01-27 14:32:00
2017-01-27 14:33:00
2017-01-27 14:34:00
2017-01-27 14:35:00
2017-01-27 14:36:00
2017-01-27 14:37:00
2017-01-27 14:38:00
2017-01-27 14:39:00
2017-01-27 14:40:00
2017-01-27 14:41:00
2017-01-27 14:42:00
2017-01-27 14:43:00
2017-01-27 14:44:00
2017-01-27 14:45:00
2017-01-27 14:46:00
2017-01-27 14:47:00
2017-01-27 14:48:00
2017-01-27 14:49:00
2017-01-27 14:50:00
2017-01-27 14:51:00
2017-01-27 14:52:00
2017-01-27 14:53:00
2017-01-27 14:54:00
2017-01-27 14:55:00
2017-01-27 14:56:00
2017-01-27 14:57:00
2017-01-27 14:58:00
2017-01-27 14:59:00
2017-01-27 15:00:00
2017-01-27 15:01:00


2017-01-30 14:50:00
2017-01-30 14:51:00
2017-01-30 14:52:00
2017-01-30 14:53:00
2017-01-30 14:54:00
2017-01-30 14:55:00
2017-01-30 14:56:00
2017-01-30 14:57:00
2017-01-30 14:58:00
2017-01-30 14:59:00
2017-01-30 15:00:00
2017-01-30 15:01:00
2017-01-30 15:02:00
2017-01-30 15:03:00
2017-01-30 15:04:00
2017-01-30 15:05:00
2017-01-30 15:06:00
2017-01-30 15:07:00
2017-01-30 15:08:00
2017-01-30 15:09:00
2017-01-30 15:10:00
2017-01-30 15:11:00
2017-01-30 15:12:00
2017-01-30 15:13:00
2017-01-30 15:14:00
2017-01-30 15:15:00
2017-01-30 15:16:00
2017-01-30 15:17:00
2017-01-30 15:18:00
2017-01-30 15:19:00
2017-01-30 15:20:00
2017-01-30 15:21:00
2017-01-30 15:22:00
2017-01-30 15:23:00
2017-01-30 15:24:00
2017-01-30 15:25:00
2017-01-30 15:26:00
2017-01-30 15:27:00
2017-01-30 15:28:00
2017-01-31 09:17:00
2017-01-31 09:18:00
2017-01-31 09:19:00
2017-01-31 09:20:00
2017-01-31 09:21:00
2017-01-31 09:22:00
2017-01-31 09:23:00
2017-01-31 09:24:00
2017-01-31 09:25:00
2017-01-31 09:26:00
2017-01-31 09:27:00


...

Warn: Not Enough Capital
2017-03-03 14:44:00
2017-03-03 14:45:00
2017-03-03 14:46:00
2017-03-03 14:47:00
2017-03-03 14:48:00
2017-03-03 14:49:00
Warn: Not Enough Capital
2017-03-03 14:50:00
Warn: Not Enough Capital
2017-03-03 14:51:00
Warn: Not Enough Capital
2017-03-03 14:52:00
Warn: Not Enough Capital
2017-03-03 14:53:00
Warn: Not Enough Capital
2017-03-03 14:54:00
Warn: Not Enough Capital
2017-03-03 14:55:00
Warn: Not Enough Capital
2017-03-03 14:56:00
2017-03-03 14:57:00
2017-03-03 14:58:00
2017-03-03 14:59:00
2017-03-03 15:00:00
Warn: Not Enough Capital
2017-03-03 15:01:00
Warn: Not Enough Capital
2017-03-03 15:02:00
Warn: Not Enough Capital
2017-03-03 15:03:00
Warn: Not Enough Capital
2017-03-03 15:04:00
Warn: Not Enough Capital
2017-03-03 15:05:00
Warn: Not Enough Capital
2017-03-03 15:06:00
Warn: Not Enough Capital
2017-03-03 15:07:00
2017-03-03 15:08:00
2017-03-03 15:09:00
2017-03-03 15:10:00
2017-03-03 15:11:00
Warn: Not Enough Capital
2017-03-03 15:12:00
Warn: Not Enough Cap

2017-03-06 14:49:00
2017-03-06 14:50:00
2017-03-06 14:51:00
2017-03-06 14:52:00
2017-03-06 14:53:00
2017-03-06 14:54:00
2017-03-06 14:55:00
2017-03-06 14:56:00
2017-03-06 14:57:00
2017-03-06 14:58:00
2017-03-06 14:59:00
2017-03-06 15:00:00
2017-03-06 15:01:00
2017-03-06 15:02:00
2017-03-06 15:03:00
2017-03-06 15:04:00
2017-03-06 15:05:00
2017-03-06 15:06:00
2017-03-06 15:07:00
2017-03-06 15:08:00
2017-03-06 15:09:00
2017-03-06 15:10:00
2017-03-06 15:11:00
2017-03-06 15:12:00
2017-03-06 15:13:00
2017-03-06 15:14:00
2017-03-06 15:15:00
2017-03-06 15:16:00
2017-03-06 15:17:00
2017-03-06 15:18:00
2017-03-06 15:19:00
2017-03-06 15:20:00
2017-03-06 15:21:00
2017-03-06 15:22:00
2017-03-06 15:23:00
2017-03-06 15:24:00
2017-03-06 15:25:00
2017-03-06 15:26:00
2017-03-06 15:27:00
2017-03-06 15:28:00
2017-03-07 09:17:00
2017-03-07 09:18:00
2017-03-07 09:19:00
2017-03-07 09:20:00
2017-03-07 09:21:00
2017-03-07 09:22:00
2017-03-07 09:23:00
2017-03-07 09:24:00
2017-03-07 09:25:00
2017-03-07 09:26:00


2017-03-07 15:20:00
2017-03-07 15:21:00
2017-03-07 15:22:00
2017-03-07 15:23:00
2017-03-07 15:24:00
2017-03-07 15:25:00
2017-03-07 15:26:00
2017-03-07 15:27:00
2017-03-07 15:28:00
2017-03-08 09:17:00
2017-03-08 09:18:00
2017-03-08 09:19:00
2017-03-08 09:20:00
2017-03-08 09:21:00
2017-03-08 09:22:00
2017-03-08 09:23:00
2017-03-08 09:24:00
2017-03-08 09:25:00
2017-03-08 09:26:00
2017-03-08 09:27:00
2017-03-08 09:28:00
2017-03-08 09:29:00
2017-03-08 09:30:00
2017-03-08 09:31:00
2017-03-08 09:32:00
2017-03-08 09:33:00
2017-03-08 09:34:00
2017-03-08 09:35:00
2017-03-08 09:36:00
2017-03-08 09:37:00
2017-03-08 09:38:00
2017-03-08 09:39:00
2017-03-08 09:40:00
2017-03-08 09:41:00
2017-03-08 09:42:00
2017-03-08 09:43:00
2017-03-08 09:44:00
2017-03-08 09:45:00
2017-03-08 09:46:00
2017-03-08 09:47:00
2017-03-08 09:48:00
2017-03-08 09:49:00
Warn: Not Enough Capital
2017-03-08 09:50:00
Warn: Not Enough Capital
2017-03-08 09:51:00
Warn: Not Enough Capital
2017-03-08 09:52:00
Warn: Not Enough Capital


2017-03-08 15:24:00
2017-03-08 15:25:00
2017-03-08 15:26:00
2017-03-08 15:27:00
2017-03-08 15:28:00
2017-03-09 09:17:00
2017-03-09 09:18:00
2017-03-09 09:19:00
2017-03-09 09:20:00
2017-03-09 09:21:00
2017-03-09 09:22:00
2017-03-09 09:23:00
2017-03-09 09:24:00
2017-03-09 09:25:00
2017-03-09 09:26:00
2017-03-09 09:27:00
2017-03-09 09:28:00
2017-03-09 09:29:00
2017-03-09 09:30:00
2017-03-09 09:31:00
2017-03-09 09:32:00
2017-03-09 09:33:00
2017-03-09 09:34:00
2017-03-09 09:35:00
2017-03-09 09:36:00
2017-03-09 09:37:00
2017-03-09 09:38:00
2017-03-09 09:39:00
2017-03-09 09:40:00
2017-03-09 09:41:00
2017-03-09 09:42:00
2017-03-09 09:43:00
2017-03-09 09:44:00
2017-03-09 09:45:00
2017-03-09 09:46:00
2017-03-09 09:47:00
2017-03-09 09:48:00
2017-03-09 09:49:00
2017-03-09 09:50:00
2017-03-09 09:51:00
2017-03-09 09:52:00
2017-03-09 09:53:00
2017-03-09 09:54:00
2017-03-09 09:55:00
2017-03-09 09:56:00
2017-03-09 09:57:00
2017-03-09 09:58:00
2017-03-09 09:59:00
2017-03-09 10:00:00
2017-03-09 10:01:00


Info: XAD:  Total Pnl: -0.01%  Profit/Loss Ratio: 0.98  Accuracy: 0.49  Score: 0.75 
Info: XPV:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.43  Accuracy: 0.51  Score: 0.71 
Info: MAS:  Total Pnl: 0.15%  Profit/Loss Ratio: 1.03  Accuracy: 0.48  Score: 1.17 
Info: WUT:  Total Pnl: -0.00%  Profit/Loss Ratio: 0.89  Accuracy: 0.38  Score: 0.70 
Info: FFS:  Total Pnl: 0.01%  Profit/Loss Ratio: 1.06  Accuracy: 0.51  Score: 0.74 
Info: UBF:  Total Pnl: -0.00%  Profit/Loss Ratio: 0.99  Accuracy: 0.50  Score: 0.80 
Info: PQS:  Total Pnl: -0.00%  Profit/Loss Ratio: 0.91  Accuracy: 0.50  Score: 0.71 
Info: FFA:  Total Pnl: -0.01%  Profit/Loss Ratio: 0.83  Accuracy: 0.48  Score: 0.72 
Info: FUR:  Total Pnl: 0.20%  Profit/Loss Ratio: 1.01  Accuracy: 0.48  Score: nan 
Info: LKB:  Total Pnl: -0.07%  Profit/Loss Ratio: 0.95  Accuracy: 0.48  Score: 0.92 
Info: RGG:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.07  Accuracy: 0.46  Score: 0.70 
Info: IFL:  Total Pnl: 0.40%  Profit/Loss Ratio: 1.06  Accuracy: 0.48  

In [37]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_2"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
         return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


https://raw.githubusercontent.com/Auquan/auquan-historical-data/master/qq2Data/trainingDataP2_2/stock_list.txt
Processing data for stock: VKE
Processing data for stock: UWC
Processing data for stock: HDK
Processing data for stock: IWU
Processing data for stock: IYU
Processing data for stock: HZT
Processing data for stock: TGI
Processing data for stock: AUZ
Processing data for stock: JSG
Processing data for stock: OMP
Processing data for stock: CYD
Processing data for stock: CHV
Processing data for stock: UBF
Processing data for stock: DCO
Processing data for stock: DVV
Processing data for stock: WUT
Processing data for stock: FKI
Processing data for stock: FFS
Processing data for stock: AIO
Processing data for stock: MQK
Processing data for stock: GGK
Processing data for stock: KFW
Processing data for stock: JYW
Processing data for stock: PLX
Processing data for stock: QVE
Processing data for stock: BLR
Processing data for stock: OGU
Processing data for stock: BSN
Processing data for s

Processing data for stock: ZSI
Processing data for stock: NBQ
Processing data for stock: KAA
Processing data for stock: FFA
Processing data for stock: ILW
Processing data for stock: WTJ
Processing data for stock: VTN
Processing data for stock: XFD
Processing data for stock: CUN
Processing data for stock: IUQ
Processing data for stock: IMC
Processing data for stock: NSL
Processing data for stock: JCR
Processing data for stock: WAG
Processing instruments before beginning backtesting. This could take some time...
10% done...
20% done...
30% done...
40% done...
50% done...
60% done...
70% done...
80% done...
90% done...
2017-02-06 09:17:00
2017-02-06 09:18:00
2017-02-06 09:19:00
2017-02-06 09:20:00
2017-02-06 09:21:00
2017-02-06 09:22:00
2017-02-06 09:23:00
2017-02-06 09:24:00
2017-02-06 09:25:00
2017-02-06 09:26:00
2017-02-06 09:27:00
2017-02-06 09:28:00
2017-02-06 09:29:00
2017-02-06 09:30:00
2017-02-06 09:31:00
2017-02-06 09:32:00
2017-02-06 09:33:00
2017-02-06 09:34:00
2017-02-06 09:35

2017-02-06 14:34:00
2017-02-06 14:35:00
2017-02-06 14:36:00
2017-02-06 14:37:00
2017-02-06 14:38:00
2017-02-06 14:39:00
2017-02-06 14:40:00
Warn: Not Enough Capital
2017-02-06 14:41:00
Warn: Not Enough Capital
2017-02-06 14:42:00
Warn: Not Enough Capital
2017-02-06 14:43:00
Warn: Not Enough Capital
2017-02-06 14:44:00
Warn: Not Enough Capital
2017-02-06 14:45:00
Warn: Not Enough Capital
2017-02-06 14:46:00
Warn: Not Enough Capital
2017-02-06 14:47:00
2017-02-06 14:48:00
2017-02-06 14:49:00
2017-02-06 14:50:00
2017-02-06 14:51:00
2017-02-06 14:52:00
2017-02-06 14:53:00
Warn: Not Enough Capital
2017-02-06 14:54:00
Warn: Not Enough Capital
2017-02-06 14:55:00
2017-02-06 14:56:00
2017-02-06 14:57:00
2017-02-06 14:58:00
2017-02-06 14:59:00
2017-02-06 15:00:00
2017-02-06 15:01:00
2017-02-06 15:02:00
2017-02-06 15:03:00
2017-02-06 15:04:00
2017-02-06 15:05:00
2017-02-06 15:06:00
2017-02-06 15:07:00
2017-02-06 15:08:00
2017-02-06 15:09:00
2017-02-06 15:10:00
2017-02-06 15:11:00
2017-02-06 15:1

2017-02-07 14:22:00
2017-02-07 14:23:00
2017-02-07 14:24:00
2017-02-07 14:25:00
2017-02-07 14:26:00
2017-02-07 14:27:00
2017-02-07 14:28:00
2017-02-07 14:29:00
2017-02-07 14:30:00
2017-02-07 14:31:00
Warn: Not Enough Capital
2017-02-07 14:32:00
Warn: Not Enough Capital
2017-02-07 14:33:00
Warn: Not Enough Capital
2017-02-07 14:34:00
2017-02-07 14:35:00
2017-02-07 14:36:00
2017-02-07 14:37:00
2017-02-07 14:38:00
Warn: Not Enough Capital
2017-02-07 14:39:00
Warn: Not Enough Capital
2017-02-07 14:40:00
2017-02-07 14:41:00
2017-02-07 14:42:00
Warn: Not Enough Capital
2017-02-07 14:43:00
Warn: Not Enough Capital
2017-02-07 14:44:00
Warn: Not Enough Capital
2017-02-07 14:45:00
Warn: Not Enough Capital
2017-02-07 14:46:00
2017-02-07 14:47:00
2017-02-07 14:48:00
2017-02-07 14:49:00
2017-02-07 14:50:00
2017-02-07 14:51:00
2017-02-07 14:52:00
2017-02-07 14:53:00
2017-02-07 14:54:00
2017-02-07 14:55:00
Warn: Not Enough Capital
2017-02-07 14:56:00
Warn: Not Enough Capital
2017-02-07 14:57:00
Warn:

2017-02-08 14:19:00
2017-02-08 14:20:00
2017-02-08 14:21:00
2017-02-08 14:22:00
2017-02-08 14:23:00
2017-02-08 14:24:00
2017-02-08 14:25:00
2017-02-08 14:26:00
2017-02-08 14:27:00
2017-02-08 14:28:00
2017-02-08 14:29:00
2017-02-08 14:30:00
2017-02-08 14:31:00
2017-02-08 14:32:00
2017-02-08 14:33:00
2017-02-08 14:34:00
2017-02-08 14:35:00
2017-02-08 14:36:00
2017-02-08 14:37:00
2017-02-08 14:38:00
2017-02-08 14:39:00
2017-02-08 14:40:00
2017-02-08 14:41:00
2017-02-08 14:42:00
2017-02-08 14:43:00
2017-02-08 14:44:00
2017-02-08 14:45:00
2017-02-08 14:46:00
2017-02-08 14:47:00
2017-02-08 14:48:00
2017-02-08 14:49:00
2017-02-08 14:50:00
2017-02-08 14:51:00
2017-02-08 14:52:00
2017-02-08 14:53:00
2017-02-08 14:54:00
2017-02-08 14:55:00
2017-02-08 14:56:00
2017-02-08 14:57:00
2017-02-08 14:58:00
2017-02-08 14:59:00
2017-02-08 15:00:00
2017-02-08 15:01:00
2017-02-08 15:02:00
2017-02-08 15:03:00
2017-02-08 15:04:00
2017-02-08 15:05:00
2017-02-08 15:06:00
2017-02-08 15:07:00
2017-02-08 15:08:00


...

2017-03-17 14:31:00
2017-03-17 14:32:00
2017-03-17 14:33:00
2017-03-17 14:34:00
2017-03-17 14:35:00
2017-03-17 14:36:00
2017-03-17 14:37:00
2017-03-17 14:38:00
2017-03-17 14:39:00
2017-03-17 14:40:00
2017-03-17 14:41:00
2017-03-17 14:42:00
2017-03-17 14:43:00
2017-03-17 14:44:00
2017-03-17 14:45:00
2017-03-17 14:46:00
2017-03-17 14:47:00
2017-03-17 14:48:00
2017-03-17 14:49:00
2017-03-17 14:50:00
2017-03-17 14:51:00
2017-03-17 14:52:00
2017-03-17 14:53:00
2017-03-17 14:54:00
2017-03-17 14:55:00
2017-03-17 14:56:00
2017-03-17 14:57:00
2017-03-17 14:58:00
2017-03-17 14:59:00
2017-03-17 15:00:00
2017-03-17 15:01:00
2017-03-17 15:02:00
2017-03-17 15:03:00
2017-03-17 15:04:00
2017-03-17 15:05:00
2017-03-17 15:06:00
2017-03-17 15:07:00
2017-03-17 15:08:00
2017-03-17 15:09:00
2017-03-17 15:10:00
2017-03-17 15:11:00
2017-03-17 15:12:00
2017-03-17 15:13:00
2017-03-17 15:14:00
2017-03-17 15:15:00
2017-03-17 15:16:00
2017-03-17 15:17:00
2017-03-17 15:18:00
2017-03-17 15:19:00
2017-03-17 15:20:00


2017-03-22 15:10:00
2017-03-22 15:11:00
2017-03-22 15:12:00
2017-03-22 15:13:00
2017-03-22 15:14:00
2017-03-22 15:15:00
2017-03-22 15:16:00
2017-03-22 15:17:00
2017-03-22 15:18:00
2017-03-22 15:19:00
2017-03-22 15:20:00
2017-03-22 15:21:00
2017-03-22 15:22:00
2017-03-22 15:23:00
2017-03-22 15:24:00
2017-03-22 15:25:00
2017-03-22 15:26:00
2017-03-22 15:27:00
2017-03-22 15:28:00
2017-03-28 09:17:00
2017-03-28 09:18:00
2017-03-28 09:19:00
2017-03-28 09:20:00
2017-03-28 09:21:00
2017-03-28 09:22:00
2017-03-28 09:23:00
2017-03-28 09:24:00
2017-03-28 09:25:00
2017-03-28 09:26:00
2017-03-28 09:27:00
2017-03-28 09:28:00
2017-03-28 09:29:00
2017-03-28 09:30:00
2017-03-28 09:31:00
2017-03-28 09:32:00
2017-03-28 09:33:00
2017-03-28 09:34:00
2017-03-28 09:35:00
2017-03-28 09:36:00
2017-03-28 09:37:00
2017-03-28 09:38:00
2017-03-28 09:39:00
2017-03-28 09:40:00
2017-03-28 09:41:00
2017-03-28 09:42:00
2017-03-28 09:43:00
2017-03-28 09:44:00
2017-03-28 09:45:00
2017-03-28 09:46:00
2017-03-28 09:47:00


2017-03-29 09:18:00
2017-03-29 09:19:00
2017-03-29 09:20:00
2017-03-29 09:21:00
2017-03-29 09:22:00
2017-03-29 09:23:00
2017-03-29 09:24:00
2017-03-29 09:25:00
2017-03-29 09:26:00
2017-03-29 09:27:00
2017-03-29 09:28:00
2017-03-29 09:29:00
2017-03-29 09:30:00
2017-03-29 09:31:00
2017-03-29 09:32:00
2017-03-29 09:33:00
2017-03-29 09:34:00
2017-03-29 09:35:00
2017-03-29 09:36:00
2017-03-29 09:37:00
2017-03-29 09:38:00
2017-03-29 09:39:00
2017-03-29 09:40:00
2017-03-29 09:41:00
2017-03-29 09:42:00
2017-03-29 09:43:00
2017-03-29 09:44:00
2017-03-29 09:45:00
2017-03-29 09:46:00
2017-03-29 09:47:00
2017-03-29 09:48:00
2017-03-29 09:49:00
2017-03-29 09:50:00
2017-03-29 09:51:00
2017-03-29 09:52:00
2017-03-29 09:53:00
2017-03-29 09:54:00
2017-03-29 09:55:00
2017-03-29 09:56:00
2017-03-29 09:57:00
2017-03-29 09:58:00
2017-03-29 09:59:00
2017-03-29 10:00:00
2017-03-29 10:01:00
2017-03-29 10:02:00
2017-03-29 10:03:00
2017-03-29 10:04:00
2017-03-29 10:05:00
2017-03-29 10:06:00
2017-03-29 10:07:00


2017-03-30 09:58:00
2017-03-30 09:59:00
2017-03-30 10:00:00
2017-03-30 10:01:00
2017-03-30 10:02:00
2017-03-30 10:03:00
2017-03-30 10:04:00
2017-03-30 10:05:00
2017-03-30 10:06:00
2017-03-30 10:07:00
2017-03-30 10:08:00
2017-03-30 10:09:00
2017-03-30 10:10:00
2017-03-30 10:11:00
2017-03-30 10:12:00
2017-03-30 10:13:00
2017-03-30 10:14:00
2017-03-30 10:15:00
2017-03-30 10:16:00
2017-03-30 10:17:00
2017-03-30 10:18:00
2017-03-30 10:19:00
2017-03-30 10:20:00
2017-03-30 10:21:00
2017-03-30 10:22:00
2017-03-30 10:23:00
2017-03-30 10:24:00
2017-03-30 10:25:00
2017-03-30 10:26:00
2017-03-30 10:27:00
2017-03-30 10:28:00
2017-03-30 10:29:00
2017-03-30 10:30:00
2017-03-30 10:31:00
2017-03-30 10:32:00
2017-03-30 10:33:00
2017-03-30 10:34:00
2017-03-30 10:35:00
2017-03-30 10:36:00
2017-03-30 10:37:00
2017-03-30 10:38:00
2017-03-30 10:39:00
2017-03-30 10:40:00
2017-03-30 10:41:00
2017-03-30 10:42:00
2017-03-30 10:43:00
2017-03-30 10:44:00
2017-03-30 10:45:00
2017-03-30 10:46:00
2017-03-30 10:47:00


Info: ESY:  Total Pnl: 0.14%  Profit/Loss Ratio: 1.34  Accuracy: 0.46  Score: nan 
Info: KAA:  Total Pnl: -0.00%  Profit/Loss Ratio: 0.99  Accuracy: 0.48  Score: 0.71 
Info: VKE:  Total Pnl: 0.20%  Profit/Loss Ratio: 1.01  Accuracy: 0.49  Score: nan 
Info: YGC:  Total Pnl: -0.43%  Profit/Loss Ratio: 0.87  Accuracy: 0.47  Score: nan 
Info: OGU:  Total Pnl: 0.02%  Profit/Loss Ratio: 1.04  Accuracy: 0.48  Score: 0.75 
Info: PFK:  Total Pnl: -0.08%  Profit/Loss Ratio: 0.86  Accuracy: 0.48  Score: 0.76 
Info: GFQ:  Total Pnl: -0.03%  Profit/Loss Ratio: 0.97  Accuracy: 0.48  Score: 0.79 
Info: HHK:  Total Pnl: -0.65%  Profit/Loss Ratio: 0.92  Accuracy: 0.49  Score: nan 
Info: VSL:  Total Pnl: -0.10%  Profit/Loss Ratio: 0.92  Accuracy: 0.47  Score: 0.78 
Info:  Total Pnl: -5.83%  Score: inf  Max Drawdown: 7.82%  RoC: -4.42%  P/L Ratio: 0.95  Accuracy: 0.50  Score: inf 


In [38]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_3"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
         return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


https://raw.githubusercontent.com/Auquan/auquan-historical-data/master/qq2Data/trainingDataP2_3/stock_list.txt
Processing data for stock: VKE
Processing data for stock: UWC
Processing data for stock: HDK
Processing data for stock: IWU
Processing data for stock: IYU
Processing data for stock: HZT
Processing data for stock: TGI
Processing data for stock: AUZ
Processing data for stock: JSG
Processing data for stock: OMP
Processing data for stock: CYD
Processing data for stock: CHV
Processing data for stock: UBF
Processing data for stock: DCO
Processing data for stock: DVV
Processing data for stock: WUT
Processing data for stock: FKI
Processing data for stock: FFS
Processing data for stock: AIO
Processing data for stock: MQK
Processing data for stock: GGK
Processing data for stock: KFW
Processing data for stock: JYW
Processing data for stock: PLX
Processing data for stock: QVE
Processing data for stock: BLR
Processing data for stock: OGU
Processing data for stock: BSN
Processing data for s

Processing data for stock: ZSI
Processing data for stock: NBQ
Processing data for stock: KAA
Processing data for stock: FFA
Processing data for stock: ILW
Processing data for stock: WTJ
Processing data for stock: VTN
Processing data for stock: XFD
Processing data for stock: CUN
Processing data for stock: IUQ
Processing data for stock: IMC
Processing data for stock: NSL
Processing data for stock: JCR
Processing data for stock: WAG
Processing instruments before beginning backtesting. This could take some time...
10% done...
20% done...
30% done...
40% done...
50% done...
60% done...
70% done...
80% done...
90% done...
2017-01-02 09:17:00
2017-01-02 09:18:00
2017-01-02 09:19:00
2017-01-02 09:20:00
2017-01-02 09:21:00
2017-01-02 09:22:00
2017-01-02 09:23:00
2017-01-02 09:24:00
2017-01-02 09:25:00
2017-01-02 09:26:00
2017-01-02 09:27:00
2017-01-02 09:28:00
2017-01-02 09:29:00
2017-01-02 09:30:00
2017-01-02 09:31:00
2017-01-02 09:32:00
2017-01-02 09:33:00
2017-01-02 09:34:00
2017-01-02 09:35

2017-01-02 14:45:00
2017-01-02 14:46:00
2017-01-02 14:47:00
2017-01-02 14:48:00
2017-01-02 14:49:00
2017-01-02 14:50:00
2017-01-02 14:51:00
2017-01-02 14:52:00
2017-01-02 14:53:00
2017-01-02 14:54:00
2017-01-02 14:55:00
2017-01-02 14:56:00
2017-01-02 14:57:00
2017-01-02 14:58:00
2017-01-02 14:59:00
2017-01-02 15:00:00
2017-01-02 15:01:00
2017-01-02 15:02:00
2017-01-02 15:03:00
2017-01-02 15:04:00
2017-01-02 15:05:00
2017-01-02 15:06:00
2017-01-02 15:07:00
2017-01-02 15:08:00
2017-01-02 15:09:00
2017-01-02 15:10:00
2017-01-02 15:11:00
2017-01-02 15:12:00
2017-01-02 15:13:00
2017-01-02 15:14:00
2017-01-02 15:15:00
2017-01-02 15:16:00
2017-01-02 15:17:00
2017-01-02 15:18:00
2017-01-02 15:19:00
2017-01-02 15:20:00
2017-01-02 15:21:00
2017-01-02 15:22:00
2017-01-02 15:23:00
2017-01-02 15:24:00
2017-01-02 15:25:00
2017-01-02 15:26:00
2017-01-02 15:27:00
2017-01-02 15:28:00
2017-01-03 09:17:00
2017-01-03 09:18:00
2017-01-03 09:19:00
2017-01-03 09:20:00
2017-01-03 09:21:00
2017-01-03 09:22:00


2017-01-03 15:26:00
2017-01-03 15:27:00
2017-01-03 15:28:00
2017-01-04 09:17:00
2017-01-04 09:18:00
2017-01-04 09:19:00
2017-01-04 09:20:00
2017-01-04 09:21:00
2017-01-04 09:22:00
2017-01-04 09:23:00
2017-01-04 09:24:00
2017-01-04 09:25:00
2017-01-04 09:26:00
2017-01-04 09:27:00
2017-01-04 09:28:00
2017-01-04 09:29:00
2017-01-04 09:30:00
2017-01-04 09:31:00
2017-01-04 09:32:00
2017-01-04 09:33:00
2017-01-04 09:34:00
2017-01-04 09:35:00
2017-01-04 09:36:00
2017-01-04 09:37:00
2017-01-04 09:38:00
2017-01-04 09:39:00
2017-01-04 09:40:00
2017-01-04 09:41:00
2017-01-04 09:42:00
2017-01-04 09:43:00
2017-01-04 09:44:00
2017-01-04 09:45:00
2017-01-04 09:46:00
2017-01-04 09:47:00
2017-01-04 09:48:00
2017-01-04 09:49:00
2017-01-04 09:50:00
2017-01-04 09:51:00
2017-01-04 09:52:00
2017-01-04 09:53:00
2017-01-04 09:54:00
2017-01-04 09:55:00
2017-01-04 09:56:00
2017-01-04 09:57:00
2017-01-04 09:58:00
2017-01-04 09:59:00
2017-01-04 10:00:00
2017-01-04 10:01:00
2017-01-04 10:02:00
2017-01-04 10:03:00


2017-01-05 09:49:00
2017-01-05 09:50:00
2017-01-05 09:51:00
2017-01-05 09:52:00
2017-01-05 09:53:00
2017-01-05 09:54:00
2017-01-05 09:55:00
2017-01-05 09:56:00
2017-01-05 09:57:00
2017-01-05 09:58:00
2017-01-05 09:59:00
2017-01-05 10:00:00
2017-01-05 10:01:00
2017-01-05 10:02:00
2017-01-05 10:03:00
2017-01-05 10:04:00
2017-01-05 10:05:00
2017-01-05 10:06:00
2017-01-05 10:07:00
2017-01-05 10:08:00
2017-01-05 10:09:00
2017-01-05 10:10:00
2017-01-05 10:11:00
2017-01-05 10:12:00
2017-01-05 10:13:00
2017-01-05 10:14:00
2017-01-05 10:15:00
2017-01-05 10:16:00
2017-01-05 10:17:00
2017-01-05 10:18:00
2017-01-05 10:19:00
2017-01-05 10:20:00
2017-01-05 10:21:00
2017-01-05 10:22:00
2017-01-05 10:23:00
2017-01-05 10:24:00
2017-01-05 10:25:00
2017-01-05 10:26:00
2017-01-05 10:27:00
2017-01-05 10:28:00
2017-01-05 10:29:00
2017-01-05 10:30:00
2017-01-05 10:31:00
2017-01-05 10:32:00
2017-01-05 10:33:00
2017-01-05 10:34:00
2017-01-05 10:35:00
2017-01-05 10:36:00
2017-01-05 10:37:00
2017-01-05 10:38:00


...

2017-01-25 10:41:00
2017-01-25 10:42:00
2017-01-25 10:43:00
2017-01-25 10:44:00
2017-01-25 10:45:00
2017-01-25 10:46:00
2017-01-25 10:47:00
2017-01-25 10:48:00
2017-01-25 10:49:00
2017-01-25 10:50:00
2017-01-25 10:51:00
2017-01-25 10:52:00
2017-01-25 10:53:00
2017-01-25 10:54:00
2017-01-25 10:55:00
2017-01-25 10:56:00
2017-01-25 10:57:00
2017-01-25 10:58:00
2017-01-25 10:59:00
2017-01-25 11:00:00
2017-01-25 11:01:00
2017-01-25 11:02:00
2017-01-25 11:03:00
2017-01-25 11:04:00
2017-01-25 11:05:00
2017-01-25 11:06:00
2017-01-25 11:07:00
2017-01-25 11:08:00
2017-01-25 11:09:00
2017-01-25 11:10:00
2017-01-25 11:11:00
2017-01-25 11:12:00
2017-01-25 11:13:00
2017-01-25 11:14:00
2017-01-25 11:15:00
2017-01-25 11:16:00
2017-01-25 11:17:00
2017-01-25 11:18:00
2017-01-25 11:19:00
2017-01-25 11:20:00
2017-01-25 11:21:00
2017-01-25 11:22:00
2017-01-25 11:23:00
2017-01-25 11:24:00
2017-01-25 11:25:00
2017-01-25 11:26:00
2017-01-25 11:27:00
2017-01-25 11:28:00
2017-01-25 11:29:00
2017-01-25 11:30:00


2017-01-27 11:20:00
2017-01-27 11:21:00
2017-01-27 11:22:00
2017-01-27 11:23:00
2017-01-27 11:24:00
2017-01-27 11:25:00
2017-01-27 11:26:00
2017-01-27 11:27:00
2017-01-27 11:28:00
2017-01-27 11:29:00
2017-01-27 11:30:00
2017-01-27 11:31:00
2017-01-27 11:32:00
2017-01-27 11:33:00
2017-01-27 11:34:00
2017-01-27 11:35:00
2017-01-27 11:36:00
2017-01-27 11:37:00
2017-01-27 11:38:00
2017-01-27 11:39:00
2017-01-27 11:40:00
2017-01-27 11:41:00
2017-01-27 11:42:00
2017-01-27 11:43:00
2017-01-27 11:44:00
2017-01-27 11:45:00
2017-01-27 11:46:00
2017-01-27 11:47:00
2017-01-27 11:48:00
2017-01-27 11:49:00
2017-01-27 11:50:00
2017-01-27 11:51:00
2017-01-27 11:52:00
2017-01-27 11:53:00
2017-01-27 11:54:00
2017-01-27 11:55:00
2017-01-27 11:56:00
2017-01-27 11:57:00
2017-01-27 11:58:00
2017-01-27 11:59:00
2017-01-27 12:00:00
2017-01-27 12:01:00
2017-01-27 12:02:00
2017-01-27 12:03:00
2017-01-27 12:04:00
2017-01-27 12:05:00
2017-01-27 12:06:00
2017-01-27 12:07:00
2017-01-27 12:08:00
2017-01-27 12:09:00


2017-01-30 11:42:00
2017-01-30 11:43:00
2017-01-30 11:44:00
2017-01-30 11:45:00
2017-01-30 11:46:00
2017-01-30 11:47:00
2017-01-30 11:48:00
2017-01-30 11:49:00
2017-01-30 11:50:00
2017-01-30 11:51:00
2017-01-30 11:52:00
2017-01-30 11:53:00
2017-01-30 11:54:00
2017-01-30 11:55:00
2017-01-30 11:56:00
2017-01-30 11:57:00
2017-01-30 11:58:00
2017-01-30 11:59:00
2017-01-30 12:00:00
2017-01-30 12:01:00
2017-01-30 12:02:00
2017-01-30 12:03:00
2017-01-30 12:04:00
2017-01-30 12:05:00
2017-01-30 12:06:00
2017-01-30 12:07:00
2017-01-30 12:08:00
2017-01-30 12:09:00
2017-01-30 12:10:00
2017-01-30 12:11:00
2017-01-30 12:12:00
2017-01-30 12:13:00
2017-01-30 12:14:00
2017-01-30 12:15:00
2017-01-30 12:16:00
2017-01-30 12:17:00
2017-01-30 12:18:00
2017-01-30 12:19:00
2017-01-30 12:20:00
2017-01-30 12:21:00
2017-01-30 12:22:00
2017-01-30 12:23:00
2017-01-30 12:24:00
2017-01-30 12:25:00
2017-01-30 12:26:00
2017-01-30 12:27:00
2017-01-30 12:28:00
2017-01-30 12:29:00
2017-01-30 12:30:00
2017-01-30 12:31:00


2017-01-31 11:56:00
2017-01-31 11:57:00
2017-01-31 11:58:00
2017-01-31 11:59:00
2017-01-31 12:00:00
2017-01-31 12:01:00
2017-01-31 12:02:00
2017-01-31 12:03:00
2017-01-31 12:04:00
2017-01-31 12:05:00
2017-01-31 12:06:00
2017-01-31 12:07:00
2017-01-31 12:08:00
2017-01-31 12:09:00
2017-01-31 12:10:00
2017-01-31 12:11:00
2017-01-31 12:12:00
2017-01-31 12:13:00
2017-01-31 12:14:00
2017-01-31 12:15:00
2017-01-31 12:16:00
2017-01-31 12:17:00
2017-01-31 12:18:00
2017-01-31 12:19:00
2017-01-31 12:20:00
2017-01-31 12:21:00
2017-01-31 12:22:00
2017-01-31 12:23:00
2017-01-31 12:24:00
2017-01-31 12:25:00
2017-01-31 12:26:00
2017-01-31 12:27:00
2017-01-31 12:28:00
2017-01-31 12:29:00
2017-01-31 12:30:00
2017-01-31 12:31:00
2017-01-31 12:32:00
2017-01-31 12:33:00
2017-01-31 12:34:00
2017-01-31 12:35:00
2017-01-31 12:36:00
2017-01-31 12:37:00
2017-01-31 12:38:00
2017-01-31 12:39:00
2017-01-31 12:40:00
2017-01-31 12:41:00
2017-01-31 12:42:00
2017-01-31 12:43:00
2017-01-31 12:44:00
2017-01-31 12:45:00


Info: KAA:  Total Pnl: -0.02%  Profit/Loss Ratio: 0.88  Accuracy: 0.49  Score: 0.73 
Info: VKE:  Total Pnl: 0.27%  Profit/Loss Ratio: 1.07  Accuracy: 0.48  Score: nan 
Info: YGC:  Total Pnl: 0.07%  Profit/Loss Ratio: 1.04  Accuracy: 0.48  Score: nan 
Info: OGU:  Total Pnl: -0.04%  Profit/Loss Ratio: 0.87  Accuracy: 0.46  Score: 0.73 
Info: PFK:  Total Pnl: -0.03%  Profit/Loss Ratio: 0.86  Accuracy: 0.45  Score: 0.74 
Info: GFQ:  Total Pnl: -0.04%  Profit/Loss Ratio: 0.86  Accuracy: 0.49  Score: 0.75 
Info: HHK:  Total Pnl: -0.26%  Profit/Loss Ratio: 0.95  Accuracy: 0.47  Score: 1.35 
Info: VSL:  Total Pnl: -0.00%  Profit/Loss Ratio: 1.00  Accuracy: 0.47  Score: 0.75 
Info:  Total Pnl: -1.83%  Score: 0.65  Max Drawdown: 6.18%  RoC: -1.57%  P/L Ratio: 0.97  Accuracy: 0.51  Score: 0.65 


In [39]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
       #  return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: HDK
Processing data for stock: IWU
Processing data for stock: IYU
Processing data for stock: HZT
Processing data for stock: OMP
Processing data for stock: CYD
Processing data for stock: CHV
Processing data for stock: UBF
Processing data for stock: DCO
Processing data for stock: DVV
Processing data for stock: WUT
Processing data for stock: FKI
Processing data for stock: FFS
Processing data for stock: MQK
Processing data for stock: PLX
Processing data for stock: QVE
Processing data for stock: BLR
Processing data for stock: OGU
Processing data for stock: BSN
Processing data for stock: VML
Processing data for stock: KKG
Processing data for stock: PFK
Processing data for stock: MUF
Processing data for stock: XIT
Processing data for stock: YUZ
Processing data for stock: DYE
Processing data for stock: ZEW
Processing data for stock: ZLX
Processing data for stock: FRE
Processing data for stock: GFQ
Processing data for stock: XPV
Processing data for stock: PQS
Processi

2017-01-26 15:07:00
2017-01-26 15:08:00
2017-01-26 15:09:00
2017-01-26 15:10:00
2017-01-26 15:11:00
2017-01-26 15:12:00
2017-01-26 15:13:00
2017-01-26 15:14:00
2017-01-26 15:15:00
2017-01-26 15:16:00
2017-01-26 15:17:00
2017-01-26 15:18:00
2017-01-26 15:19:00
2017-01-26 15:20:00
2017-01-26 15:21:00
2017-01-26 15:22:00
2017-01-26 15:23:00
2017-01-26 15:24:00
2017-01-26 15:25:00
2017-01-26 15:26:00
2017-01-26 15:27:00
2017-01-26 15:28:00
2017-01-27 09:17:00
2017-01-27 09:18:00
2017-01-27 09:19:00
2017-01-27 09:20:00
2017-01-27 09:21:00
2017-01-27 09:22:00
2017-01-27 09:23:00
2017-01-27 09:24:00
2017-01-27 09:25:00
2017-01-27 09:26:00
2017-01-27 09:27:00
2017-01-27 09:28:00
2017-01-27 09:29:00
2017-01-27 09:30:00
2017-01-27 09:31:00
2017-01-27 09:32:00
2017-01-27 09:33:00
2017-01-27 09:34:00
2017-01-27 09:35:00
2017-01-27 09:36:00
2017-01-27 09:37:00
2017-01-27 09:38:00
2017-01-27 09:39:00
2017-01-27 09:40:00
2017-01-27 09:41:00
2017-01-27 09:42:00
2017-01-27 09:43:00
2017-01-27 09:44:00


2017-01-30 09:34:00
2017-01-30 09:35:00
2017-01-30 09:36:00
2017-01-30 09:37:00
2017-01-30 09:38:00
2017-01-30 09:39:00
2017-01-30 09:40:00
2017-01-30 09:41:00
2017-01-30 09:42:00
2017-01-30 09:43:00
2017-01-30 09:44:00
2017-01-30 09:45:00
2017-01-30 09:46:00
2017-01-30 09:47:00
2017-01-30 09:48:00
2017-01-30 09:49:00
2017-01-30 09:50:00
2017-01-30 09:51:00
2017-01-30 09:52:00
2017-01-30 09:53:00
2017-01-30 09:54:00
2017-01-30 09:55:00
2017-01-30 09:56:00
2017-01-30 09:57:00
2017-01-30 09:58:00
2017-01-30 09:59:00
2017-01-30 10:00:00
2017-01-30 10:01:00
2017-01-30 10:02:00
2017-01-30 10:03:00
2017-01-30 10:04:00
2017-01-30 10:05:00
2017-01-30 10:06:00
2017-01-30 10:07:00
2017-01-30 10:08:00
2017-01-30 10:09:00
2017-01-30 10:10:00
2017-01-30 10:11:00
2017-01-30 10:12:00
2017-01-30 10:13:00
2017-01-30 10:14:00
2017-01-30 10:15:00
2017-01-30 10:16:00
2017-01-30 10:17:00
2017-01-30 10:18:00
2017-01-30 10:19:00
2017-01-30 10:20:00
2017-01-30 10:21:00
2017-01-30 10:22:00
2017-01-30 10:23:00


2017-01-31 10:12:00
2017-01-31 10:13:00
2017-01-31 10:14:00
2017-01-31 10:15:00
2017-01-31 10:16:00
2017-01-31 10:17:00
2017-01-31 10:18:00
2017-01-31 10:19:00
2017-01-31 10:20:00
2017-01-31 10:21:00
2017-01-31 10:22:00
2017-01-31 10:23:00
2017-01-31 10:24:00
2017-01-31 10:25:00
2017-01-31 10:26:00
2017-01-31 10:27:00
2017-01-31 10:28:00
2017-01-31 10:29:00
2017-01-31 10:30:00
2017-01-31 10:31:00
2017-01-31 10:32:00
2017-01-31 10:33:00
2017-01-31 10:34:00
2017-01-31 10:35:00
2017-01-31 10:36:00
2017-01-31 10:37:00
2017-01-31 10:38:00
2017-01-31 10:39:00
2017-01-31 10:40:00
2017-01-31 10:41:00
2017-01-31 10:42:00
2017-01-31 10:43:00
2017-01-31 10:44:00
2017-01-31 10:45:00
2017-01-31 10:46:00
2017-01-31 10:47:00
2017-01-31 10:48:00
2017-01-31 10:49:00
2017-01-31 10:50:00
2017-01-31 10:51:00
2017-01-31 10:52:00
2017-01-31 10:53:00
2017-01-31 10:54:00
2017-01-31 10:55:00
2017-01-31 10:56:00
2017-01-31 10:57:00
2017-01-31 10:58:00
2017-01-31 10:59:00
2017-01-31 11:00:00
2017-01-31 11:01:00


2017-02-01 10:51:00
2017-02-01 10:52:00
2017-02-01 10:53:00
2017-02-01 10:54:00
2017-02-01 10:55:00
2017-02-01 10:56:00
2017-02-01 10:57:00
2017-02-01 10:58:00
2017-02-01 10:59:00
2017-02-01 11:00:00
2017-02-01 11:01:00
2017-02-01 11:02:00
2017-02-01 11:03:00
2017-02-01 11:04:00
2017-02-01 11:05:00
2017-02-01 11:06:00
2017-02-01 11:07:00
2017-02-01 11:08:00
2017-02-01 11:09:00
2017-02-01 11:10:00
2017-02-01 11:11:00
2017-02-01 11:12:00
2017-02-01 11:13:00
2017-02-01 11:14:00
2017-02-01 11:15:00
2017-02-01 11:16:00
2017-02-01 11:17:00
2017-02-01 11:18:00
2017-02-01 11:19:00
2017-02-01 11:20:00
2017-02-01 11:21:00
2017-02-01 11:22:00
2017-02-01 11:23:00
2017-02-01 11:24:00
2017-02-01 11:25:00
2017-02-01 11:26:00
2017-02-01 11:27:00
2017-02-01 11:28:00
2017-02-01 11:29:00
2017-02-01 11:30:00
2017-02-01 11:31:00
2017-02-01 11:32:00
2017-02-01 11:33:00
2017-02-01 11:34:00
2017-02-01 11:35:00
2017-02-01 11:36:00
2017-02-01 11:37:00
2017-02-01 11:38:00
2017-02-01 11:39:00
2017-02-01 11:40:00


...

2017-03-03 11:10:00
2017-03-03 11:11:00
2017-03-03 11:12:00
2017-03-03 11:13:00
2017-03-03 11:14:00
2017-03-03 11:15:00
2017-03-03 11:16:00
2017-03-03 11:17:00
2017-03-03 11:18:00
2017-03-03 11:19:00
2017-03-03 11:20:00
2017-03-03 11:21:00
2017-03-03 11:22:00
2017-03-03 11:23:00
2017-03-03 11:24:00
2017-03-03 11:25:00
2017-03-03 11:26:00
2017-03-03 11:27:00
2017-03-03 11:28:00
2017-03-03 11:29:00
2017-03-03 11:30:00
2017-03-03 11:31:00
2017-03-03 11:32:00
2017-03-03 11:33:00
2017-03-03 11:34:00
2017-03-03 11:35:00
2017-03-03 11:36:00
2017-03-03 11:37:00
2017-03-03 11:38:00
2017-03-03 11:39:00
2017-03-03 11:40:00
2017-03-03 11:41:00
2017-03-03 11:42:00
2017-03-03 11:43:00
2017-03-03 11:44:00
2017-03-03 11:45:00
2017-03-03 11:46:00
2017-03-03 11:47:00
2017-03-03 11:48:00
2017-03-03 11:49:00
2017-03-03 11:50:00
2017-03-03 11:51:00
2017-03-03 11:52:00
2017-03-03 11:53:00
2017-03-03 11:54:00
2017-03-03 11:55:00
2017-03-03 11:56:00
2017-03-03 11:57:00
2017-03-03 11:58:00
2017-03-03 11:59:00


2017-03-06 11:47:00
2017-03-06 11:48:00
2017-03-06 11:49:00
2017-03-06 11:50:00
2017-03-06 11:51:00
2017-03-06 11:52:00
2017-03-06 11:53:00
2017-03-06 11:54:00
2017-03-06 11:55:00
2017-03-06 11:56:00
2017-03-06 11:57:00
2017-03-06 11:58:00
2017-03-06 11:59:00
2017-03-06 12:00:00
2017-03-06 12:01:00
2017-03-06 12:02:00
2017-03-06 12:03:00
2017-03-06 12:04:00
2017-03-06 12:05:00
2017-03-06 12:06:00
2017-03-06 12:07:00
2017-03-06 12:08:00
2017-03-06 12:09:00
2017-03-06 12:10:00
2017-03-06 12:11:00
2017-03-06 12:12:00
2017-03-06 12:13:00
2017-03-06 12:14:00
2017-03-06 12:15:00
2017-03-06 12:16:00
2017-03-06 12:17:00
2017-03-06 12:18:00
2017-03-06 12:19:00
2017-03-06 12:20:00
2017-03-06 12:21:00
2017-03-06 12:22:00
2017-03-06 12:23:00
2017-03-06 12:24:00
2017-03-06 12:25:00
2017-03-06 12:26:00
2017-03-06 12:27:00
2017-03-06 12:28:00
2017-03-06 12:29:00
2017-03-06 12:30:00
2017-03-06 12:31:00
2017-03-06 12:32:00
2017-03-06 12:33:00
2017-03-06 12:34:00
2017-03-06 12:35:00
2017-03-06 12:36:00


2017-03-07 12:28:00
2017-03-07 12:29:00
2017-03-07 12:30:00
2017-03-07 12:31:00
2017-03-07 12:32:00
2017-03-07 12:33:00
2017-03-07 12:34:00
2017-03-07 12:35:00
2017-03-07 12:36:00
2017-03-07 12:37:00
2017-03-07 12:38:00
2017-03-07 12:39:00
2017-03-07 12:40:00
2017-03-07 12:41:00
2017-03-07 12:42:00
2017-03-07 12:43:00
2017-03-07 12:44:00
2017-03-07 12:45:00
2017-03-07 12:46:00
2017-03-07 12:47:00
2017-03-07 12:48:00
2017-03-07 12:49:00
2017-03-07 12:50:00
2017-03-07 12:51:00
2017-03-07 12:52:00
2017-03-07 12:53:00
2017-03-07 12:54:00
2017-03-07 12:55:00
2017-03-07 12:56:00
2017-03-07 12:57:00
2017-03-07 12:58:00
2017-03-07 12:59:00
2017-03-07 13:00:00
2017-03-07 13:01:00
2017-03-07 13:02:00
2017-03-07 13:03:00
2017-03-07 13:04:00
2017-03-07 13:05:00
2017-03-07 13:06:00
2017-03-07 13:07:00
2017-03-07 13:08:00
2017-03-07 13:09:00
2017-03-07 13:10:00
2017-03-07 13:11:00
2017-03-07 13:12:00
2017-03-07 13:13:00
2017-03-07 13:14:00
2017-03-07 13:15:00
2017-03-07 13:16:00
2017-03-07 13:17:00


2017-03-08 12:46:00
2017-03-08 12:47:00
2017-03-08 12:48:00
2017-03-08 12:49:00
2017-03-08 12:50:00
2017-03-08 12:51:00
2017-03-08 12:52:00
2017-03-08 12:53:00
2017-03-08 12:54:00
2017-03-08 12:55:00
2017-03-08 12:56:00
2017-03-08 12:57:00
2017-03-08 12:58:00
2017-03-08 12:59:00
2017-03-08 13:00:00
2017-03-08 13:01:00
2017-03-08 13:02:00
2017-03-08 13:03:00
2017-03-08 13:04:00
2017-03-08 13:05:00
2017-03-08 13:06:00
2017-03-08 13:07:00
2017-03-08 13:08:00
2017-03-08 13:09:00
2017-03-08 13:10:00
2017-03-08 13:11:00
2017-03-08 13:12:00
2017-03-08 13:13:00
2017-03-08 13:14:00
2017-03-08 13:15:00
2017-03-08 13:16:00
2017-03-08 13:17:00
2017-03-08 13:18:00
2017-03-08 13:19:00
2017-03-08 13:20:00
2017-03-08 13:21:00
2017-03-08 13:22:00
2017-03-08 13:23:00
2017-03-08 13:24:00
2017-03-08 13:25:00
2017-03-08 13:26:00
2017-03-08 13:27:00
2017-03-08 13:28:00
2017-03-08 13:29:00
2017-03-08 13:30:00
2017-03-08 13:31:00
2017-03-08 13:32:00
2017-03-08 13:33:00
2017-03-08 13:34:00
2017-03-08 13:35:00


2017-03-09 13:25:00
2017-03-09 13:26:00
2017-03-09 13:27:00
2017-03-09 13:28:00
2017-03-09 13:29:00
2017-03-09 13:30:00
2017-03-09 13:31:00
2017-03-09 13:32:00
2017-03-09 13:33:00
2017-03-09 13:34:00
2017-03-09 13:35:00
2017-03-09 13:36:00
2017-03-09 13:37:00
2017-03-09 13:38:00
2017-03-09 13:39:00
2017-03-09 13:40:00
2017-03-09 13:41:00
2017-03-09 13:42:00
2017-03-09 13:43:00
2017-03-09 13:44:00
2017-03-09 13:45:00
2017-03-09 13:46:00
2017-03-09 13:47:00
2017-03-09 13:48:00
2017-03-09 13:49:00
2017-03-09 13:50:00
2017-03-09 13:51:00
2017-03-09 13:52:00
2017-03-09 13:53:00
2017-03-09 13:54:00
2017-03-09 13:55:00
2017-03-09 13:56:00
2017-03-09 13:57:00
2017-03-09 13:58:00
2017-03-09 13:59:00
2017-03-09 14:00:00
2017-03-09 14:01:00
2017-03-09 14:02:00
2017-03-09 14:03:00
2017-03-09 14:04:00
2017-03-09 14:05:00
2017-03-09 14:06:00
2017-03-09 14:07:00
2017-03-09 14:08:00
2017-03-09 14:09:00
2017-03-09 14:10:00
2017-03-09 14:11:00
2017-03-09 14:12:00
2017-03-09 14:13:00
2017-03-09 14:14:00


In [40]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_2"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
       #  return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)

Processing data for stock: HDK
Processing data for stock: IWU
Processing data for stock: IYU
Processing data for stock: HZT
Processing data for stock: OMP
Processing data for stock: CYD
Processing data for stock: CHV
Processing data for stock: UBF
Processing data for stock: DCO
Processing data for stock: DVV
Processing data for stock: WUT
Processing data for stock: FKI
Processing data for stock: FFS
Processing data for stock: MQK
Processing data for stock: PLX
Processing data for stock: QVE
Processing data for stock: BLR
Processing data for stock: OGU
Processing data for stock: BSN
Processing data for stock: VML
Processing data for stock: KKG
Processing data for stock: PFK
Processing data for stock: MUF
Processing data for stock: XIT
Processing data for stock: YUZ
Processing data for stock: DYE
Processing data for stock: ZEW
Processing data for stock: ZLX
Processing data for stock: FRE
Processing data for stock: GFQ
Processing data for stock: XPV
Processing data for stock: PQS
Processi

2017-02-06 14:33:00
2017-02-06 14:34:00
2017-02-06 14:35:00
2017-02-06 14:36:00
2017-02-06 14:37:00
2017-02-06 14:38:00
2017-02-06 14:39:00
2017-02-06 14:40:00
2017-02-06 14:41:00
2017-02-06 14:42:00
2017-02-06 14:43:00
2017-02-06 14:44:00
2017-02-06 14:45:00
2017-02-06 14:46:00
2017-02-06 14:47:00
2017-02-06 14:48:00
2017-02-06 14:49:00
2017-02-06 14:50:00
2017-02-06 14:51:00
2017-02-06 14:52:00
2017-02-06 14:53:00
2017-02-06 14:54:00
2017-02-06 14:55:00
2017-02-06 14:56:00
2017-02-06 14:57:00
2017-02-06 14:58:00
2017-02-06 14:59:00
2017-02-06 15:00:00
2017-02-06 15:01:00
2017-02-06 15:02:00
2017-02-06 15:03:00
2017-02-06 15:04:00
2017-02-06 15:05:00
2017-02-06 15:06:00
2017-02-06 15:07:00
2017-02-06 15:08:00
2017-02-06 15:09:00
2017-02-06 15:10:00
2017-02-06 15:11:00
2017-02-06 15:12:00
2017-02-06 15:13:00
2017-02-06 15:14:00
2017-02-06 15:15:00
2017-02-06 15:16:00
2017-02-06 15:17:00
2017-02-06 15:18:00
2017-02-06 15:19:00
2017-02-06 15:20:00
2017-02-06 15:21:00
2017-02-06 15:22:00


2017-02-07 14:39:00
2017-02-07 14:40:00
2017-02-07 14:41:00
2017-02-07 14:42:00
2017-02-07 14:43:00
2017-02-07 14:44:00
2017-02-07 14:45:00
2017-02-07 14:46:00
2017-02-07 14:47:00
2017-02-07 14:48:00
2017-02-07 14:49:00
2017-02-07 14:50:00
2017-02-07 14:51:00
2017-02-07 14:52:00
2017-02-07 14:53:00
2017-02-07 14:54:00
2017-02-07 14:55:00
2017-02-07 14:56:00
2017-02-07 14:57:00
2017-02-07 14:58:00
2017-02-07 14:59:00
2017-02-07 15:00:00
2017-02-07 15:01:00
2017-02-07 15:02:00
2017-02-07 15:03:00
2017-02-07 15:04:00
2017-02-07 15:05:00
2017-02-07 15:06:00
2017-02-07 15:07:00
2017-02-07 15:08:00
2017-02-07 15:09:00
2017-02-07 15:10:00
2017-02-07 15:11:00
2017-02-07 15:12:00
2017-02-07 15:13:00
2017-02-07 15:14:00
2017-02-07 15:15:00
2017-02-07 15:16:00
2017-02-07 15:17:00
2017-02-07 15:18:00
2017-02-07 15:19:00
2017-02-07 15:20:00
2017-02-07 15:21:00
2017-02-07 15:22:00
2017-02-07 15:23:00
2017-02-07 15:24:00
2017-02-07 15:25:00
2017-02-07 15:26:00
2017-02-07 15:27:00
2017-02-07 15:28:00


2017-02-08 15:08:00
2017-02-08 15:09:00
2017-02-08 15:10:00
2017-02-08 15:11:00
2017-02-08 15:12:00
2017-02-08 15:13:00
2017-02-08 15:14:00
2017-02-08 15:15:00
2017-02-08 15:16:00
2017-02-08 15:17:00
2017-02-08 15:18:00
2017-02-08 15:19:00
2017-02-08 15:20:00
2017-02-08 15:21:00
2017-02-08 15:22:00
2017-02-08 15:23:00
2017-02-08 15:24:00
2017-02-08 15:25:00
2017-02-08 15:26:00
2017-02-08 15:27:00
2017-02-08 15:28:00
2017-02-09 09:17:00
2017-02-09 09:18:00
2017-02-09 09:19:00
2017-02-09 09:20:00
2017-02-09 09:21:00
2017-02-09 09:22:00
2017-02-09 09:23:00
2017-02-09 09:24:00
2017-02-09 09:25:00
2017-02-09 09:26:00
2017-02-09 09:27:00
2017-02-09 09:28:00
2017-02-09 09:29:00
2017-02-09 09:30:00
2017-02-09 09:31:00
2017-02-09 09:32:00
2017-02-09 09:33:00
2017-02-09 09:34:00
2017-02-09 09:35:00
2017-02-09 09:36:00
2017-02-09 09:37:00
2017-02-09 09:38:00
2017-02-09 09:39:00
2017-02-09 09:40:00
2017-02-09 09:41:00
2017-02-09 09:42:00
2017-02-09 09:43:00
2017-02-09 09:44:00
2017-02-09 09:45:00


2017-02-10 10:35:00
2017-02-10 10:36:00
2017-02-10 10:37:00
2017-02-10 10:38:00
2017-02-10 10:39:00
2017-02-10 10:40:00
2017-02-10 10:41:00
2017-02-10 10:42:00
2017-02-10 10:43:00
2017-02-10 10:44:00
2017-02-10 10:45:00
2017-02-10 10:46:00
2017-02-10 10:47:00
2017-02-10 10:48:00
2017-02-10 10:49:00
2017-02-10 10:50:00
2017-02-10 10:51:00
2017-02-10 10:52:00
2017-02-10 10:53:00
2017-02-10 10:54:00
2017-02-10 10:55:00
2017-02-10 10:56:00
2017-02-10 10:57:00
2017-02-10 10:58:00
2017-02-10 10:59:00
2017-02-10 11:00:00
2017-02-10 11:01:00
2017-02-10 11:02:00
2017-02-10 11:03:00
2017-02-10 11:04:00
2017-02-10 11:05:00
2017-02-10 11:06:00
2017-02-10 11:07:00
2017-02-10 11:08:00
2017-02-10 11:09:00
2017-02-10 11:10:00
2017-02-10 11:11:00
2017-02-10 11:12:00
2017-02-10 11:13:00
2017-02-10 11:14:00
2017-02-10 11:15:00
2017-02-10 11:16:00
2017-02-10 11:17:00
2017-02-10 11:18:00
2017-02-10 11:19:00
2017-02-10 11:20:00
2017-02-10 11:21:00
2017-02-10 11:22:00
2017-02-10 11:23:00
2017-02-10 11:24:00


...

2017-03-16 11:11:00
2017-03-16 11:12:00
2017-03-16 11:13:00
2017-03-16 11:14:00
2017-03-16 11:15:00
2017-03-16 11:16:00
2017-03-16 11:17:00
2017-03-16 11:18:00
2017-03-16 11:19:00
2017-03-16 11:20:00
2017-03-16 11:21:00
2017-03-16 11:22:00
2017-03-16 11:23:00
2017-03-16 11:24:00
2017-03-16 11:25:00
2017-03-16 11:26:00
2017-03-16 11:27:00
2017-03-16 11:28:00
2017-03-16 11:29:00
2017-03-16 11:30:00
2017-03-16 11:31:00
2017-03-16 11:32:00
2017-03-16 11:33:00
2017-03-16 11:34:00
2017-03-16 11:35:00
2017-03-16 11:36:00
2017-03-16 11:37:00
2017-03-16 11:38:00
2017-03-16 11:39:00
2017-03-16 11:40:00
2017-03-16 11:41:00
2017-03-16 11:42:00
2017-03-16 11:43:00
2017-03-16 11:44:00
2017-03-16 11:45:00
2017-03-16 11:46:00
2017-03-16 11:47:00
2017-03-16 11:48:00
2017-03-16 11:49:00
2017-03-16 11:50:00
2017-03-16 11:51:00
2017-03-16 11:52:00
2017-03-16 11:53:00
2017-03-16 11:54:00
2017-03-16 11:55:00
2017-03-16 11:56:00
2017-03-16 11:57:00
2017-03-16 11:58:00
2017-03-16 11:59:00
2017-03-16 12:00:00


2017-03-17 12:35:00
2017-03-17 12:36:00
2017-03-17 12:37:00
2017-03-17 12:38:00
2017-03-17 12:39:00
2017-03-17 12:40:00
2017-03-17 12:41:00
2017-03-17 12:42:00
2017-03-17 12:43:00
2017-03-17 12:44:00
2017-03-17 12:45:00
2017-03-17 12:46:00
2017-03-17 12:47:00
2017-03-17 12:48:00
2017-03-17 12:49:00
2017-03-17 12:50:00
2017-03-17 12:51:00
2017-03-17 12:52:00
2017-03-17 12:53:00
2017-03-17 12:54:00
2017-03-17 12:55:00
2017-03-17 12:56:00
2017-03-17 12:57:00
2017-03-17 12:58:00
2017-03-17 12:59:00
2017-03-17 13:00:00
2017-03-17 13:01:00
2017-03-17 13:02:00
2017-03-17 13:03:00
2017-03-17 13:04:00
2017-03-17 13:05:00
2017-03-17 13:06:00
2017-03-17 13:07:00
2017-03-17 13:08:00
2017-03-17 13:09:00
2017-03-17 13:10:00
2017-03-17 13:11:00
2017-03-17 13:12:00
2017-03-17 13:13:00
2017-03-17 13:14:00
2017-03-17 13:15:00
2017-03-17 13:16:00
2017-03-17 13:17:00
2017-03-17 13:18:00
2017-03-17 13:19:00
2017-03-17 13:20:00
2017-03-17 13:21:00
2017-03-17 13:22:00
2017-03-17 13:23:00
2017-03-17 13:24:00


2017-03-22 13:17:00
2017-03-22 13:18:00
2017-03-22 13:19:00
2017-03-22 13:20:00
2017-03-22 13:21:00
2017-03-22 13:22:00
2017-03-22 13:23:00
2017-03-22 13:24:00
2017-03-22 13:25:00
2017-03-22 13:26:00
2017-03-22 13:27:00
2017-03-22 13:28:00
2017-03-22 13:29:00
2017-03-22 13:30:00
2017-03-22 13:31:00
2017-03-22 13:32:00
2017-03-22 13:33:00
2017-03-22 13:34:00
2017-03-22 13:35:00
2017-03-22 13:36:00
2017-03-22 13:37:00
2017-03-22 13:38:00
2017-03-22 13:39:00
2017-03-22 13:40:00
2017-03-22 13:41:00
2017-03-22 13:42:00
2017-03-22 13:43:00
2017-03-22 13:44:00
2017-03-22 13:45:00
2017-03-22 13:46:00
2017-03-22 13:47:00
2017-03-22 13:48:00
2017-03-22 13:49:00
2017-03-22 13:50:00
2017-03-22 13:51:00
2017-03-22 13:52:00
2017-03-22 13:53:00
2017-03-22 13:54:00
2017-03-22 13:55:00
2017-03-22 13:56:00
2017-03-22 13:57:00
2017-03-22 13:58:00
2017-03-22 13:59:00
2017-03-22 14:00:00
2017-03-22 14:01:00
2017-03-22 14:02:00
2017-03-22 14:03:00
2017-03-22 14:04:00
2017-03-22 14:05:00
2017-03-22 14:06:00


2017-03-29 14:33:00
2017-03-29 14:34:00
2017-03-29 14:35:00
2017-03-29 14:36:00
2017-03-29 14:37:00
2017-03-29 14:38:00
2017-03-29 14:39:00
2017-03-29 14:40:00
2017-03-29 14:41:00
2017-03-29 14:42:00
2017-03-29 14:43:00
2017-03-29 14:44:00
2017-03-29 14:45:00
2017-03-29 14:46:00
2017-03-29 14:47:00
2017-03-29 14:48:00
2017-03-29 14:49:00
2017-03-29 14:50:00
2017-03-29 14:51:00
2017-03-29 14:52:00
2017-03-29 14:53:00
2017-03-29 14:54:00
2017-03-29 14:55:00
2017-03-29 14:56:00
2017-03-29 14:57:00
2017-03-29 14:58:00
2017-03-29 14:59:00
2017-03-29 15:00:00
2017-03-29 15:01:00
2017-03-29 15:02:00
2017-03-29 15:03:00
2017-03-29 15:04:00
2017-03-29 15:05:00
2017-03-29 15:06:00
2017-03-29 15:07:00
2017-03-29 15:08:00
2017-03-29 15:09:00
2017-03-29 15:10:00
2017-03-29 15:11:00
2017-03-29 15:12:00
2017-03-29 15:13:00
2017-03-29 15:14:00
2017-03-29 15:15:00
2017-03-29 15:16:00
2017-03-29 15:17:00
2017-03-29 15:18:00
2017-03-29 15:19:00
2017-03-29 15:20:00
2017-03-29 15:21:00
2017-03-29 15:22:00


Info: OMP:  Total Pnl: -0.02%  Profit/Loss Ratio: 0.88  Accuracy: 0.47  Score: 0.72 
Info: ZEW:  Total Pnl: -0.47%  Profit/Loss Ratio: 0.95  Accuracy: 0.49  Score: 1.07 
Info: KKG:  Total Pnl: -0.02%  Profit/Loss Ratio: 0.81  Accuracy: 0.47  Score: 0.72 
Info: UWD:  Total Pnl: -0.60%  Profit/Loss Ratio: 0.92  Accuracy: 0.49  Score: 1.08 
Info: VSL:  Total Pnl: -0.16%  Profit/Loss Ratio: 0.93  Accuracy: 0.47  Score: 0.78 
Info: FFA:  Total Pnl: -0.03%  Profit/Loss Ratio: 0.83  Accuracy: 0.48  Score: 0.72 
Info: OED:  Total Pnl: 0.38%  Profit/Loss Ratio: 1.04  Accuracy: 0.49  Score: nan 
Info:  Total Pnl: -3.20%  Score: 0.79  Max Drawdown: 4.43%  RoC: -2.46%  P/L Ratio: 0.95  Accuracy: 0.50  Score: 0.79 


In [41]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_3"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
       #  return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: HDK
Processing data for stock: IWU
Processing data for stock: IYU
Processing data for stock: HZT
Processing data for stock: OMP
Processing data for stock: CYD
Processing data for stock: CHV
Processing data for stock: UBF
Processing data for stock: DCO
Processing data for stock: DVV
Processing data for stock: WUT
Processing data for stock: FKI
Processing data for stock: FFS
Processing data for stock: MQK
Processing data for stock: PLX
Processing data for stock: QVE
Processing data for stock: BLR
Processing data for stock: OGU
Processing data for stock: BSN
Processing data for stock: VML
Processing data for stock: KKG
Processing data for stock: PFK
Processing data for stock: MUF
Processing data for stock: XIT
Processing data for stock: YUZ
Processing data for stock: DYE
Processing data for stock: ZEW
Processing data for stock: ZLX
Processing data for stock: FRE
Processing data for stock: GFQ
Processing data for stock: XPV
Processing data for stock: PQS
Processi

2017-01-02 14:31:00
2017-01-02 14:32:00
2017-01-02 14:33:00
2017-01-02 14:34:00
2017-01-02 14:35:00
2017-01-02 14:36:00
2017-01-02 14:37:00
2017-01-02 14:38:00
2017-01-02 14:39:00
2017-01-02 14:40:00
2017-01-02 14:41:00
2017-01-02 14:42:00
2017-01-02 14:43:00
2017-01-02 14:44:00
2017-01-02 14:45:00
2017-01-02 14:46:00
2017-01-02 14:47:00
2017-01-02 14:48:00
2017-01-02 14:49:00
2017-01-02 14:50:00
2017-01-02 14:51:00
2017-01-02 14:52:00
2017-01-02 14:53:00
2017-01-02 14:54:00
2017-01-02 14:55:00
2017-01-02 14:56:00
2017-01-02 14:57:00
2017-01-02 14:58:00
2017-01-02 14:59:00
2017-01-02 15:00:00
2017-01-02 15:01:00
2017-01-02 15:02:00
2017-01-02 15:03:00
2017-01-02 15:04:00
2017-01-02 15:05:00
2017-01-02 15:06:00
2017-01-02 15:07:00
2017-01-02 15:08:00
2017-01-02 15:09:00
2017-01-02 15:10:00
2017-01-02 15:11:00
2017-01-02 15:12:00
2017-01-02 15:13:00
2017-01-02 15:14:00
2017-01-02 15:15:00
2017-01-02 15:16:00
2017-01-02 15:17:00
2017-01-02 15:18:00
2017-01-02 15:19:00
2017-01-02 15:20:00


2017-01-03 15:10:00
2017-01-03 15:11:00
2017-01-03 15:12:00
2017-01-03 15:13:00
2017-01-03 15:14:00
2017-01-03 15:15:00
2017-01-03 15:16:00
2017-01-03 15:17:00
2017-01-03 15:18:00
2017-01-03 15:19:00
2017-01-03 15:20:00
2017-01-03 15:21:00
2017-01-03 15:22:00
2017-01-03 15:23:00
2017-01-03 15:24:00
2017-01-03 15:25:00
2017-01-03 15:26:00
2017-01-03 15:27:00
2017-01-03 15:28:00
2017-01-04 09:17:00
2017-01-04 09:18:00
2017-01-04 09:19:00
2017-01-04 09:20:00
2017-01-04 09:21:00
2017-01-04 09:22:00
2017-01-04 09:23:00
2017-01-04 09:24:00
2017-01-04 09:25:00
2017-01-04 09:26:00
2017-01-04 09:27:00
2017-01-04 09:28:00
2017-01-04 09:29:00
2017-01-04 09:30:00
2017-01-04 09:31:00
2017-01-04 09:32:00
2017-01-04 09:33:00
2017-01-04 09:34:00
2017-01-04 09:35:00
2017-01-04 09:36:00
2017-01-04 09:37:00
2017-01-04 09:38:00
2017-01-04 09:39:00
2017-01-04 09:40:00
2017-01-04 09:41:00
2017-01-04 09:42:00
2017-01-04 09:43:00
2017-01-04 09:44:00
2017-01-04 09:45:00
2017-01-04 09:46:00
2017-01-04 09:47:00


2017-01-05 09:37:00
2017-01-05 09:38:00
2017-01-05 09:39:00
2017-01-05 09:40:00
2017-01-05 09:41:00
2017-01-05 09:42:00
2017-01-05 09:43:00
2017-01-05 09:44:00
2017-01-05 09:45:00
2017-01-05 09:46:00
2017-01-05 09:47:00
2017-01-05 09:48:00
2017-01-05 09:49:00
2017-01-05 09:50:00
2017-01-05 09:51:00
2017-01-05 09:52:00
2017-01-05 09:53:00
2017-01-05 09:54:00
2017-01-05 09:55:00
2017-01-05 09:56:00
2017-01-05 09:57:00
2017-01-05 09:58:00
2017-01-05 09:59:00
2017-01-05 10:00:00
2017-01-05 10:01:00
2017-01-05 10:02:00
2017-01-05 10:03:00
2017-01-05 10:04:00
2017-01-05 10:05:00
2017-01-05 10:06:00
2017-01-05 10:07:00
2017-01-05 10:08:00
2017-01-05 10:09:00
2017-01-05 10:10:00
2017-01-05 10:11:00
2017-01-05 10:12:00
2017-01-05 10:13:00
2017-01-05 10:14:00
2017-01-05 10:15:00
2017-01-05 10:16:00
2017-01-05 10:17:00
2017-01-05 10:18:00
2017-01-05 10:19:00
2017-01-05 10:20:00
2017-01-05 10:21:00
2017-01-05 10:22:00
2017-01-05 10:23:00
2017-01-05 10:24:00
2017-01-05 10:25:00
2017-01-05 10:26:00


2017-01-06 10:18:00
2017-01-06 10:19:00
2017-01-06 10:20:00
2017-01-06 10:21:00
2017-01-06 10:22:00
2017-01-06 10:23:00
2017-01-06 10:24:00
2017-01-06 10:25:00
2017-01-06 10:26:00
2017-01-06 10:27:00
2017-01-06 10:28:00
2017-01-06 10:29:00
2017-01-06 10:30:00
2017-01-06 10:31:00
2017-01-06 10:32:00
2017-01-06 10:33:00
2017-01-06 10:34:00
2017-01-06 10:35:00
2017-01-06 10:36:00
2017-01-06 10:37:00
2017-01-06 10:38:00
2017-01-06 10:39:00
2017-01-06 10:40:00
2017-01-06 10:41:00
2017-01-06 10:42:00
2017-01-06 10:43:00
2017-01-06 10:44:00
2017-01-06 10:45:00
2017-01-06 10:46:00
2017-01-06 10:47:00
2017-01-06 10:48:00
2017-01-06 10:49:00
2017-01-06 10:50:00
2017-01-06 10:51:00
2017-01-06 10:52:00
2017-01-06 10:53:00
2017-01-06 10:54:00
2017-01-06 10:55:00
2017-01-06 10:56:00
2017-01-06 10:57:00
2017-01-06 10:58:00
2017-01-06 10:59:00
2017-01-06 11:00:00
2017-01-06 11:01:00
2017-01-06 11:02:00
2017-01-06 11:03:00
2017-01-06 11:04:00
2017-01-06 11:05:00
2017-01-06 11:06:00
2017-01-06 11:07:00


...

2017-01-24 11:16:00
2017-01-24 11:17:00
2017-01-24 11:18:00
2017-01-24 11:19:00
2017-01-24 11:20:00
2017-01-24 11:21:00
2017-01-24 11:22:00
2017-01-24 11:23:00
2017-01-24 11:24:00
2017-01-24 11:25:00
2017-01-24 11:26:00
2017-01-24 11:27:00
2017-01-24 11:28:00
2017-01-24 11:29:00
2017-01-24 11:30:00
2017-01-24 11:31:00
2017-01-24 11:32:00
2017-01-24 11:33:00
2017-01-24 11:34:00
2017-01-24 11:35:00
2017-01-24 11:36:00
2017-01-24 11:37:00
2017-01-24 11:38:00
2017-01-24 11:39:00
2017-01-24 11:40:00
2017-01-24 11:41:00
2017-01-24 11:42:00
2017-01-24 11:43:00
2017-01-24 11:44:00
2017-01-24 11:45:00
2017-01-24 11:46:00
2017-01-24 11:47:00
2017-01-24 11:48:00
2017-01-24 11:49:00
2017-01-24 11:50:00
2017-01-24 11:51:00
2017-01-24 11:52:00
2017-01-24 11:53:00
2017-01-24 11:54:00
2017-01-24 11:55:00
2017-01-24 11:56:00
2017-01-24 11:57:00
2017-01-24 11:58:00
2017-01-24 11:59:00
2017-01-24 12:00:00
2017-01-24 12:01:00
2017-01-24 12:02:00
2017-01-24 12:03:00
2017-01-24 12:04:00
2017-01-24 12:05:00


2017-01-25 11:57:00
2017-01-25 11:58:00
2017-01-25 11:59:00
2017-01-25 12:00:00
2017-01-25 12:01:00
2017-01-25 12:02:00
2017-01-25 12:03:00
2017-01-25 12:04:00
2017-01-25 12:05:00
2017-01-25 12:06:00
2017-01-25 12:07:00
2017-01-25 12:08:00
2017-01-25 12:09:00
2017-01-25 12:10:00
2017-01-25 12:11:00
2017-01-25 12:12:00
2017-01-25 12:13:00
2017-01-25 12:14:00
2017-01-25 12:15:00
2017-01-25 12:16:00
2017-01-25 12:17:00
2017-01-25 12:18:00
2017-01-25 12:19:00
2017-01-25 12:20:00
2017-01-25 12:21:00
2017-01-25 12:22:00
2017-01-25 12:23:00
2017-01-25 12:24:00
2017-01-25 12:25:00
2017-01-25 12:26:00
2017-01-25 12:27:00
2017-01-25 12:28:00
2017-01-25 12:29:00
2017-01-25 12:30:00
2017-01-25 12:31:00
2017-01-25 12:32:00
2017-01-25 12:33:00
2017-01-25 12:34:00
2017-01-25 12:35:00
2017-01-25 12:36:00
2017-01-25 12:37:00
2017-01-25 12:38:00
2017-01-25 12:39:00
2017-01-25 12:40:00
2017-01-25 12:41:00
2017-01-25 12:42:00
2017-01-25 12:43:00
2017-01-25 12:44:00
2017-01-25 12:45:00
2017-01-25 12:46:00


2017-01-27 12:39:00
2017-01-27 12:40:00
2017-01-27 12:41:00
2017-01-27 12:42:00
2017-01-27 12:43:00
2017-01-27 12:44:00
2017-01-27 12:45:00
2017-01-27 12:46:00
2017-01-27 12:47:00
2017-01-27 12:48:00
2017-01-27 12:49:00
2017-01-27 12:50:00
2017-01-27 12:51:00
2017-01-27 12:52:00
2017-01-27 12:53:00
2017-01-27 12:54:00
2017-01-27 12:55:00
2017-01-27 12:56:00
2017-01-27 12:57:00
2017-01-27 12:58:00
2017-01-27 12:59:00
2017-01-27 13:00:00
2017-01-27 13:01:00
2017-01-27 13:02:00
2017-01-27 13:03:00
2017-01-27 13:04:00
2017-01-27 13:05:00
2017-01-27 13:06:00
2017-01-27 13:07:00
2017-01-27 13:08:00
2017-01-27 13:09:00
2017-01-27 13:10:00
2017-01-27 13:11:00
2017-01-27 13:12:00
2017-01-27 13:13:00
2017-01-27 13:14:00
2017-01-27 13:15:00
2017-01-27 13:16:00
2017-01-27 13:17:00
2017-01-27 13:18:00
2017-01-27 13:19:00
2017-01-27 13:20:00
2017-01-27 13:21:00
2017-01-27 13:22:00
2017-01-27 13:23:00
2017-01-27 13:24:00
2017-01-27 13:25:00
2017-01-27 13:26:00
2017-01-27 13:27:00
2017-01-27 13:28:00


2017-01-30 13:14:00
2017-01-30 13:15:00
2017-01-30 13:16:00
2017-01-30 13:17:00
2017-01-30 13:18:00
2017-01-30 13:19:00
2017-01-30 13:20:00
2017-01-30 13:21:00
2017-01-30 13:22:00
2017-01-30 13:23:00
2017-01-30 13:24:00
2017-01-30 13:25:00
2017-01-30 13:26:00
2017-01-30 13:27:00
2017-01-30 13:28:00
2017-01-30 13:29:00
2017-01-30 13:30:00
2017-01-30 13:31:00
2017-01-30 13:32:00
2017-01-30 13:33:00
2017-01-30 13:34:00
2017-01-30 13:35:00
2017-01-30 13:36:00
2017-01-30 13:37:00
2017-01-30 13:38:00
2017-01-30 13:39:00
2017-01-30 13:40:00
2017-01-30 13:41:00
2017-01-30 13:42:00
2017-01-30 13:43:00
2017-01-30 13:44:00
2017-01-30 13:45:00
2017-01-30 13:46:00
2017-01-30 13:47:00
2017-01-30 13:48:00
2017-01-30 13:49:00
2017-01-30 13:50:00
2017-01-30 13:51:00
2017-01-30 13:52:00
2017-01-30 13:53:00
2017-01-30 13:54:00
2017-01-30 13:55:00
2017-01-30 13:56:00
2017-01-30 13:57:00
2017-01-30 13:58:00
2017-01-30 13:59:00
2017-01-30 14:00:00
2017-01-30 14:01:00
2017-01-30 14:02:00
2017-01-30 14:03:00


2017-01-31 13:53:00
2017-01-31 13:54:00
2017-01-31 13:55:00
2017-01-31 13:56:00
2017-01-31 13:57:00
2017-01-31 13:58:00
2017-01-31 13:59:00
2017-01-31 14:00:00
2017-01-31 14:01:00
2017-01-31 14:02:00
2017-01-31 14:03:00
2017-01-31 14:04:00
2017-01-31 14:05:00
2017-01-31 14:06:00
2017-01-31 14:07:00
2017-01-31 14:08:00
2017-01-31 14:09:00
2017-01-31 14:10:00
2017-01-31 14:11:00
2017-01-31 14:12:00
2017-01-31 14:13:00
2017-01-31 14:14:00
2017-01-31 14:15:00
2017-01-31 14:16:00
2017-01-31 14:17:00
2017-01-31 14:18:00
2017-01-31 14:19:00
2017-01-31 14:20:00
2017-01-31 14:21:00
2017-01-31 14:22:00
2017-01-31 14:23:00
2017-01-31 14:24:00
2017-01-31 14:25:00
2017-01-31 14:26:00
2017-01-31 14:27:00
2017-01-31 14:28:00
2017-01-31 14:29:00
2017-01-31 14:30:00
2017-01-31 14:31:00
2017-01-31 14:32:00
2017-01-31 14:33:00
2017-01-31 14:34:00
2017-01-31 14:35:00
2017-01-31 14:36:00
2017-01-31 14:37:00
2017-01-31 14:38:00
2017-01-31 14:39:00
2017-01-31 14:40:00
2017-01-31 14:41:00
2017-01-31 14:42:00


In [42]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_3"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['BSN',
 'DCO',
 'DYE',
 'FFA',
 'FFS',
 'HDK',
 'HZT',
 'ILW',
 'IMC',
 'IWU',
 'IYU',
 'KAA',
 'KKG',
 'LPQ',
 'NNA',
 'NSL',
 'OMP',
 'QTY',
 'QVE',
 'RGG',
 'WTJ',
 'WUT',
 'XPV',
 'XYR']
       # return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
       #  return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: BSN
Processing data for stock: DCO
Processing data for stock: DYE
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: HDK
Processing data for stock: HZT
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IWU
Processing data for stock: IYU
Processing data for stock: KAA
Processing data for stock: KKG
Processing data for stock: LPQ
Processing data for stock: NNA
Processing data for stock: NSL
Processing data for stock: OMP
Processing data for stock: QTY
Processing data for stock: QVE
Processing data for stock: RGG
Processing data for stock: WTJ
Processing data for stock: WUT
Processing data for stock: XPV
Processing data for stock: XYR
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-02 09:17:00
2017-01-02 09:18:00
2017-01-02 09:19:00
2017-01-02 09:20:00
2017-01-02 09:21:00
2017-01-02 09:22:00
2017-0

2017-01-02 15:25:00
2017-01-02 15:26:00
2017-01-02 15:27:00
2017-01-02 15:28:00
2017-01-03 09:17:00
2017-01-03 09:18:00
2017-01-03 09:19:00
2017-01-03 09:20:00
2017-01-03 09:21:00
2017-01-03 09:22:00
2017-01-03 09:23:00
2017-01-03 09:24:00
2017-01-03 09:25:00
2017-01-03 09:26:00
2017-01-03 09:27:00
2017-01-03 09:28:00
2017-01-03 09:29:00
2017-01-03 09:30:00
2017-01-03 09:31:00
2017-01-03 09:32:00
2017-01-03 09:33:00
2017-01-03 09:34:00
2017-01-03 09:35:00
2017-01-03 09:36:00
2017-01-03 09:37:00
2017-01-03 09:38:00
2017-01-03 09:39:00
2017-01-03 09:40:00
2017-01-03 09:41:00
2017-01-03 09:42:00
2017-01-03 09:43:00
2017-01-03 09:44:00
2017-01-03 09:45:00
2017-01-03 09:46:00
2017-01-03 09:47:00
2017-01-03 09:48:00
2017-01-03 09:49:00
2017-01-03 09:50:00
2017-01-03 09:51:00
2017-01-03 09:52:00
2017-01-03 09:53:00
2017-01-03 09:54:00
2017-01-03 09:55:00
2017-01-03 09:56:00
2017-01-03 09:57:00
2017-01-03 09:58:00
2017-01-03 09:59:00
2017-01-03 10:00:00
2017-01-03 10:01:00
2017-01-03 10:02:00


2017-01-04 09:52:00
2017-01-04 09:53:00
2017-01-04 09:54:00
2017-01-04 09:55:00
2017-01-04 09:56:00
2017-01-04 09:57:00
2017-01-04 09:58:00
2017-01-04 09:59:00
2017-01-04 10:00:00
2017-01-04 10:01:00
2017-01-04 10:02:00
2017-01-04 10:03:00
2017-01-04 10:04:00
2017-01-04 10:05:00
2017-01-04 10:06:00
2017-01-04 10:07:00
2017-01-04 10:08:00
2017-01-04 10:09:00
2017-01-04 10:10:00
2017-01-04 10:11:00
2017-01-04 10:12:00
2017-01-04 10:13:00
2017-01-04 10:14:00
2017-01-04 10:15:00
2017-01-04 10:16:00
2017-01-04 10:17:00
2017-01-04 10:18:00
2017-01-04 10:19:00
2017-01-04 10:20:00
2017-01-04 10:21:00
2017-01-04 10:22:00
2017-01-04 10:23:00
2017-01-04 10:24:00
2017-01-04 10:25:00
2017-01-04 10:26:00
2017-01-04 10:27:00
2017-01-04 10:28:00
2017-01-04 10:29:00
2017-01-04 10:30:00
2017-01-04 10:31:00
2017-01-04 10:32:00
2017-01-04 10:33:00
2017-01-04 10:34:00
2017-01-04 10:35:00
2017-01-04 10:36:00
2017-01-04 10:37:00
2017-01-04 10:38:00
2017-01-04 10:39:00
2017-01-04 10:40:00
2017-01-04 10:41:00


2017-01-05 10:34:00
2017-01-05 10:35:00
2017-01-05 10:36:00
2017-01-05 10:37:00
2017-01-05 10:38:00
2017-01-05 10:39:00
2017-01-05 10:40:00
2017-01-05 10:41:00
2017-01-05 10:42:00
2017-01-05 10:43:00
2017-01-05 10:44:00
2017-01-05 10:45:00
2017-01-05 10:46:00
2017-01-05 10:47:00
2017-01-05 10:48:00
2017-01-05 10:49:00
2017-01-05 10:50:00
2017-01-05 10:51:00
2017-01-05 10:52:00
2017-01-05 10:53:00
2017-01-05 10:54:00
2017-01-05 10:55:00
2017-01-05 10:56:00
2017-01-05 10:57:00
2017-01-05 10:58:00
2017-01-05 10:59:00
2017-01-05 11:00:00
2017-01-05 11:01:00
2017-01-05 11:02:00
2017-01-05 11:03:00
2017-01-05 11:04:00
2017-01-05 11:05:00
2017-01-05 11:06:00
2017-01-05 11:07:00
2017-01-05 11:08:00
2017-01-05 11:09:00
2017-01-05 11:10:00
2017-01-05 11:11:00
2017-01-05 11:12:00
2017-01-05 11:13:00
2017-01-05 11:14:00
2017-01-05 11:15:00
2017-01-05 11:16:00
2017-01-05 11:17:00
2017-01-05 11:18:00
2017-01-05 11:19:00
2017-01-05 11:20:00
2017-01-05 11:21:00
2017-01-05 11:22:00
2017-01-05 11:23:00


2017-01-06 11:15:00
2017-01-06 11:16:00
2017-01-06 11:17:00
2017-01-06 11:18:00
2017-01-06 11:19:00
2017-01-06 11:20:00
2017-01-06 11:21:00
2017-01-06 11:22:00
2017-01-06 11:23:00
2017-01-06 11:24:00
2017-01-06 11:25:00
2017-01-06 11:26:00
2017-01-06 11:27:00
2017-01-06 11:28:00
2017-01-06 11:29:00
2017-01-06 11:30:00
2017-01-06 11:31:00
2017-01-06 11:32:00
2017-01-06 11:33:00
2017-01-06 11:34:00
2017-01-06 11:35:00
2017-01-06 11:36:00
2017-01-06 11:37:00
2017-01-06 11:38:00
2017-01-06 11:39:00
2017-01-06 11:40:00
2017-01-06 11:41:00
2017-01-06 11:42:00
2017-01-06 11:43:00
2017-01-06 11:44:00
2017-01-06 11:45:00
2017-01-06 11:46:00
2017-01-06 11:47:00
2017-01-06 11:48:00
2017-01-06 11:49:00
2017-01-06 11:50:00
2017-01-06 11:51:00
2017-01-06 11:52:00
2017-01-06 11:53:00
2017-01-06 11:54:00
2017-01-06 11:55:00
2017-01-06 11:56:00
2017-01-06 11:57:00
2017-01-06 11:58:00
2017-01-06 11:59:00
2017-01-06 12:00:00
2017-01-06 12:01:00
2017-01-06 12:02:00
2017-01-06 12:03:00
2017-01-06 12:04:00


...

2017-01-24 12:16:00
2017-01-24 12:17:00
2017-01-24 12:18:00
2017-01-24 12:19:00
2017-01-24 12:20:00
2017-01-24 12:21:00
2017-01-24 12:22:00
2017-01-24 12:23:00
2017-01-24 12:24:00
2017-01-24 12:25:00
2017-01-24 12:26:00
2017-01-24 12:27:00
2017-01-24 12:28:00
2017-01-24 12:29:00
2017-01-24 12:30:00
2017-01-24 12:31:00
2017-01-24 12:32:00
2017-01-24 12:33:00
2017-01-24 12:34:00
2017-01-24 12:35:00
2017-01-24 12:36:00
2017-01-24 12:37:00
2017-01-24 12:38:00
2017-01-24 12:39:00
2017-01-24 12:40:00
2017-01-24 12:41:00
2017-01-24 12:42:00
2017-01-24 12:43:00
2017-01-24 12:44:00
2017-01-24 12:45:00
2017-01-24 12:46:00
2017-01-24 12:47:00
2017-01-24 12:48:00
2017-01-24 12:49:00
2017-01-24 12:50:00
2017-01-24 12:51:00
2017-01-24 12:52:00
2017-01-24 12:53:00
2017-01-24 12:54:00
2017-01-24 12:55:00
2017-01-24 12:56:00
2017-01-24 12:57:00
2017-01-24 12:58:00
2017-01-24 12:59:00
2017-01-24 13:00:00
2017-01-24 13:01:00
2017-01-24 13:02:00
2017-01-24 13:03:00
2017-01-24 13:04:00
2017-01-24 13:05:00


2017-01-25 12:57:00
2017-01-25 12:58:00
2017-01-25 12:59:00
2017-01-25 13:00:00
2017-01-25 13:01:00
2017-01-25 13:02:00
2017-01-25 13:03:00
2017-01-25 13:04:00
2017-01-25 13:05:00
2017-01-25 13:06:00
2017-01-25 13:07:00
2017-01-25 13:08:00
2017-01-25 13:09:00
2017-01-25 13:10:00
2017-01-25 13:11:00
2017-01-25 13:12:00
2017-01-25 13:13:00
2017-01-25 13:14:00
2017-01-25 13:15:00
2017-01-25 13:16:00
2017-01-25 13:17:00
2017-01-25 13:18:00
2017-01-25 13:19:00
2017-01-25 13:20:00
2017-01-25 13:21:00
2017-01-25 13:22:00
2017-01-25 13:23:00
2017-01-25 13:24:00
2017-01-25 13:25:00
2017-01-25 13:26:00
2017-01-25 13:27:00
2017-01-25 13:28:00
2017-01-25 13:29:00
2017-01-25 13:30:00
2017-01-25 13:31:00
2017-01-25 13:32:00
2017-01-25 13:33:00
2017-01-25 13:34:00
2017-01-25 13:35:00
2017-01-25 13:36:00
2017-01-25 13:37:00
2017-01-25 13:38:00
2017-01-25 13:39:00
2017-01-25 13:40:00
2017-01-25 13:41:00
2017-01-25 13:42:00
2017-01-25 13:43:00
2017-01-25 13:44:00
2017-01-25 13:45:00
2017-01-25 13:46:00


2017-01-27 13:36:00
2017-01-27 13:37:00
2017-01-27 13:38:00
2017-01-27 13:39:00
2017-01-27 13:40:00
2017-01-27 13:41:00
2017-01-27 13:42:00
2017-01-27 13:43:00
2017-01-27 13:44:00
2017-01-27 13:45:00
2017-01-27 13:46:00
2017-01-27 13:47:00
2017-01-27 13:48:00
2017-01-27 13:49:00
2017-01-27 13:50:00
2017-01-27 13:51:00
2017-01-27 13:52:00
2017-01-27 13:53:00
2017-01-27 13:54:00
2017-01-27 13:55:00
2017-01-27 13:56:00
2017-01-27 13:57:00
2017-01-27 13:58:00
2017-01-27 13:59:00
2017-01-27 14:00:00
2017-01-27 14:01:00
2017-01-27 14:02:00
2017-01-27 14:03:00
2017-01-27 14:04:00
2017-01-27 14:05:00
2017-01-27 14:06:00
2017-01-27 14:07:00
2017-01-27 14:08:00
2017-01-27 14:09:00
2017-01-27 14:10:00
2017-01-27 14:11:00
2017-01-27 14:12:00
2017-01-27 14:13:00
2017-01-27 14:14:00
2017-01-27 14:15:00
2017-01-27 14:16:00
2017-01-27 14:17:00
2017-01-27 14:18:00
2017-01-27 14:19:00
2017-01-27 14:20:00
2017-01-27 14:21:00
2017-01-27 14:22:00
2017-01-27 14:23:00
2017-01-27 14:24:00
2017-01-27 14:25:00


2017-01-30 14:18:00
2017-01-30 14:19:00
2017-01-30 14:20:00
2017-01-30 14:21:00
2017-01-30 14:22:00
2017-01-30 14:23:00
2017-01-30 14:24:00
2017-01-30 14:25:00
2017-01-30 14:26:00
2017-01-30 14:27:00
2017-01-30 14:28:00
2017-01-30 14:29:00
2017-01-30 14:30:00
2017-01-30 14:31:00
2017-01-30 14:32:00
2017-01-30 14:33:00
2017-01-30 14:34:00
2017-01-30 14:35:00
2017-01-30 14:36:00
2017-01-30 14:37:00
2017-01-30 14:38:00
2017-01-30 14:39:00
2017-01-30 14:40:00
2017-01-30 14:41:00
2017-01-30 14:42:00
2017-01-30 14:43:00
2017-01-30 14:44:00
2017-01-30 14:45:00
2017-01-30 14:46:00
2017-01-30 14:47:00
2017-01-30 14:48:00
2017-01-30 14:49:00
2017-01-30 14:50:00
2017-01-30 14:51:00
2017-01-30 14:52:00
2017-01-30 14:53:00
2017-01-30 14:54:00
2017-01-30 14:55:00
2017-01-30 14:56:00
2017-01-30 14:57:00
2017-01-30 14:58:00
2017-01-30 14:59:00
2017-01-30 15:00:00
2017-01-30 15:01:00
2017-01-30 15:02:00
2017-01-30 15:03:00
2017-01-30 15:04:00
2017-01-30 15:05:00
2017-01-30 15:06:00
2017-01-30 15:07:00


2017-01-31 14:57:00
2017-01-31 14:58:00
2017-01-31 14:59:00
Info: IYU:  Total Pnl: -0.09%  Profit/Loss Ratio: 0.92  Accuracy: 0.49  Score: 0.76 
Info: ILW:  Total Pnl: -0.00%  Profit/Loss Ratio: 1.00  Accuracy: 0.48  Score: 0.76 
Info: RGG:  Total Pnl: -0.07%  Profit/Loss Ratio: 0.62  Accuracy: 0.44  Score: 0.70 
Info: HDK:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.66  Accuracy: 0.62  Score: 0.69 
Info: DCO:  Total Pnl: -0.00%  Profit/Loss Ratio: 0.91  Accuracy: 0.48  Score: 0.70 
Info: NSL:  Total Pnl: -0.06%  Profit/Loss Ratio: 0.68  Accuracy: 0.48  Score: 0.72 
Info: QVE:  Total Pnl: 0.05%  Profit/Loss Ratio: 1.75  Accuracy: 0.45  Score: 0.69 
Info: BSN:  Total Pnl: 0.00%  Profit/Loss Ratio: nan  Accuracy: 0.00  Score: 0.69 
Info: NNA:  Total Pnl: 0.50%  Profit/Loss Ratio: 1.56  Accuracy: 0.41  Score: 0.71 
Info: QTY:  Total Pnl: -0.02%  Profit/Loss Ratio: 0.80  Accuracy: 0.47  Score: 0.71 
Info: IWU:  Total Pnl: 0.01%  Profit/Loss Ratio: 1.46  Accuracy: 0.53  Score: 0.70 
Info: DYE: 

In [43]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_2"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['BSN',
 'DCO',
 'DYE',
 'FFA',
 'FFS',
 'HDK',
 'HZT',
 'ILW',
 'IMC',
 'IWU',
 'IYU',
 'KAA',
 'KKG',
 'LPQ',
 'NNA',
 'NSL',
 'OMP',
 'QTY',
 'QVE',
 'RGG',
 'WTJ',
 'WUT',
 'XPV',
 'XYR']
       # return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
       #  return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: BSN
Processing data for stock: DCO
Processing data for stock: DYE
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: HDK
Processing data for stock: HZT
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IWU
Processing data for stock: IYU
Processing data for stock: KAA
Processing data for stock: KKG
Processing data for stock: LPQ
Processing data for stock: NNA
Processing data for stock: NSL
Processing data for stock: OMP
Processing data for stock: QTY
Processing data for stock: QVE
Processing data for stock: RGG
Processing data for stock: WTJ
Processing data for stock: WUT
Processing data for stock: XPV
Processing data for stock: XYR
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-02-06 09:17:00
2017-02-06 09:18:00
2017-02-06 09:19:00
2017-02-06 09:20:00
2017-02-06 09:21:00
2017-02-06 09:22:00
2017-0

2017-02-06 15:27:00
2017-02-06 15:28:00
2017-02-07 09:17:00
2017-02-07 09:18:00
2017-02-07 09:19:00
2017-02-07 09:20:00
2017-02-07 09:21:00
2017-02-07 09:22:00
2017-02-07 09:23:00
2017-02-07 09:24:00
2017-02-07 09:25:00
2017-02-07 09:26:00
2017-02-07 09:27:00
2017-02-07 09:28:00
2017-02-07 09:29:00
2017-02-07 09:30:00
2017-02-07 09:31:00
2017-02-07 09:32:00
2017-02-07 09:33:00
2017-02-07 09:34:00
2017-02-07 09:35:00
2017-02-07 09:36:00
2017-02-07 09:37:00
2017-02-07 09:38:00
2017-02-07 09:39:00
2017-02-07 09:40:00
2017-02-07 09:41:00
2017-02-07 09:42:00
2017-02-07 09:43:00
2017-02-07 09:44:00
2017-02-07 09:45:00
2017-02-07 09:46:00
2017-02-07 09:47:00
2017-02-07 09:48:00
2017-02-07 09:49:00
2017-02-07 09:50:00
2017-02-07 09:51:00
2017-02-07 09:52:00
2017-02-07 09:53:00
2017-02-07 09:54:00
2017-02-07 09:55:00
2017-02-07 09:56:00
2017-02-07 09:57:00
2017-02-07 09:58:00
2017-02-07 09:59:00
2017-02-07 10:00:00
2017-02-07 10:01:00
2017-02-07 10:02:00
2017-02-07 10:03:00
2017-02-07 10:04:00


2017-02-08 09:55:00
2017-02-08 09:56:00
2017-02-08 09:57:00
2017-02-08 09:58:00
2017-02-08 09:59:00
2017-02-08 10:00:00
2017-02-08 10:01:00
2017-02-08 10:02:00
2017-02-08 10:03:00
2017-02-08 10:04:00
2017-02-08 10:05:00
2017-02-08 10:06:00
2017-02-08 10:07:00
2017-02-08 10:08:00
2017-02-08 10:09:00
2017-02-08 10:10:00
2017-02-08 10:11:00
2017-02-08 10:12:00
2017-02-08 10:13:00
2017-02-08 10:14:00
2017-02-08 10:15:00
2017-02-08 10:16:00
2017-02-08 10:17:00
2017-02-08 10:18:00
2017-02-08 10:19:00
2017-02-08 10:20:00
2017-02-08 10:21:00
2017-02-08 10:22:00
2017-02-08 10:23:00
2017-02-08 10:24:00
2017-02-08 10:25:00
2017-02-08 10:26:00
2017-02-08 10:27:00
2017-02-08 10:28:00
2017-02-08 10:29:00
2017-02-08 10:30:00
2017-02-08 10:31:00
2017-02-08 10:32:00
2017-02-08 10:33:00
2017-02-08 10:34:00
2017-02-08 10:35:00
2017-02-08 10:36:00
2017-02-08 10:37:00
2017-02-08 10:38:00
2017-02-08 10:39:00
2017-02-08 10:40:00
2017-02-08 10:41:00
2017-02-08 10:42:00
2017-02-08 10:43:00
2017-02-08 10:44:00


2017-02-09 10:37:00
2017-02-09 10:38:00
2017-02-09 10:39:00
2017-02-09 10:40:00
2017-02-09 10:41:00
2017-02-09 10:42:00
2017-02-09 10:43:00
2017-02-09 10:44:00
2017-02-09 10:45:00
2017-02-09 10:46:00
2017-02-09 10:47:00
2017-02-09 10:48:00
2017-02-09 10:49:00
2017-02-09 10:50:00
2017-02-09 10:51:00
2017-02-09 10:52:00
2017-02-09 10:53:00
2017-02-09 10:54:00
2017-02-09 10:55:00
2017-02-09 10:56:00
2017-02-09 10:57:00
2017-02-09 10:58:00
2017-02-09 10:59:00
2017-02-09 11:00:00
2017-02-09 11:01:00
2017-02-09 11:02:00
2017-02-09 11:03:00
2017-02-09 11:04:00
2017-02-09 11:05:00
2017-02-09 11:06:00
2017-02-09 11:07:00
2017-02-09 11:08:00
2017-02-09 11:09:00
2017-02-09 11:10:00
2017-02-09 11:11:00
2017-02-09 11:12:00
2017-02-09 11:13:00
2017-02-09 11:14:00
2017-02-09 11:15:00
2017-02-09 11:16:00
2017-02-09 11:17:00
2017-02-09 11:18:00
2017-02-09 11:19:00
2017-02-09 11:20:00
2017-02-09 11:21:00
2017-02-09 11:22:00
2017-02-09 11:23:00
2017-02-09 11:24:00
2017-02-09 11:25:00
2017-02-09 11:26:00


2017-02-10 12:14:00
2017-02-10 12:15:00
2017-02-10 12:16:00
2017-02-10 12:17:00
2017-02-10 12:18:00
2017-02-10 12:19:00
2017-02-10 12:20:00
2017-02-10 12:21:00
2017-02-10 12:22:00
2017-02-10 12:23:00
2017-02-10 12:24:00
2017-02-10 12:25:00
2017-02-10 12:26:00
2017-02-10 12:27:00
2017-02-10 12:28:00
2017-02-10 12:29:00
2017-02-10 12:30:00
2017-02-10 12:31:00
2017-02-10 12:32:00
2017-02-10 12:33:00
2017-02-10 12:34:00
2017-02-10 12:35:00
2017-02-10 12:36:00
2017-02-10 12:37:00
2017-02-10 12:38:00
2017-02-10 12:39:00
2017-02-10 12:40:00
2017-02-10 12:41:00
2017-02-10 12:42:00
2017-02-10 12:43:00
2017-02-10 12:44:00
2017-02-10 12:45:00
2017-02-10 12:46:00
2017-02-10 12:47:00
2017-02-10 12:48:00
2017-02-10 12:49:00
2017-02-10 12:50:00
2017-02-10 12:51:00
2017-02-10 12:52:00
2017-02-10 12:53:00
2017-02-10 12:54:00
2017-02-10 12:55:00
2017-02-10 12:56:00
2017-02-10 12:57:00
2017-02-10 12:58:00
2017-02-10 12:59:00
2017-02-10 13:00:00
2017-02-10 13:01:00
2017-02-10 13:02:00
2017-02-10 13:03:00


...

2017-03-16 13:50:00
2017-03-16 13:51:00
2017-03-16 13:52:00
2017-03-16 13:53:00
2017-03-16 13:54:00
2017-03-16 13:55:00
2017-03-16 13:56:00
2017-03-16 13:57:00
2017-03-16 13:58:00
2017-03-16 13:59:00
2017-03-16 14:00:00
2017-03-16 14:01:00
2017-03-16 14:02:00
2017-03-16 14:03:00
2017-03-16 14:04:00
2017-03-16 14:05:00
2017-03-16 14:06:00
2017-03-16 14:07:00
2017-03-16 14:08:00
2017-03-16 14:09:00
2017-03-16 14:10:00
2017-03-16 14:11:00
2017-03-16 14:12:00
2017-03-16 14:13:00
2017-03-16 14:14:00
2017-03-16 14:15:00
2017-03-16 14:16:00
2017-03-16 14:17:00
2017-03-16 14:18:00
2017-03-16 14:19:00
2017-03-16 14:20:00
2017-03-16 14:21:00
2017-03-16 14:22:00
2017-03-16 14:23:00
2017-03-16 14:24:00
2017-03-16 14:25:00
2017-03-16 14:26:00
2017-03-16 14:27:00
2017-03-16 14:28:00
2017-03-16 14:29:00
2017-03-16 14:30:00
2017-03-17 09:17:00
2017-03-17 09:18:00
2017-03-17 09:19:00
2017-03-17 09:20:00
2017-03-17 09:21:00
2017-03-17 09:22:00
2017-03-17 09:23:00
2017-03-17 09:24:00
2017-03-17 09:25:00


2017-03-22 09:18:00
2017-03-22 09:19:00
2017-03-22 09:20:00
2017-03-22 09:21:00
2017-03-22 09:22:00
2017-03-22 09:23:00
2017-03-22 09:24:00
2017-03-22 09:25:00
2017-03-22 09:26:00
2017-03-22 09:27:00
2017-03-22 09:28:00
2017-03-22 09:29:00
2017-03-22 09:30:00
2017-03-22 09:31:00
2017-03-22 09:32:00
2017-03-22 09:33:00
2017-03-22 09:34:00
2017-03-22 09:35:00
2017-03-22 09:36:00
2017-03-22 09:37:00
2017-03-22 09:38:00
2017-03-22 09:39:00
2017-03-22 09:40:00
2017-03-22 09:41:00
2017-03-22 09:42:00
2017-03-22 09:43:00
2017-03-22 09:44:00
2017-03-22 09:45:00
2017-03-22 09:46:00
2017-03-22 09:47:00
2017-03-22 09:48:00
2017-03-22 09:49:00
2017-03-22 09:50:00
2017-03-22 09:51:00
2017-03-22 09:52:00
2017-03-22 09:53:00
2017-03-22 09:54:00
2017-03-22 09:55:00
2017-03-22 09:56:00
2017-03-22 09:57:00
2017-03-22 09:58:00
2017-03-22 09:59:00
2017-03-22 10:00:00
2017-03-22 10:01:00
2017-03-22 10:02:00
2017-03-22 10:03:00
2017-03-22 10:04:00
2017-03-22 10:05:00
2017-03-22 10:06:00
2017-03-22 10:07:00


2017-03-28 09:59:00
2017-03-28 10:00:00
2017-03-28 10:01:00
2017-03-28 10:02:00
2017-03-28 10:03:00
2017-03-28 10:04:00
2017-03-28 10:05:00
2017-03-28 10:06:00
2017-03-28 10:07:00
2017-03-28 10:08:00
2017-03-28 10:09:00
2017-03-28 10:10:00
2017-03-28 10:11:00
2017-03-28 10:12:00
2017-03-28 10:13:00
2017-03-28 10:14:00
2017-03-28 10:15:00
2017-03-28 10:16:00
2017-03-28 10:17:00
2017-03-28 10:18:00
2017-03-28 10:19:00
2017-03-28 10:20:00
2017-03-28 10:21:00
2017-03-28 10:22:00
2017-03-28 10:23:00
2017-03-28 10:24:00
2017-03-28 10:25:00
2017-03-28 10:26:00
2017-03-28 10:27:00
2017-03-28 10:28:00
2017-03-28 10:29:00
2017-03-28 10:30:00
2017-03-28 10:31:00
2017-03-28 10:32:00
2017-03-28 10:33:00
2017-03-28 10:34:00
2017-03-28 10:35:00
2017-03-28 10:36:00
2017-03-28 10:37:00
2017-03-28 10:38:00
2017-03-28 10:39:00
2017-03-28 10:40:00
2017-03-28 10:41:00
2017-03-28 10:42:00
2017-03-28 10:43:00
2017-03-28 10:44:00
2017-03-28 10:45:00
2017-03-28 10:46:00
2017-03-28 10:47:00
2017-03-28 10:48:00


2017-03-29 10:37:00
2017-03-29 10:38:00
2017-03-29 10:39:00
2017-03-29 10:40:00
2017-03-29 10:41:00
2017-03-29 10:42:00
2017-03-29 10:43:00
2017-03-29 10:44:00
2017-03-29 10:45:00
2017-03-29 10:46:00
2017-03-29 10:47:00
2017-03-29 10:48:00
2017-03-29 10:49:00
2017-03-29 10:50:00
2017-03-29 10:51:00
2017-03-29 10:52:00
2017-03-29 10:53:00
2017-03-29 10:54:00
2017-03-29 10:55:00
2017-03-29 10:56:00
2017-03-29 10:57:00
2017-03-29 10:58:00
2017-03-29 10:59:00
2017-03-29 11:00:00
2017-03-29 11:01:00
2017-03-29 11:02:00
2017-03-29 11:03:00
2017-03-29 11:04:00
2017-03-29 11:05:00
2017-03-29 11:06:00
2017-03-29 11:07:00
2017-03-29 11:08:00
2017-03-29 11:09:00
2017-03-29 11:10:00
2017-03-29 11:11:00
2017-03-29 11:12:00
2017-03-29 11:13:00
2017-03-29 11:14:00
2017-03-29 11:15:00
2017-03-29 11:16:00
2017-03-29 11:17:00
2017-03-29 11:18:00
2017-03-29 11:19:00
2017-03-29 11:20:00
2017-03-29 11:21:00
2017-03-29 11:22:00
2017-03-29 11:23:00
2017-03-29 11:24:00
2017-03-29 11:25:00
2017-03-29 11:26:00


2017-03-30 11:18:00
2017-03-30 11:19:00
2017-03-30 11:20:00
2017-03-30 11:21:00
2017-03-30 11:22:00
2017-03-30 11:23:00
2017-03-30 11:24:00
2017-03-30 11:25:00
2017-03-30 11:26:00
2017-03-30 11:27:00
2017-03-30 11:28:00
2017-03-30 11:29:00
2017-03-30 11:30:00
2017-03-30 11:31:00
2017-03-30 11:32:00
2017-03-30 11:33:00
2017-03-30 11:34:00
2017-03-30 11:35:00
2017-03-30 11:36:00
2017-03-30 11:37:00
2017-03-30 11:38:00
2017-03-30 11:39:00
2017-03-30 11:40:00
2017-03-30 11:41:00
2017-03-30 11:42:00
2017-03-30 11:43:00
2017-03-30 11:44:00
2017-03-30 11:45:00
2017-03-30 11:46:00
2017-03-30 11:47:00
2017-03-30 11:48:00
2017-03-30 11:49:00
2017-03-30 11:50:00
2017-03-30 11:51:00
2017-03-30 11:52:00
2017-03-30 11:53:00
2017-03-30 11:54:00
2017-03-30 11:55:00
2017-03-30 11:56:00
2017-03-30 11:57:00
2017-03-30 11:58:00
2017-03-30 11:59:00
2017-03-30 12:00:00
2017-03-30 12:01:00
2017-03-30 12:02:00
2017-03-30 12:03:00
2017-03-30 12:04:00
2017-03-30 12:05:00
2017-03-30 12:06:00
2017-03-30 12:07:00


In [44]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['BSN',
 'DCO',
 'DYE',
 'FFA',
 'FFS',
 'HDK',
 'HZT',
 'ILW',
 'IMC',
 'IWU',
 'IYU',
 'KAA',
 'KKG',
 'LPQ',
 'NNA',
 'NSL',
 'OMP',
 'QTY',
 'QVE',
 'RGG',
 'WTJ',
 'WUT',
 'XPV',
 'XYR']
       # return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
       #  return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: BSN
Processing data for stock: DCO
Processing data for stock: DYE
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: HDK
Processing data for stock: HZT
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IWU
Processing data for stock: IYU
Processing data for stock: KAA
Processing data for stock: KKG
Processing data for stock: LPQ
Processing data for stock: NNA
Processing data for stock: NSL
Processing data for stock: OMP
Processing data for stock: QTY
Processing data for stock: QVE
Processing data for stock: RGG
Processing data for stock: WTJ
Processing data for stock: WUT
Processing data for stock: XPV
Processing data for stock: XYR
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-25 09:17:00
2017-01-25 09:18:00
2017-01-25 09:19:00
2017-01-25 09:20:00
2017-01-25 09:21:00
2017-01-25 09:22:00
2017-0

2017-01-25 15:26:00
2017-01-25 15:27:00
2017-01-25 15:28:00
2017-01-26 09:17:00
2017-01-26 09:18:00
2017-01-26 09:19:00
2017-01-26 09:20:00
2017-01-26 09:21:00
2017-01-26 09:22:00
2017-01-26 09:23:00
2017-01-26 09:24:00
2017-01-26 09:25:00
2017-01-26 09:26:00
2017-01-26 09:27:00
2017-01-26 09:28:00
2017-01-26 09:29:00
2017-01-26 09:30:00
2017-01-26 09:31:00
2017-01-26 09:32:00
2017-01-26 09:33:00
2017-01-26 09:34:00
2017-01-26 09:35:00
2017-01-26 09:36:00
2017-01-26 09:37:00
2017-01-26 09:38:00
2017-01-26 09:39:00
2017-01-26 09:40:00
2017-01-26 09:41:00
2017-01-26 09:42:00
2017-01-26 09:43:00
2017-01-26 09:44:00
2017-01-26 09:45:00
2017-01-26 09:46:00
2017-01-26 09:47:00
2017-01-26 09:48:00
2017-01-26 09:49:00
2017-01-26 09:50:00
2017-01-26 09:51:00
2017-01-26 09:52:00
2017-01-26 09:53:00
2017-01-26 09:54:00
2017-01-26 09:55:00
2017-01-26 09:56:00
2017-01-26 09:57:00
2017-01-26 09:58:00
2017-01-26 09:59:00
2017-01-26 10:00:00
2017-01-26 10:01:00
2017-01-26 10:02:00
2017-01-26 10:03:00


2017-01-27 09:52:00
2017-01-27 09:53:00
2017-01-27 09:54:00
2017-01-27 09:55:00
2017-01-27 09:56:00
2017-01-27 09:57:00
2017-01-27 09:58:00
2017-01-27 09:59:00
2017-01-27 10:00:00
2017-01-27 10:01:00
2017-01-27 10:02:00
2017-01-27 10:03:00
2017-01-27 10:04:00
2017-01-27 10:05:00
2017-01-27 10:06:00
2017-01-27 10:07:00
2017-01-27 10:08:00
2017-01-27 10:09:00
2017-01-27 10:10:00
2017-01-27 10:11:00
2017-01-27 10:12:00
2017-01-27 10:13:00
2017-01-27 10:14:00
2017-01-27 10:15:00
2017-01-27 10:16:00
2017-01-27 10:17:00
2017-01-27 10:18:00
2017-01-27 10:19:00
2017-01-27 10:20:00
2017-01-27 10:21:00
2017-01-27 10:22:00
2017-01-27 10:23:00
2017-01-27 10:24:00
2017-01-27 10:25:00
2017-01-27 10:26:00
2017-01-27 10:27:00
2017-01-27 10:28:00
2017-01-27 10:29:00
2017-01-27 10:30:00
2017-01-27 10:31:00
2017-01-27 10:32:00
2017-01-27 10:33:00
2017-01-27 10:34:00
2017-01-27 10:35:00
2017-01-27 10:36:00
2017-01-27 10:37:00
2017-01-27 10:38:00
2017-01-27 10:39:00
2017-01-27 10:40:00
2017-01-27 10:41:00


2017-01-30 10:33:00
2017-01-30 10:34:00
2017-01-30 10:35:00
2017-01-30 10:36:00
2017-01-30 10:37:00
2017-01-30 10:38:00
2017-01-30 10:39:00
2017-01-30 10:40:00
2017-01-30 10:41:00
2017-01-30 10:42:00
2017-01-30 10:43:00
2017-01-30 10:44:00
2017-01-30 10:45:00
2017-01-30 10:46:00
2017-01-30 10:47:00
2017-01-30 10:48:00
2017-01-30 10:49:00
2017-01-30 10:50:00
2017-01-30 10:51:00
2017-01-30 10:52:00
2017-01-30 10:53:00
2017-01-30 10:54:00
2017-01-30 10:55:00
2017-01-30 10:56:00
2017-01-30 10:57:00
2017-01-30 10:58:00
2017-01-30 10:59:00
2017-01-30 11:00:00
2017-01-30 11:01:00
2017-01-30 11:02:00
2017-01-30 11:03:00
2017-01-30 11:04:00
2017-01-30 11:05:00
2017-01-30 11:06:00
2017-01-30 11:07:00
2017-01-30 11:08:00
2017-01-30 11:09:00
2017-01-30 11:10:00
2017-01-30 11:11:00
2017-01-30 11:12:00
2017-01-30 11:13:00
2017-01-30 11:14:00
2017-01-30 11:15:00
2017-01-30 11:16:00
2017-01-30 11:17:00
2017-01-30 11:18:00
2017-01-30 11:19:00
2017-01-30 11:20:00
2017-01-30 11:21:00
2017-01-30 11:22:00


2017-01-31 11:13:00
2017-01-31 11:14:00
2017-01-31 11:15:00
2017-01-31 11:16:00
2017-01-31 11:17:00
2017-01-31 11:18:00
2017-01-31 11:19:00
2017-01-31 11:20:00
2017-01-31 11:21:00
2017-01-31 11:22:00
2017-01-31 11:23:00
2017-01-31 11:24:00
2017-01-31 11:25:00
2017-01-31 11:26:00
2017-01-31 11:27:00
2017-01-31 11:28:00
2017-01-31 11:29:00
2017-01-31 11:30:00
2017-01-31 11:31:00
2017-01-31 11:32:00
2017-01-31 11:33:00
2017-01-31 11:34:00
2017-01-31 11:35:00
2017-01-31 11:36:00
2017-01-31 11:37:00
2017-01-31 11:38:00
2017-01-31 11:39:00
2017-01-31 11:40:00
2017-01-31 11:41:00
2017-01-31 11:42:00
2017-01-31 11:43:00
2017-01-31 11:44:00
2017-01-31 11:45:00
2017-01-31 11:46:00
2017-01-31 11:47:00
2017-01-31 11:48:00
2017-01-31 11:49:00
2017-01-31 11:50:00
2017-01-31 11:51:00
2017-01-31 11:52:00
2017-01-31 11:53:00
2017-01-31 11:54:00
2017-01-31 11:55:00
2017-01-31 11:56:00
2017-01-31 11:57:00
2017-01-31 11:58:00
2017-01-31 11:59:00
2017-01-31 12:00:00
2017-01-31 12:01:00
2017-01-31 12:02:00


...

2017-03-03 12:24:00
2017-03-03 12:25:00
2017-03-03 12:26:00
2017-03-03 12:27:00
2017-03-03 12:28:00
2017-03-03 12:29:00
2017-03-03 12:30:00
2017-03-03 12:31:00
2017-03-03 12:32:00
2017-03-03 12:33:00
2017-03-03 12:34:00
2017-03-03 12:35:00
2017-03-03 12:36:00
2017-03-03 12:37:00
2017-03-03 12:38:00
2017-03-03 12:39:00
2017-03-03 12:40:00
2017-03-03 12:41:00
2017-03-03 12:42:00
2017-03-03 12:43:00
2017-03-03 12:44:00
2017-03-03 12:45:00
2017-03-03 12:46:00
2017-03-03 12:47:00
2017-03-03 12:48:00
2017-03-03 12:49:00
2017-03-03 12:50:00
2017-03-03 12:51:00
2017-03-03 12:52:00
2017-03-03 12:53:00
2017-03-03 12:54:00
2017-03-03 12:55:00
2017-03-03 12:56:00
2017-03-03 12:57:00
2017-03-03 12:58:00
2017-03-03 12:59:00
2017-03-03 13:00:00
2017-03-03 13:01:00
2017-03-03 13:02:00
2017-03-03 13:03:00
2017-03-03 13:04:00
2017-03-03 13:05:00
2017-03-03 13:06:00
2017-03-03 13:07:00
2017-03-03 13:08:00
2017-03-03 13:09:00
2017-03-03 13:10:00
2017-03-03 13:11:00
2017-03-03 13:12:00
2017-03-03 13:13:00


2017-03-06 13:05:00
2017-03-06 13:06:00
2017-03-06 13:07:00
2017-03-06 13:08:00
2017-03-06 13:09:00
2017-03-06 13:10:00
2017-03-06 13:11:00
2017-03-06 13:12:00
2017-03-06 13:13:00
2017-03-06 13:14:00
2017-03-06 13:15:00
2017-03-06 13:16:00
2017-03-06 13:17:00
2017-03-06 13:18:00
2017-03-06 13:19:00
2017-03-06 13:20:00
2017-03-06 13:21:00
2017-03-06 13:22:00
2017-03-06 13:23:00
2017-03-06 13:24:00
2017-03-06 13:25:00
2017-03-06 13:26:00
2017-03-06 13:27:00
2017-03-06 13:28:00
2017-03-06 13:29:00
2017-03-06 13:30:00
2017-03-06 13:31:00
2017-03-06 13:32:00
2017-03-06 13:33:00
2017-03-06 13:34:00
2017-03-06 13:35:00
2017-03-06 13:36:00
2017-03-06 13:37:00
2017-03-06 13:38:00
2017-03-06 13:39:00
2017-03-06 13:40:00
2017-03-06 13:41:00
2017-03-06 13:42:00
2017-03-06 13:43:00
2017-03-06 13:44:00
2017-03-06 13:45:00
2017-03-06 13:46:00
2017-03-06 13:47:00
2017-03-06 13:48:00
2017-03-06 13:49:00
2017-03-06 13:50:00
2017-03-06 13:51:00
2017-03-06 13:52:00
2017-03-06 13:53:00
2017-03-06 13:54:00


2017-03-07 13:43:00
2017-03-07 13:44:00
2017-03-07 13:45:00
2017-03-07 13:46:00
2017-03-07 13:47:00
2017-03-07 13:48:00
2017-03-07 13:49:00
2017-03-07 13:50:00
2017-03-07 13:51:00
2017-03-07 13:52:00
2017-03-07 13:53:00
2017-03-07 13:54:00
2017-03-07 13:55:00
2017-03-07 13:56:00
2017-03-07 13:57:00
2017-03-07 13:58:00
2017-03-07 13:59:00
2017-03-07 14:00:00
2017-03-07 14:01:00
2017-03-07 14:02:00
2017-03-07 14:03:00
2017-03-07 14:04:00
2017-03-07 14:05:00
2017-03-07 14:06:00
2017-03-07 14:07:00
2017-03-07 14:08:00
2017-03-07 14:09:00
2017-03-07 14:10:00
2017-03-07 14:11:00
2017-03-07 14:12:00
2017-03-07 14:13:00
2017-03-07 14:14:00
2017-03-07 14:15:00
2017-03-07 14:16:00
2017-03-07 14:17:00
2017-03-07 14:18:00
2017-03-07 14:19:00
2017-03-07 14:20:00
2017-03-07 14:21:00
2017-03-07 14:22:00
2017-03-07 14:23:00
2017-03-07 14:24:00
2017-03-07 14:25:00
2017-03-07 14:26:00
2017-03-07 14:27:00
2017-03-07 14:28:00
2017-03-07 14:29:00
2017-03-07 14:30:00
2017-03-07 14:31:00
2017-03-07 14:32:00


2017-03-08 14:25:00
2017-03-08 14:26:00
2017-03-08 14:27:00
2017-03-08 14:28:00
2017-03-08 14:29:00
2017-03-08 14:30:00
2017-03-08 14:31:00
2017-03-08 14:32:00
2017-03-08 14:33:00
2017-03-08 14:34:00
2017-03-08 14:35:00
2017-03-08 14:36:00
2017-03-08 14:37:00
2017-03-08 14:38:00
2017-03-08 14:39:00
2017-03-08 14:40:00
2017-03-08 14:41:00
2017-03-08 14:42:00
2017-03-08 14:43:00
2017-03-08 14:44:00
2017-03-08 14:45:00
2017-03-08 14:46:00
2017-03-08 14:47:00
2017-03-08 14:48:00
2017-03-08 14:49:00
2017-03-08 14:50:00
2017-03-08 14:51:00
2017-03-08 14:52:00
2017-03-08 14:53:00
2017-03-08 14:54:00
2017-03-08 14:55:00
2017-03-08 14:56:00
2017-03-08 14:57:00
2017-03-08 14:58:00
2017-03-08 14:59:00
2017-03-08 15:00:00
2017-03-08 15:01:00
2017-03-08 15:02:00
2017-03-08 15:03:00
2017-03-08 15:04:00
2017-03-08 15:05:00
2017-03-08 15:06:00
2017-03-08 15:07:00
2017-03-08 15:08:00
2017-03-08 15:09:00
2017-03-08 15:10:00
2017-03-08 15:11:00
2017-03-08 15:12:00
2017-03-08 15:13:00
2017-03-08 15:14:00


2017-03-09 15:06:00
2017-03-09 15:07:00
2017-03-09 15:08:00
2017-03-09 15:09:00
2017-03-09 15:10:00
2017-03-09 15:11:00
2017-03-09 15:12:00
2017-03-09 15:13:00
2017-03-09 15:14:00
2017-03-09 15:15:00
2017-03-09 15:16:00
2017-03-09 15:17:00
2017-03-09 15:18:00
2017-03-09 15:19:00
2017-03-09 15:20:00
2017-03-09 15:21:00
2017-03-09 15:22:00
2017-03-09 15:23:00
2017-03-09 15:24:00
2017-03-09 15:25:00
2017-03-09 15:26:00
2017-03-09 15:27:00
2017-03-09 15:28:00
Info: IYU:  Total Pnl: -0.05%  Profit/Loss Ratio: 0.98  Accuracy: 0.49  Score: 0.77 
Info: ILW:  Total Pnl: -0.07%  Profit/Loss Ratio: 0.77  Accuracy: 0.46  Score: 0.71 
Info: RGG:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.07  Accuracy: 0.46  Score: 0.70 
Info: HDK:  Total Pnl: -0.00%  Profit/Loss Ratio: 0.79  Accuracy: 0.47  Score: 0.70 
Info: DCO:  Total Pnl: 0.01%  Profit/Loss Ratio: 1.21  Accuracy: 0.51  Score: 0.70 
Info: NSL:  Total Pnl: -0.02%  Profit/Loss Ratio: 0.90  Accuracy: 0.48  Score: 0.70 
Info: QVE:  Total Pnl: 0.00%  Pr

In [47]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['BSN',
 'DCO',
 'DYE',
 'FFA',
 'FFS',
 'HDK',
 'HZT',
 'ILW',
 'IMC',
 'IWU',
 'IYU',
 'KAA',
 'KKG',
 'LPQ',
 'NNA',
 'NSL',
 'OMP',
 'QTY',
 'QVE',
 'RGG',
 'WTJ',
 'WUT',
 'XPV',
 'XYR',
 'BLR',
 'BWU',
 'CUN',
 'DUR',
 'FRE',
 'IUE',
 'IUQ',
 'MUF',
 'OGU',
 'PQS',
 'UBF',
 'XAD',
 'XZR',
 'YUZ',
 'ZLX']
       # return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
       #  return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: BSN
Processing data for stock: DCO
Processing data for stock: DYE
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: HDK
Processing data for stock: HZT
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IWU
Processing data for stock: IYU
Processing data for stock: KAA
Processing data for stock: KKG
Processing data for stock: LPQ
Processing data for stock: NNA
Processing data for stock: NSL
Processing data for stock: OMP
Processing data for stock: QTY
Processing data for stock: QVE
Processing data for stock: RGG
Processing data for stock: WTJ
Processing data for stock: WUT
Processing data for stock: XPV
Processing data for stock: XYR
Processing data for stock: BLR
Processing data for stock: BWU
Processing data for stock: CUN
Processing data for stock: DUR
Processing data for stock: FRE
Processing data for stock: IUE
Processing data for stock: IUQ
Processing data for stock: MUF
Processi

2017-01-25 15:00:00
2017-01-25 15:01:00
2017-01-25 15:02:00
2017-01-25 15:03:00
2017-01-25 15:04:00
2017-01-25 15:05:00
2017-01-25 15:06:00
2017-01-25 15:07:00
2017-01-25 15:08:00
2017-01-25 15:09:00
2017-01-25 15:10:00
2017-01-25 15:11:00
2017-01-25 15:12:00
2017-01-25 15:13:00
2017-01-25 15:14:00
2017-01-25 15:15:00
2017-01-25 15:16:00
2017-01-25 15:17:00
2017-01-25 15:18:00
2017-01-25 15:19:00
2017-01-25 15:20:00
2017-01-25 15:21:00
2017-01-25 15:22:00
2017-01-25 15:23:00
2017-01-25 15:24:00
2017-01-25 15:25:00
2017-01-25 15:26:00
2017-01-25 15:27:00
2017-01-25 15:28:00
2017-01-26 09:17:00
2017-01-26 09:18:00
2017-01-26 09:19:00
2017-01-26 09:20:00
2017-01-26 09:21:00
2017-01-26 09:22:00
2017-01-26 09:23:00
2017-01-26 09:24:00
2017-01-26 09:25:00
2017-01-26 09:26:00
2017-01-26 09:27:00
2017-01-26 09:28:00
2017-01-26 09:29:00
2017-01-26 09:30:00
2017-01-26 09:31:00
2017-01-26 09:32:00
2017-01-26 09:33:00
2017-01-26 09:34:00
2017-01-26 09:35:00
2017-01-26 09:36:00
2017-01-26 09:37:00


2017-01-27 09:28:00
2017-01-27 09:29:00
2017-01-27 09:30:00
2017-01-27 09:31:00
2017-01-27 09:32:00
2017-01-27 09:33:00
2017-01-27 09:34:00
2017-01-27 09:35:00
2017-01-27 09:36:00
2017-01-27 09:37:00
2017-01-27 09:38:00
2017-01-27 09:39:00
2017-01-27 09:40:00
2017-01-27 09:41:00
2017-01-27 09:42:00
2017-01-27 09:43:00
2017-01-27 09:44:00
2017-01-27 09:45:00
2017-01-27 09:46:00
2017-01-27 09:47:00
2017-01-27 09:48:00
2017-01-27 09:49:00
2017-01-27 09:50:00
2017-01-27 09:51:00
2017-01-27 09:52:00
2017-01-27 09:53:00
2017-01-27 09:54:00
2017-01-27 09:55:00
2017-01-27 09:56:00
2017-01-27 09:57:00
2017-01-27 09:58:00
2017-01-27 09:59:00
2017-01-27 10:00:00
2017-01-27 10:01:00
2017-01-27 10:02:00
2017-01-27 10:03:00
2017-01-27 10:04:00
2017-01-27 10:05:00
2017-01-27 10:06:00
2017-01-27 10:07:00
2017-01-27 10:08:00
2017-01-27 10:09:00
2017-01-27 10:10:00
2017-01-27 10:11:00
2017-01-27 10:12:00
2017-01-27 10:13:00
2017-01-27 10:14:00
2017-01-27 10:15:00
2017-01-27 10:16:00
2017-01-27 10:17:00


2017-01-30 10:06:00
2017-01-30 10:07:00
2017-01-30 10:08:00
2017-01-30 10:09:00
2017-01-30 10:10:00
2017-01-30 10:11:00
2017-01-30 10:12:00
2017-01-30 10:13:00
2017-01-30 10:14:00
2017-01-30 10:15:00
2017-01-30 10:16:00
2017-01-30 10:17:00
2017-01-30 10:18:00
2017-01-30 10:19:00
2017-01-30 10:20:00
2017-01-30 10:21:00
2017-01-30 10:22:00
2017-01-30 10:23:00
2017-01-30 10:24:00
2017-01-30 10:25:00
2017-01-30 10:26:00
2017-01-30 10:27:00
2017-01-30 10:28:00
2017-01-30 10:29:00
2017-01-30 10:30:00
2017-01-30 10:31:00
2017-01-30 10:32:00
2017-01-30 10:33:00
2017-01-30 10:34:00
2017-01-30 10:35:00
2017-01-30 10:36:00
2017-01-30 10:37:00
2017-01-30 10:38:00
2017-01-30 10:39:00
2017-01-30 10:40:00
2017-01-30 10:41:00
2017-01-30 10:42:00
2017-01-30 10:43:00
2017-01-30 10:44:00
2017-01-30 10:45:00
2017-01-30 10:46:00
2017-01-30 10:47:00
2017-01-30 10:48:00
2017-01-30 10:49:00
2017-01-30 10:50:00
2017-01-30 10:51:00
2017-01-30 10:52:00
2017-01-30 10:53:00
2017-01-30 10:54:00
2017-01-30 10:55:00


2017-01-31 10:45:00
2017-01-31 10:46:00
2017-01-31 10:47:00
2017-01-31 10:48:00
2017-01-31 10:49:00
2017-01-31 10:50:00
2017-01-31 10:51:00
2017-01-31 10:52:00
2017-01-31 10:53:00
2017-01-31 10:54:00
2017-01-31 10:55:00
2017-01-31 10:56:00
2017-01-31 10:57:00
2017-01-31 10:58:00
2017-01-31 10:59:00
2017-01-31 11:00:00
2017-01-31 11:01:00
2017-01-31 11:02:00
2017-01-31 11:03:00
2017-01-31 11:04:00
2017-01-31 11:05:00
2017-01-31 11:06:00
2017-01-31 11:07:00
2017-01-31 11:08:00
2017-01-31 11:09:00
2017-01-31 11:10:00
2017-01-31 11:11:00
2017-01-31 11:12:00
2017-01-31 11:13:00
2017-01-31 11:14:00
2017-01-31 11:15:00
2017-01-31 11:16:00
2017-01-31 11:17:00
2017-01-31 11:18:00
2017-01-31 11:19:00
2017-01-31 11:20:00
2017-01-31 11:21:00
2017-01-31 11:22:00
2017-01-31 11:23:00
2017-01-31 11:24:00
2017-01-31 11:25:00
2017-01-31 11:26:00
2017-01-31 11:27:00
2017-01-31 11:28:00
2017-01-31 11:29:00
2017-01-31 11:30:00
2017-01-31 11:31:00
2017-01-31 11:32:00
2017-01-31 11:33:00
2017-01-31 11:34:00


...

2017-03-03 11:54:00
2017-03-03 11:55:00
2017-03-03 11:56:00
2017-03-03 11:57:00
2017-03-03 11:58:00
2017-03-03 11:59:00
2017-03-03 12:00:00
2017-03-03 12:01:00
2017-03-03 12:02:00
2017-03-03 12:03:00
2017-03-03 12:04:00
2017-03-03 12:05:00
2017-03-03 12:06:00
2017-03-03 12:07:00
2017-03-03 12:08:00
2017-03-03 12:09:00
2017-03-03 12:10:00
2017-03-03 12:11:00
2017-03-03 12:12:00
2017-03-03 12:13:00
2017-03-03 12:14:00
2017-03-03 12:15:00
2017-03-03 12:16:00
2017-03-03 12:17:00
2017-03-03 12:18:00
2017-03-03 12:19:00
2017-03-03 12:20:00
2017-03-03 12:21:00
2017-03-03 12:22:00
2017-03-03 12:23:00
2017-03-03 12:24:00
2017-03-03 12:25:00
2017-03-03 12:26:00
2017-03-03 12:27:00
2017-03-03 12:28:00
2017-03-03 12:29:00
2017-03-03 12:30:00
2017-03-03 12:31:00
2017-03-03 12:32:00
2017-03-03 12:33:00
2017-03-03 12:34:00
2017-03-03 12:35:00
2017-03-03 12:36:00
2017-03-03 12:37:00
2017-03-03 12:38:00
2017-03-03 12:39:00
2017-03-03 12:40:00
2017-03-03 12:41:00
2017-03-03 12:42:00
2017-03-03 12:43:00


2017-03-06 12:34:00
2017-03-06 12:35:00
2017-03-06 12:36:00
2017-03-06 12:37:00
2017-03-06 12:38:00
2017-03-06 12:39:00
2017-03-06 12:40:00
2017-03-06 12:41:00
2017-03-06 12:42:00
2017-03-06 12:43:00
2017-03-06 12:44:00
2017-03-06 12:45:00
2017-03-06 12:46:00
2017-03-06 12:47:00
2017-03-06 12:48:00
2017-03-06 12:49:00
2017-03-06 12:50:00
2017-03-06 12:51:00
2017-03-06 12:52:00
2017-03-06 12:53:00
2017-03-06 12:54:00
2017-03-06 12:55:00
2017-03-06 12:56:00
2017-03-06 12:57:00
2017-03-06 12:58:00
2017-03-06 12:59:00
2017-03-06 13:00:00
2017-03-06 13:01:00
2017-03-06 13:02:00
2017-03-06 13:03:00
2017-03-06 13:04:00
2017-03-06 13:05:00
2017-03-06 13:06:00
2017-03-06 13:07:00
2017-03-06 13:08:00
2017-03-06 13:09:00
2017-03-06 13:10:00
2017-03-06 13:11:00
2017-03-06 13:12:00
2017-03-06 13:13:00
2017-03-06 13:14:00
2017-03-06 13:15:00
2017-03-06 13:16:00
2017-03-06 13:17:00
2017-03-06 13:18:00
2017-03-06 13:19:00
2017-03-06 13:20:00
2017-03-06 13:21:00
2017-03-06 13:22:00
2017-03-06 13:23:00


2017-03-07 13:16:00
2017-03-07 13:17:00
2017-03-07 13:18:00
2017-03-07 13:19:00
2017-03-07 13:20:00
2017-03-07 13:21:00
2017-03-07 13:22:00
2017-03-07 13:23:00
2017-03-07 13:24:00
2017-03-07 13:25:00
2017-03-07 13:26:00
2017-03-07 13:27:00
2017-03-07 13:28:00
2017-03-07 13:29:00
2017-03-07 13:30:00
2017-03-07 13:31:00
2017-03-07 13:32:00
2017-03-07 13:33:00
2017-03-07 13:34:00
2017-03-07 13:35:00
2017-03-07 13:36:00
2017-03-07 13:37:00
2017-03-07 13:38:00
2017-03-07 13:39:00
2017-03-07 13:40:00
2017-03-07 13:41:00
2017-03-07 13:42:00
2017-03-07 13:43:00
2017-03-07 13:44:00
2017-03-07 13:45:00
2017-03-07 13:46:00
2017-03-07 13:47:00
2017-03-07 13:48:00
2017-03-07 13:49:00
2017-03-07 13:50:00
2017-03-07 13:51:00
2017-03-07 13:52:00
2017-03-07 13:53:00
2017-03-07 13:54:00
2017-03-07 13:55:00
2017-03-07 13:56:00
2017-03-07 13:57:00
2017-03-07 13:58:00
2017-03-07 13:59:00
2017-03-07 14:00:00
2017-03-07 14:01:00
2017-03-07 14:02:00
2017-03-07 14:03:00
2017-03-07 14:04:00
2017-03-07 14:05:00


2017-03-08 13:53:00
2017-03-08 13:54:00
2017-03-08 13:55:00
2017-03-08 13:56:00
2017-03-08 13:57:00
2017-03-08 13:58:00
2017-03-08 13:59:00
2017-03-08 14:00:00
2017-03-08 14:01:00
2017-03-08 14:02:00
2017-03-08 14:03:00
2017-03-08 14:04:00
2017-03-08 14:05:00
2017-03-08 14:06:00
2017-03-08 14:07:00
2017-03-08 14:08:00
2017-03-08 14:09:00
2017-03-08 14:10:00
2017-03-08 14:11:00
2017-03-08 14:12:00
2017-03-08 14:13:00
2017-03-08 14:14:00
2017-03-08 14:15:00
2017-03-08 14:16:00
2017-03-08 14:17:00
2017-03-08 14:18:00
2017-03-08 14:19:00
2017-03-08 14:20:00
2017-03-08 14:21:00
2017-03-08 14:22:00
2017-03-08 14:23:00
2017-03-08 14:24:00
2017-03-08 14:25:00
2017-03-08 14:26:00
2017-03-08 14:27:00
2017-03-08 14:28:00
2017-03-08 14:29:00
2017-03-08 14:30:00
2017-03-08 14:31:00
2017-03-08 14:32:00
2017-03-08 14:33:00
2017-03-08 14:34:00
2017-03-08 14:35:00
2017-03-08 14:36:00
2017-03-08 14:37:00
2017-03-08 14:38:00
2017-03-08 14:39:00
2017-03-08 14:40:00
2017-03-08 14:41:00
2017-03-08 14:42:00


2017-03-09 14:31:00
2017-03-09 14:32:00
2017-03-09 14:33:00
2017-03-09 14:34:00
2017-03-09 14:35:00
2017-03-09 14:36:00
2017-03-09 14:37:00
2017-03-09 14:38:00
2017-03-09 14:39:00
2017-03-09 14:40:00
2017-03-09 14:41:00
2017-03-09 14:42:00
2017-03-09 14:43:00
2017-03-09 14:44:00
2017-03-09 14:45:00
2017-03-09 14:46:00
2017-03-09 14:47:00
2017-03-09 14:48:00
2017-03-09 14:49:00
2017-03-09 14:50:00
2017-03-09 14:51:00
2017-03-09 14:52:00
2017-03-09 14:53:00
2017-03-09 14:54:00
2017-03-09 14:55:00
2017-03-09 14:56:00
2017-03-09 14:57:00
2017-03-09 14:58:00
2017-03-09 14:59:00
2017-03-09 15:00:00
2017-03-09 15:01:00
2017-03-09 15:02:00
2017-03-09 15:03:00
2017-03-09 15:04:00
2017-03-09 15:05:00
2017-03-09 15:06:00
2017-03-09 15:07:00
2017-03-09 15:08:00
2017-03-09 15:09:00
2017-03-09 15:10:00
2017-03-09 15:11:00
2017-03-09 15:12:00
2017-03-09 15:13:00
2017-03-09 15:14:00
2017-03-09 15:15:00
2017-03-09 15:16:00
2017-03-09 15:17:00
2017-03-09 15:18:00
2017-03-09 15:19:00
2017-03-09 15:20:00


In [48]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_2"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['BSN',
 'DCO',
 'DYE',
 'FFA',
 'FFS',
 'HDK',
 'HZT',
 'ILW',
 'IMC',
 'IWU',
 'IYU',
 'KAA',
 'KKG',
 'LPQ',
 'NNA',
 'NSL',
 'OMP',
 'QTY',
 'QVE',
 'RGG',
 'WTJ',
 'WUT',
 'XPV',
 'XYR',
 'BLR',
 'BWU',
 'CUN',
 'DUR',
 'FRE',
 'IUE',
 'IUQ',
 'MUF',
 'OGU',
 'PQS',
 'UBF',
 'XAD',
 'XZR',
 'YUZ',
 'ZLX']
       # return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
       #  return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: BSN
Processing data for stock: DCO
Processing data for stock: DYE
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: HDK
Processing data for stock: HZT
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IWU
Processing data for stock: IYU
Processing data for stock: KAA
Processing data for stock: KKG
Processing data for stock: LPQ
Processing data for stock: NNA
Processing data for stock: NSL
Processing data for stock: OMP
Processing data for stock: QTY
Processing data for stock: QVE
Processing data for stock: RGG
Processing data for stock: WTJ
Processing data for stock: WUT
Processing data for stock: XPV
Processing data for stock: XYR
Processing data for stock: BLR
Processing data for stock: BWU
Processing data for stock: CUN
Processing data for stock: DUR
Processing data for stock: FRE
Processing data for stock: IUE
Processing data for stock: IUQ
Processing data for stock: MUF
Processi

KeyboardInterrupt: 

In [ ]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_3"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['BSN',
 'DCO',
 'DYE',
 'FFA',
 'FFS',
 'HDK',
 'HZT',
 'ILW',
 'IMC',
 'IWU',
 'IYU',
 'KAA',
 'KKG',
 'LPQ',
 'NNA',
 'NSL',
 'OMP',
 'QTY',
 'QVE',
 'RGG',
 'WTJ',
 'WUT',
 'XPV',
 'XYR',
 'BLR',
 'BWU',
 'CUN',
 'DUR',
 'FRE',
 'IUE',
 'IUQ',
 'MUF',
 'OGU',
 'PQS',
 'UBF',
 'XAD',
 'XZR',
 'YUZ',
 'ZLX']
       # return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
       #  return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


In [49]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['BSN',
 'DCO',
 'DYE',
 'FFA',
 'FFS',
 'HDK',
 'HZT',
 #'ILW',
 'IMC',
 'IWU',
 #'IYU',
 'KAA',
 'KKG',
 'LPQ',
 'NNA',
 #'NSL',
 'OMP',
 'QTY',
 'QVE',
 'RGG',
 #'WTJ',
 'WUT',
 'XPV',
 'XYR']
       # return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
       #  return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: BSN
Processing data for stock: DCO
Processing data for stock: DYE
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: HDK
Processing data for stock: HZT
Processing data for stock: IMC
Processing data for stock: IWU
Processing data for stock: KAA
Processing data for stock: KKG
Processing data for stock: LPQ
Processing data for stock: NNA
Processing data for stock: OMP
Processing data for stock: QTY
Processing data for stock: QVE
Processing data for stock: RGG
Processing data for stock: WUT
Processing data for stock: XPV
Processing data for stock: XYR
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-25 09:17:00
2017-01-25 09:18:00
2017-01-25 09:19:00
2017-01-25 09:20:00
2017-01-25 09:21:00
2017-01-25 09:22:00
2017-01-25 09:23:00
2017-01-25 09:24:00
2017-01-25 09:25:00
2017-01-25 09:26:00
2017-01-25 09:27:00
2017-01-25 09:28:00
2017-01-25

2017-01-26 09:20:00
2017-01-26 09:21:00
2017-01-26 09:22:00
2017-01-26 09:23:00
2017-01-26 09:24:00
2017-01-26 09:25:00
2017-01-26 09:26:00
2017-01-26 09:27:00
2017-01-26 09:28:00
2017-01-26 09:29:00
2017-01-26 09:30:00
2017-01-26 09:31:00
2017-01-26 09:32:00
2017-01-26 09:33:00
2017-01-26 09:34:00
2017-01-26 09:35:00
2017-01-26 09:36:00
2017-01-26 09:37:00
2017-01-26 09:38:00
2017-01-26 09:39:00
2017-01-26 09:40:00
2017-01-26 09:41:00
2017-01-26 09:42:00
2017-01-26 09:43:00
2017-01-26 09:44:00
2017-01-26 09:45:00
2017-01-26 09:46:00
2017-01-26 09:47:00
2017-01-26 09:48:00
2017-01-26 09:49:00
2017-01-26 09:50:00
2017-01-26 09:51:00
2017-01-26 09:52:00
2017-01-26 09:53:00
2017-01-26 09:54:00
2017-01-26 09:55:00
2017-01-26 09:56:00
2017-01-26 09:57:00
2017-01-26 09:58:00
2017-01-26 09:59:00
2017-01-26 10:00:00
2017-01-26 10:01:00
2017-01-26 10:02:00
2017-01-26 10:03:00
2017-01-26 10:04:00
2017-01-26 10:05:00
2017-01-26 10:06:00
2017-01-26 10:07:00
2017-01-26 10:08:00
2017-01-26 10:09:00


2017-01-27 10:02:00
2017-01-27 10:03:00
2017-01-27 10:04:00
2017-01-27 10:05:00
2017-01-27 10:06:00
2017-01-27 10:07:00
2017-01-27 10:08:00
2017-01-27 10:09:00
2017-01-27 10:10:00
2017-01-27 10:11:00
2017-01-27 10:12:00
2017-01-27 10:13:00
2017-01-27 10:14:00
2017-01-27 10:15:00
2017-01-27 10:16:00
2017-01-27 10:17:00
2017-01-27 10:18:00
2017-01-27 10:19:00
2017-01-27 10:20:00
2017-01-27 10:21:00
2017-01-27 10:22:00
2017-01-27 10:23:00
2017-01-27 10:24:00
2017-01-27 10:25:00
2017-01-27 10:26:00
2017-01-27 10:27:00
2017-01-27 10:28:00
2017-01-27 10:29:00
2017-01-27 10:30:00
2017-01-27 10:31:00
2017-01-27 10:32:00
2017-01-27 10:33:00
2017-01-27 10:34:00
2017-01-27 10:35:00
2017-01-27 10:36:00
2017-01-27 10:37:00
2017-01-27 10:38:00
2017-01-27 10:39:00
2017-01-27 10:40:00
2017-01-27 10:41:00
2017-01-27 10:42:00
2017-01-27 10:43:00
2017-01-27 10:44:00
2017-01-27 10:45:00
2017-01-27 10:46:00
2017-01-27 10:47:00
2017-01-27 10:48:00
2017-01-27 10:49:00
2017-01-27 10:50:00
2017-01-27 10:51:00


2017-01-30 10:40:00
2017-01-30 10:41:00
2017-01-30 10:42:00
2017-01-30 10:43:00
2017-01-30 10:44:00
2017-01-30 10:45:00
2017-01-30 10:46:00
2017-01-30 10:47:00
2017-01-30 10:48:00
2017-01-30 10:49:00
2017-01-30 10:50:00
2017-01-30 10:51:00
2017-01-30 10:52:00
2017-01-30 10:53:00
2017-01-30 10:54:00
2017-01-30 10:55:00
2017-01-30 10:56:00
2017-01-30 10:57:00
2017-01-30 10:58:00
2017-01-30 10:59:00
2017-01-30 11:00:00
2017-01-30 11:01:00
2017-01-30 11:02:00
2017-01-30 11:03:00
2017-01-30 11:04:00
2017-01-30 11:05:00
2017-01-30 11:06:00
2017-01-30 11:07:00
2017-01-30 11:08:00
2017-01-30 11:09:00
2017-01-30 11:10:00
2017-01-30 11:11:00
2017-01-30 11:12:00
2017-01-30 11:13:00
2017-01-30 11:14:00
2017-01-30 11:15:00
2017-01-30 11:16:00
2017-01-30 11:17:00
2017-01-30 11:18:00
2017-01-30 11:19:00
2017-01-30 11:20:00
2017-01-30 11:21:00
2017-01-30 11:22:00
2017-01-30 11:23:00
2017-01-30 11:24:00
2017-01-30 11:25:00
2017-01-30 11:26:00
2017-01-30 11:27:00
2017-01-30 11:28:00
2017-01-30 11:29:00


2017-01-31 11:18:00
2017-01-31 11:19:00
2017-01-31 11:20:00
2017-01-31 11:21:00
2017-01-31 11:22:00
2017-01-31 11:23:00
2017-01-31 11:24:00
2017-01-31 11:25:00
2017-01-31 11:26:00
2017-01-31 11:27:00
2017-01-31 11:28:00
2017-01-31 11:29:00
2017-01-31 11:30:00
2017-01-31 11:31:00
2017-01-31 11:32:00
2017-01-31 11:33:00
2017-01-31 11:34:00
2017-01-31 11:35:00
2017-01-31 11:36:00
2017-01-31 11:37:00
2017-01-31 11:38:00
2017-01-31 11:39:00
2017-01-31 11:40:00
2017-01-31 11:41:00
2017-01-31 11:42:00
2017-01-31 11:43:00
2017-01-31 11:44:00
2017-01-31 11:45:00
2017-01-31 11:46:00
2017-01-31 11:47:00
2017-01-31 11:48:00
2017-01-31 11:49:00
2017-01-31 11:50:00
2017-01-31 11:51:00
2017-01-31 11:52:00
2017-01-31 11:53:00
2017-01-31 11:54:00
2017-01-31 11:55:00
2017-01-31 11:56:00
2017-01-31 11:57:00
2017-01-31 11:58:00
2017-01-31 11:59:00
2017-01-31 12:00:00
2017-01-31 12:01:00
2017-01-31 12:02:00
2017-01-31 12:03:00
2017-01-31 12:04:00
2017-01-31 12:05:00
2017-01-31 12:06:00
2017-01-31 12:07:00


...

2017-03-03 12:29:00
2017-03-03 12:30:00
2017-03-03 12:31:00
2017-03-03 12:32:00
2017-03-03 12:33:00
2017-03-03 12:34:00
2017-03-03 12:35:00
2017-03-03 12:36:00
2017-03-03 12:37:00
2017-03-03 12:38:00
2017-03-03 12:39:00
2017-03-03 12:40:00
2017-03-03 12:41:00
2017-03-03 12:42:00
2017-03-03 12:43:00
2017-03-03 12:44:00
2017-03-03 12:45:00
2017-03-03 12:46:00
2017-03-03 12:47:00
2017-03-03 12:48:00
2017-03-03 12:49:00
2017-03-03 12:50:00
2017-03-03 12:51:00
2017-03-03 12:52:00
2017-03-03 12:53:00
2017-03-03 12:54:00
2017-03-03 12:55:00
2017-03-03 12:56:00
2017-03-03 12:57:00
2017-03-03 12:58:00
2017-03-03 12:59:00
2017-03-03 13:00:00
2017-03-03 13:01:00
2017-03-03 13:02:00
2017-03-03 13:03:00
2017-03-03 13:04:00
2017-03-03 13:05:00
2017-03-03 13:06:00
2017-03-03 13:07:00
2017-03-03 13:08:00
2017-03-03 13:09:00
2017-03-03 13:10:00
2017-03-03 13:11:00
2017-03-03 13:12:00
2017-03-03 13:13:00
2017-03-03 13:14:00
2017-03-03 13:15:00
2017-03-03 13:16:00
2017-03-03 13:17:00
2017-03-03 13:18:00


2017-03-06 13:08:00
2017-03-06 13:09:00
2017-03-06 13:10:00
2017-03-06 13:11:00
2017-03-06 13:12:00
2017-03-06 13:13:00
2017-03-06 13:14:00
2017-03-06 13:15:00
2017-03-06 13:16:00
2017-03-06 13:17:00
2017-03-06 13:18:00
2017-03-06 13:19:00
2017-03-06 13:20:00
2017-03-06 13:21:00
2017-03-06 13:22:00
2017-03-06 13:23:00
2017-03-06 13:24:00
2017-03-06 13:25:00
2017-03-06 13:26:00
2017-03-06 13:27:00
2017-03-06 13:28:00
2017-03-06 13:29:00
2017-03-06 13:30:00
2017-03-06 13:31:00
2017-03-06 13:32:00
2017-03-06 13:33:00
2017-03-06 13:34:00
2017-03-06 13:35:00
2017-03-06 13:36:00
2017-03-06 13:37:00
2017-03-06 13:38:00
2017-03-06 13:39:00
2017-03-06 13:40:00
2017-03-06 13:41:00
2017-03-06 13:42:00
2017-03-06 13:43:00
2017-03-06 13:44:00
2017-03-06 13:45:00
2017-03-06 13:46:00
2017-03-06 13:47:00
2017-03-06 13:48:00
2017-03-06 13:49:00
2017-03-06 13:50:00
2017-03-06 13:51:00
2017-03-06 13:52:00
2017-03-06 13:53:00
2017-03-06 13:54:00
2017-03-06 13:55:00
2017-03-06 13:56:00
2017-03-06 13:57:00


2017-03-07 13:46:00
2017-03-07 13:47:00
2017-03-07 13:48:00
2017-03-07 13:49:00
2017-03-07 13:50:00
2017-03-07 13:51:00
2017-03-07 13:52:00
2017-03-07 13:53:00
2017-03-07 13:54:00
2017-03-07 13:55:00
2017-03-07 13:56:00
2017-03-07 13:57:00
2017-03-07 13:58:00
2017-03-07 13:59:00
2017-03-07 14:00:00
2017-03-07 14:01:00
2017-03-07 14:02:00
2017-03-07 14:03:00
2017-03-07 14:04:00
2017-03-07 14:05:00
2017-03-07 14:06:00
2017-03-07 14:07:00
2017-03-07 14:08:00
2017-03-07 14:09:00
2017-03-07 14:10:00
2017-03-07 14:11:00
2017-03-07 14:12:00
2017-03-07 14:13:00
2017-03-07 14:14:00
2017-03-07 14:15:00
2017-03-07 14:16:00
2017-03-07 14:17:00
2017-03-07 14:18:00
2017-03-07 14:19:00
2017-03-07 14:20:00
2017-03-07 14:21:00
2017-03-07 14:22:00
2017-03-07 14:23:00
2017-03-07 14:24:00
2017-03-07 14:25:00
2017-03-07 14:26:00
2017-03-07 14:27:00
2017-03-07 14:28:00
2017-03-07 14:29:00
2017-03-07 14:30:00
2017-03-07 14:31:00
2017-03-07 14:32:00
2017-03-07 14:33:00
2017-03-07 14:34:00
2017-03-07 14:35:00


2017-03-08 14:24:00
2017-03-08 14:25:00
2017-03-08 14:26:00
2017-03-08 14:27:00
2017-03-08 14:28:00
2017-03-08 14:29:00
2017-03-08 14:30:00
2017-03-08 14:31:00
2017-03-08 14:32:00
2017-03-08 14:33:00
2017-03-08 14:34:00
2017-03-08 14:35:00
2017-03-08 14:36:00
2017-03-08 14:37:00
2017-03-08 14:38:00
2017-03-08 14:39:00
2017-03-08 14:40:00
2017-03-08 14:41:00
2017-03-08 14:42:00
2017-03-08 14:43:00
2017-03-08 14:44:00
2017-03-08 14:45:00
2017-03-08 14:46:00
2017-03-08 14:47:00
2017-03-08 14:48:00
2017-03-08 14:49:00
2017-03-08 14:50:00
2017-03-08 14:51:00
2017-03-08 14:52:00
2017-03-08 14:53:00
2017-03-08 14:54:00
2017-03-08 14:55:00
2017-03-08 14:56:00
2017-03-08 14:57:00
2017-03-08 14:58:00
2017-03-08 14:59:00
2017-03-08 15:00:00
2017-03-08 15:01:00
2017-03-08 15:02:00
2017-03-08 15:03:00
2017-03-08 15:04:00
2017-03-08 15:05:00
2017-03-08 15:06:00
2017-03-08 15:07:00
2017-03-08 15:08:00
2017-03-08 15:09:00
2017-03-08 15:10:00
2017-03-08 15:11:00
2017-03-08 15:12:00
2017-03-08 15:13:00


2017-03-09 15:02:00
2017-03-09 15:03:00
2017-03-09 15:04:00
2017-03-09 15:05:00
2017-03-09 15:06:00
2017-03-09 15:07:00
2017-03-09 15:08:00
2017-03-09 15:09:00
2017-03-09 15:10:00
2017-03-09 15:11:00
2017-03-09 15:12:00
2017-03-09 15:13:00
2017-03-09 15:14:00
2017-03-09 15:15:00
2017-03-09 15:16:00
2017-03-09 15:17:00
2017-03-09 15:18:00
2017-03-09 15:19:00
2017-03-09 15:20:00
2017-03-09 15:21:00
2017-03-09 15:22:00
2017-03-09 15:23:00
2017-03-09 15:24:00
2017-03-09 15:25:00
2017-03-09 15:26:00
2017-03-09 15:27:00
2017-03-09 15:28:00
Info: DCO:  Total Pnl: 0.02%  Profit/Loss Ratio: 1.21  Accuracy: 0.51  Score: 0.70 
Info: IMC:  Total Pnl: 0.04%  Profit/Loss Ratio: 1.05  Accuracy: 0.47  Score: 0.72 
Info: XYR:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.53  Accuracy: 0.77  Score: 0.70 
Info: WUT:  Total Pnl: -0.00%  Profit/Loss Ratio: 0.89  Accuracy: 0.38  Score: 0.70 
Info: QVE:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.01  Accuracy: 0.49  Score: 0.71 
Info: FFS:  Total Pnl: 0.05%  Profit/Lo

In [50]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_2"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['BSN',
 'DCO',
 'DYE',
 'FFA',
 'FFS',
 'HDK',
 'HZT',
 #'ILW',
 'IMC',
 'IWU',
 #'IYU',
 'KAA',
 'KKG',
 'LPQ',
 'NNA',
 #'NSL',
 'OMP',
 'QTY',
 'QVE',
 'RGG',
 #'WTJ',
 'WUT',
 'XPV',
 'XYR']
       # return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
       #  return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: BSN
Processing data for stock: DCO
Processing data for stock: DYE
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: HDK
Processing data for stock: HZT
Processing data for stock: IMC
Processing data for stock: IWU
Processing data for stock: KAA
Processing data for stock: KKG
Processing data for stock: LPQ
Processing data for stock: NNA
Processing data for stock: OMP
Processing data for stock: QTY
Processing data for stock: QVE
Processing data for stock: RGG
Processing data for stock: WUT
Processing data for stock: XPV
Processing data for stock: XYR
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-02-06 09:17:00
2017-02-06 09:18:00
2017-02-06 09:19:00
2017-02-06 09:20:00
2017-02-06 09:21:00
2017-02-06 09:22:00
2017-02-06 09:23:00
2017-02-06 09:24:00
2017-02-06 09:25:00
2017-02-06 09:26:00
2017-02-06 09:27:00
2017-02-06 09:28:00
2017-02-06

2017-02-07 09:20:00
2017-02-07 09:21:00
2017-02-07 09:22:00
2017-02-07 09:23:00
2017-02-07 09:24:00
2017-02-07 09:25:00
2017-02-07 09:26:00
2017-02-07 09:27:00
2017-02-07 09:28:00
2017-02-07 09:29:00
2017-02-07 09:30:00
2017-02-07 09:31:00
2017-02-07 09:32:00
2017-02-07 09:33:00
2017-02-07 09:34:00
2017-02-07 09:35:00
2017-02-07 09:36:00
2017-02-07 09:37:00
2017-02-07 09:38:00
2017-02-07 09:39:00
2017-02-07 09:40:00
2017-02-07 09:41:00
2017-02-07 09:42:00
2017-02-07 09:43:00
2017-02-07 09:44:00
2017-02-07 09:45:00
2017-02-07 09:46:00
2017-02-07 09:47:00
2017-02-07 09:48:00
2017-02-07 09:49:00
2017-02-07 09:50:00
2017-02-07 09:51:00
2017-02-07 09:52:00
2017-02-07 09:53:00
2017-02-07 09:54:00
2017-02-07 09:55:00
2017-02-07 09:56:00
2017-02-07 09:57:00
2017-02-07 09:58:00
2017-02-07 09:59:00
2017-02-07 10:00:00
2017-02-07 10:01:00
2017-02-07 10:02:00
2017-02-07 10:03:00
2017-02-07 10:04:00
2017-02-07 10:05:00
2017-02-07 10:06:00
2017-02-07 10:07:00
2017-02-07 10:08:00
2017-02-07 10:09:00


2017-02-08 09:59:00
2017-02-08 10:00:00
2017-02-08 10:01:00
2017-02-08 10:02:00
2017-02-08 10:03:00
2017-02-08 10:04:00
2017-02-08 10:05:00
2017-02-08 10:06:00
2017-02-08 10:07:00
2017-02-08 10:08:00
2017-02-08 10:09:00
2017-02-08 10:10:00
2017-02-08 10:11:00
2017-02-08 10:12:00
2017-02-08 10:13:00
2017-02-08 10:14:00
2017-02-08 10:15:00
2017-02-08 10:16:00
2017-02-08 10:17:00
2017-02-08 10:18:00
2017-02-08 10:19:00
2017-02-08 10:20:00
2017-02-08 10:21:00
2017-02-08 10:22:00
2017-02-08 10:23:00
2017-02-08 10:24:00
2017-02-08 10:25:00
2017-02-08 10:26:00
2017-02-08 10:27:00
2017-02-08 10:28:00
2017-02-08 10:29:00
2017-02-08 10:30:00
2017-02-08 10:31:00
2017-02-08 10:32:00
2017-02-08 10:33:00
2017-02-08 10:34:00
2017-02-08 10:35:00
2017-02-08 10:36:00
2017-02-08 10:37:00
2017-02-08 10:38:00
2017-02-08 10:39:00
2017-02-08 10:40:00
2017-02-08 10:41:00
2017-02-08 10:42:00
2017-02-08 10:43:00
2017-02-08 10:44:00
2017-02-08 10:45:00
2017-02-08 10:46:00
2017-02-08 10:47:00
2017-02-08 10:48:00


2017-02-09 10:40:00
2017-02-09 10:41:00
2017-02-09 10:42:00
2017-02-09 10:43:00
2017-02-09 10:44:00
2017-02-09 10:45:00
2017-02-09 10:46:00
2017-02-09 10:47:00
2017-02-09 10:48:00
2017-02-09 10:49:00
2017-02-09 10:50:00
2017-02-09 10:51:00
2017-02-09 10:52:00
2017-02-09 10:53:00
2017-02-09 10:54:00
2017-02-09 10:55:00
2017-02-09 10:56:00
2017-02-09 10:57:00
2017-02-09 10:58:00
2017-02-09 10:59:00
2017-02-09 11:00:00
2017-02-09 11:01:00
2017-02-09 11:02:00
2017-02-09 11:03:00
2017-02-09 11:04:00
2017-02-09 11:05:00
2017-02-09 11:06:00
2017-02-09 11:07:00
2017-02-09 11:08:00
2017-02-09 11:09:00
2017-02-09 11:10:00
2017-02-09 11:11:00
2017-02-09 11:12:00
2017-02-09 11:13:00
2017-02-09 11:14:00
2017-02-09 11:15:00
2017-02-09 11:16:00
2017-02-09 11:17:00
2017-02-09 11:18:00
2017-02-09 11:19:00
2017-02-09 11:20:00
2017-02-09 11:21:00
2017-02-09 11:22:00
2017-02-09 11:23:00
2017-02-09 11:24:00
2017-02-09 11:25:00
2017-02-09 11:26:00
2017-02-09 11:27:00
2017-02-09 11:28:00
2017-02-09 11:29:00


2017-02-10 12:19:00
2017-02-10 12:20:00
2017-02-10 12:21:00
2017-02-10 12:22:00
2017-02-10 12:23:00
2017-02-10 12:24:00
2017-02-10 12:25:00
2017-02-10 12:26:00
2017-02-10 12:27:00
2017-02-10 12:28:00
2017-02-10 12:29:00
2017-02-10 12:30:00
2017-02-10 12:31:00
2017-02-10 12:32:00
2017-02-10 12:33:00
2017-02-10 12:34:00
2017-02-10 12:35:00
2017-02-10 12:36:00
2017-02-10 12:37:00
2017-02-10 12:38:00
2017-02-10 12:39:00
2017-02-10 12:40:00
2017-02-10 12:41:00
2017-02-10 12:42:00
2017-02-10 12:43:00
2017-02-10 12:44:00
2017-02-10 12:45:00
2017-02-10 12:46:00
2017-02-10 12:47:00
2017-02-10 12:48:00
2017-02-10 12:49:00
2017-02-10 12:50:00
2017-02-10 12:51:00
2017-02-10 12:52:00
2017-02-10 12:53:00
2017-02-10 12:54:00
2017-02-10 12:55:00
2017-02-10 12:56:00
2017-02-10 12:57:00
2017-02-10 12:58:00
2017-02-10 12:59:00
2017-02-10 13:00:00
2017-02-10 13:01:00
2017-02-10 13:02:00
2017-02-10 13:03:00
2017-02-10 13:04:00
2017-02-10 13:05:00
2017-02-10 13:06:00
2017-02-10 13:07:00
2017-02-10 13:08:00


...

2017-03-16 13:45:00
2017-03-16 13:46:00
2017-03-16 13:47:00
2017-03-16 13:48:00
2017-03-16 13:49:00
2017-03-16 13:50:00
2017-03-16 13:51:00
2017-03-16 13:52:00
2017-03-16 13:53:00
2017-03-16 13:54:00
2017-03-16 13:55:00
2017-03-16 13:56:00
2017-03-16 13:57:00
2017-03-16 13:58:00
2017-03-16 13:59:00
2017-03-16 14:00:00
2017-03-16 14:01:00
2017-03-16 14:02:00
2017-03-16 14:03:00
2017-03-16 14:04:00
2017-03-16 14:05:00
2017-03-16 14:06:00
2017-03-16 14:07:00
2017-03-16 14:08:00
2017-03-16 14:09:00
2017-03-16 14:10:00
2017-03-16 14:11:00
2017-03-16 14:12:00
2017-03-16 14:13:00
2017-03-16 14:14:00
2017-03-16 14:15:00
2017-03-16 14:16:00
2017-03-16 14:17:00
2017-03-16 14:18:00
2017-03-16 14:19:00
2017-03-16 14:20:00
2017-03-16 14:21:00
2017-03-16 14:22:00
2017-03-16 14:23:00
2017-03-16 14:24:00
2017-03-16 14:25:00
2017-03-16 14:26:00
2017-03-16 14:27:00
2017-03-16 14:28:00
2017-03-16 14:29:00
2017-03-16 14:30:00
2017-03-17 09:17:00
2017-03-17 09:18:00
2017-03-17 09:19:00
2017-03-17 09:20:00


2017-03-17 15:22:00
2017-03-17 15:23:00
2017-03-17 15:24:00
2017-03-17 15:25:00
2017-03-17 15:26:00
2017-03-17 15:27:00
2017-03-17 15:28:00
2017-03-22 09:17:00
2017-03-22 09:18:00
2017-03-22 09:19:00
2017-03-22 09:20:00
2017-03-22 09:21:00
2017-03-22 09:22:00
2017-03-22 09:23:00
2017-03-22 09:24:00
2017-03-22 09:25:00
2017-03-22 09:26:00
2017-03-22 09:27:00
2017-03-22 09:28:00
2017-03-22 09:29:00
2017-03-22 09:30:00
2017-03-22 09:31:00
2017-03-22 09:32:00
2017-03-22 09:33:00
2017-03-22 09:34:00
2017-03-22 09:35:00
2017-03-22 09:36:00
2017-03-22 09:37:00
2017-03-22 09:38:00
2017-03-22 09:39:00
2017-03-22 09:40:00
2017-03-22 09:41:00
2017-03-22 09:42:00
2017-03-22 09:43:00
2017-03-22 09:44:00
2017-03-22 09:45:00
2017-03-22 09:46:00
2017-03-22 09:47:00
2017-03-22 09:48:00
2017-03-22 09:49:00
2017-03-22 09:50:00
2017-03-22 09:51:00
2017-03-22 09:52:00
2017-03-22 09:53:00
2017-03-22 09:54:00
2017-03-22 09:55:00
2017-03-22 09:56:00
2017-03-22 09:57:00
2017-03-22 09:58:00
2017-03-22 09:59:00


2017-03-28 09:48:00
2017-03-28 09:49:00
2017-03-28 09:50:00
2017-03-28 09:51:00
2017-03-28 09:52:00
2017-03-28 09:53:00
2017-03-28 09:54:00
2017-03-28 09:55:00
2017-03-28 09:56:00
2017-03-28 09:57:00
2017-03-28 09:58:00
2017-03-28 09:59:00
2017-03-28 10:00:00
2017-03-28 10:01:00
2017-03-28 10:02:00
2017-03-28 10:03:00
2017-03-28 10:04:00
2017-03-28 10:05:00
2017-03-28 10:06:00
2017-03-28 10:07:00
2017-03-28 10:08:00
2017-03-28 10:09:00
2017-03-28 10:10:00
2017-03-28 10:11:00
2017-03-28 10:12:00
2017-03-28 10:13:00
2017-03-28 10:14:00
2017-03-28 10:15:00
2017-03-28 10:16:00
2017-03-28 10:17:00
2017-03-28 10:18:00
2017-03-28 10:19:00
2017-03-28 10:20:00
2017-03-28 10:21:00
2017-03-28 10:22:00
2017-03-28 10:23:00
2017-03-28 10:24:00
2017-03-28 10:25:00
2017-03-28 10:26:00
2017-03-28 10:27:00
2017-03-28 10:28:00
2017-03-28 10:29:00
2017-03-28 10:30:00
2017-03-28 10:31:00
2017-03-28 10:32:00
2017-03-28 10:33:00
2017-03-28 10:34:00
2017-03-28 10:35:00
2017-03-28 10:36:00
2017-03-28 10:37:00


2017-03-29 10:27:00
2017-03-29 10:28:00
2017-03-29 10:29:00
2017-03-29 10:30:00
2017-03-29 10:31:00
2017-03-29 10:32:00
2017-03-29 10:33:00
2017-03-29 10:34:00
2017-03-29 10:35:00
2017-03-29 10:36:00
2017-03-29 10:37:00
2017-03-29 10:38:00
2017-03-29 10:39:00
2017-03-29 10:40:00
2017-03-29 10:41:00
2017-03-29 10:42:00
2017-03-29 10:43:00
2017-03-29 10:44:00
2017-03-29 10:45:00
2017-03-29 10:46:00
2017-03-29 10:47:00
2017-03-29 10:48:00
2017-03-29 10:49:00
2017-03-29 10:50:00
2017-03-29 10:51:00
2017-03-29 10:52:00
2017-03-29 10:53:00
2017-03-29 10:54:00
2017-03-29 10:55:00
2017-03-29 10:56:00
2017-03-29 10:57:00
2017-03-29 10:58:00
2017-03-29 10:59:00
2017-03-29 11:00:00
2017-03-29 11:01:00
2017-03-29 11:02:00
2017-03-29 11:03:00
2017-03-29 11:04:00
2017-03-29 11:05:00
2017-03-29 11:06:00
2017-03-29 11:07:00
2017-03-29 11:08:00
2017-03-29 11:09:00
2017-03-29 11:10:00
2017-03-29 11:11:00
2017-03-29 11:12:00
2017-03-29 11:13:00
2017-03-29 11:14:00
2017-03-29 11:15:00
2017-03-29 11:16:00


2017-03-30 11:07:00
2017-03-30 11:08:00
2017-03-30 11:09:00
2017-03-30 11:10:00
2017-03-30 11:11:00
2017-03-30 11:12:00
2017-03-30 11:13:00
2017-03-30 11:14:00
2017-03-30 11:15:00
2017-03-30 11:16:00
2017-03-30 11:17:00
2017-03-30 11:18:00
2017-03-30 11:19:00
2017-03-30 11:20:00
2017-03-30 11:21:00
2017-03-30 11:22:00
2017-03-30 11:23:00
2017-03-30 11:24:00
2017-03-30 11:25:00
2017-03-30 11:26:00
2017-03-30 11:27:00
2017-03-30 11:28:00
2017-03-30 11:29:00
2017-03-30 11:30:00
2017-03-30 11:31:00
2017-03-30 11:32:00
2017-03-30 11:33:00
2017-03-30 11:34:00
2017-03-30 11:35:00
2017-03-30 11:36:00
2017-03-30 11:37:00
2017-03-30 11:38:00
2017-03-30 11:39:00
2017-03-30 11:40:00
2017-03-30 11:41:00
2017-03-30 11:42:00
2017-03-30 11:43:00
2017-03-30 11:44:00
2017-03-30 11:45:00
2017-03-30 11:46:00
2017-03-30 11:47:00
2017-03-30 11:48:00
2017-03-30 11:49:00
2017-03-30 11:50:00
2017-03-30 11:51:00
2017-03-30 11:52:00
2017-03-30 11:53:00
2017-03-30 11:54:00
2017-03-30 11:55:00
2017-03-30 11:56:00


In [51]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_3"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['BSN',
 'DCO',
 'DYE',
 'FFA',
 'FFS',
 'HDK',
 'HZT',
 #'ILW',
 'IMC',
 'IWU',
 #'IYU',
 'KAA',
 'KKG',
 'LPQ',
 'NNA',
 #'NSL',
 'OMP',
 'QTY',
 'QVE',
 'RGG',
 #'WTJ',
 'WUT',
 'XPV',
 'XYR']
       # return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
       #  return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 30,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: BSN
Processing data for stock: DCO
Processing data for stock: DYE
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: HDK
Processing data for stock: HZT
Processing data for stock: IMC
Processing data for stock: IWU
Processing data for stock: KAA
Processing data for stock: KKG
Processing data for stock: LPQ
Processing data for stock: NNA
Processing data for stock: OMP
Processing data for stock: QTY
Processing data for stock: QVE
Processing data for stock: RGG
Processing data for stock: WUT
Processing data for stock: XPV
Processing data for stock: XYR
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-02 09:17:00
2017-01-02 09:18:00
2017-01-02 09:19:00
2017-01-02 09:20:00
2017-01-02 09:21:00
2017-01-02 09:22:00
2017-01-02 09:23:00
2017-01-02 09:24:00
2017-01-02 09:25:00
2017-01-02 09:26:00
2017-01-02 09:27:00
2017-01-02 09:28:00
2017-01-02

2017-01-03 09:18:00
2017-01-03 09:19:00
2017-01-03 09:20:00
2017-01-03 09:21:00
2017-01-03 09:22:00
2017-01-03 09:23:00
2017-01-03 09:24:00
2017-01-03 09:25:00
2017-01-03 09:26:00
2017-01-03 09:27:00
2017-01-03 09:28:00
2017-01-03 09:29:00
2017-01-03 09:30:00
2017-01-03 09:31:00
2017-01-03 09:32:00
2017-01-03 09:33:00
2017-01-03 09:34:00
2017-01-03 09:35:00
2017-01-03 09:36:00
2017-01-03 09:37:00
2017-01-03 09:38:00
2017-01-03 09:39:00
2017-01-03 09:40:00
2017-01-03 09:41:00
2017-01-03 09:42:00
2017-01-03 09:43:00
2017-01-03 09:44:00
2017-01-03 09:45:00
2017-01-03 09:46:00
2017-01-03 09:47:00
2017-01-03 09:48:00
2017-01-03 09:49:00
2017-01-03 09:50:00
2017-01-03 09:51:00
2017-01-03 09:52:00
2017-01-03 09:53:00
2017-01-03 09:54:00
2017-01-03 09:55:00
2017-01-03 09:56:00
2017-01-03 09:57:00
2017-01-03 09:58:00
2017-01-03 09:59:00
2017-01-03 10:00:00
2017-01-03 10:01:00
2017-01-03 10:02:00
2017-01-03 10:03:00
2017-01-03 10:04:00
2017-01-03 10:05:00
2017-01-03 10:06:00
2017-01-03 10:07:00


2017-01-04 09:56:00
2017-01-04 09:57:00
2017-01-04 09:58:00
2017-01-04 09:59:00
2017-01-04 10:00:00
2017-01-04 10:01:00
2017-01-04 10:02:00
2017-01-04 10:03:00
2017-01-04 10:04:00
2017-01-04 10:05:00
2017-01-04 10:06:00
2017-01-04 10:07:00
2017-01-04 10:08:00
2017-01-04 10:09:00
2017-01-04 10:10:00
2017-01-04 10:11:00
2017-01-04 10:12:00
2017-01-04 10:13:00
2017-01-04 10:14:00
2017-01-04 10:15:00
2017-01-04 10:16:00
2017-01-04 10:17:00
2017-01-04 10:18:00
2017-01-04 10:19:00
2017-01-04 10:20:00
2017-01-04 10:21:00
2017-01-04 10:22:00
2017-01-04 10:23:00
2017-01-04 10:24:00
2017-01-04 10:25:00
2017-01-04 10:26:00
2017-01-04 10:27:00
2017-01-04 10:28:00
2017-01-04 10:29:00
2017-01-04 10:30:00
2017-01-04 10:31:00
2017-01-04 10:32:00
2017-01-04 10:33:00
2017-01-04 10:34:00
2017-01-04 10:35:00
2017-01-04 10:36:00
2017-01-04 10:37:00
2017-01-04 10:38:00
2017-01-04 10:39:00
2017-01-04 10:40:00
2017-01-04 10:41:00
2017-01-04 10:42:00
2017-01-04 10:43:00
2017-01-04 10:44:00
2017-01-04 10:45:00


2017-01-05 10:34:00
2017-01-05 10:35:00
2017-01-05 10:36:00
2017-01-05 10:37:00
2017-01-05 10:38:00
2017-01-05 10:39:00
2017-01-05 10:40:00
2017-01-05 10:41:00
2017-01-05 10:42:00
2017-01-05 10:43:00
2017-01-05 10:44:00
2017-01-05 10:45:00
2017-01-05 10:46:00
2017-01-05 10:47:00
2017-01-05 10:48:00
2017-01-05 10:49:00
2017-01-05 10:50:00
2017-01-05 10:51:00
2017-01-05 10:52:00
2017-01-05 10:53:00
2017-01-05 10:54:00
2017-01-05 10:55:00
2017-01-05 10:56:00
2017-01-05 10:57:00
2017-01-05 10:58:00
2017-01-05 10:59:00
2017-01-05 11:00:00
2017-01-05 11:01:00
2017-01-05 11:02:00
2017-01-05 11:03:00
2017-01-05 11:04:00
2017-01-05 11:05:00
2017-01-05 11:06:00
2017-01-05 11:07:00
2017-01-05 11:08:00
2017-01-05 11:09:00
2017-01-05 11:10:00
2017-01-05 11:11:00
2017-01-05 11:12:00
2017-01-05 11:13:00
2017-01-05 11:14:00
2017-01-05 11:15:00
2017-01-05 11:16:00
2017-01-05 11:17:00
2017-01-05 11:18:00
2017-01-05 11:19:00
2017-01-05 11:20:00
2017-01-05 11:21:00
2017-01-05 11:22:00
2017-01-05 11:23:00


2017-01-06 11:16:00
2017-01-06 11:17:00
2017-01-06 11:18:00
2017-01-06 11:19:00
2017-01-06 11:20:00
2017-01-06 11:21:00
2017-01-06 11:22:00
2017-01-06 11:23:00
2017-01-06 11:24:00
2017-01-06 11:25:00
2017-01-06 11:26:00
2017-01-06 11:27:00
2017-01-06 11:28:00
2017-01-06 11:29:00
2017-01-06 11:30:00
2017-01-06 11:31:00
2017-01-06 11:32:00
2017-01-06 11:33:00
2017-01-06 11:34:00
2017-01-06 11:35:00
2017-01-06 11:36:00
2017-01-06 11:37:00
2017-01-06 11:38:00
2017-01-06 11:39:00
2017-01-06 11:40:00
2017-01-06 11:41:00
2017-01-06 11:42:00
2017-01-06 11:43:00
2017-01-06 11:44:00
2017-01-06 11:45:00
2017-01-06 11:46:00
2017-01-06 11:47:00
2017-01-06 11:48:00
2017-01-06 11:49:00
2017-01-06 11:50:00
2017-01-06 11:51:00
2017-01-06 11:52:00
2017-01-06 11:53:00
2017-01-06 11:54:00
2017-01-06 11:55:00
2017-01-06 11:56:00
2017-01-06 11:57:00
2017-01-06 11:58:00
2017-01-06 11:59:00
2017-01-06 12:00:00
2017-01-06 12:01:00
2017-01-06 12:02:00
2017-01-06 12:03:00
2017-01-06 12:04:00
2017-01-06 12:05:00


...

2017-01-24 12:21:00
2017-01-24 12:22:00
2017-01-24 12:23:00
2017-01-24 12:24:00
2017-01-24 12:25:00
2017-01-24 12:26:00
2017-01-24 12:27:00
2017-01-24 12:28:00
2017-01-24 12:29:00
2017-01-24 12:30:00
2017-01-24 12:31:00
2017-01-24 12:32:00
2017-01-24 12:33:00
2017-01-24 12:34:00
2017-01-24 12:35:00
2017-01-24 12:36:00
2017-01-24 12:37:00
2017-01-24 12:38:00
2017-01-24 12:39:00
2017-01-24 12:40:00
2017-01-24 12:41:00
2017-01-24 12:42:00
2017-01-24 12:43:00
2017-01-24 12:44:00
2017-01-24 12:45:00
2017-01-24 12:46:00
2017-01-24 12:47:00
2017-01-24 12:48:00
2017-01-24 12:49:00
2017-01-24 12:50:00
2017-01-24 12:51:00
2017-01-24 12:52:00
2017-01-24 12:53:00
2017-01-24 12:54:00
2017-01-24 12:55:00
2017-01-24 12:56:00
2017-01-24 12:57:00
2017-01-24 12:58:00
2017-01-24 12:59:00
2017-01-24 13:00:00
2017-01-24 13:01:00
2017-01-24 13:02:00
2017-01-24 13:03:00
2017-01-24 13:04:00
2017-01-24 13:05:00
2017-01-24 13:06:00
2017-01-24 13:07:00
2017-01-24 13:08:00
2017-01-24 13:09:00
2017-01-24 13:10:00


2017-01-25 12:59:00
2017-01-25 13:00:00
2017-01-25 13:01:00
2017-01-25 13:02:00
2017-01-25 13:03:00
2017-01-25 13:04:00
2017-01-25 13:05:00
2017-01-25 13:06:00
2017-01-25 13:07:00
2017-01-25 13:08:00
2017-01-25 13:09:00
2017-01-25 13:10:00
2017-01-25 13:11:00
2017-01-25 13:12:00
2017-01-25 13:13:00
2017-01-25 13:14:00
2017-01-25 13:15:00
2017-01-25 13:16:00
2017-01-25 13:17:00
2017-01-25 13:18:00
2017-01-25 13:19:00
2017-01-25 13:20:00
2017-01-25 13:21:00
2017-01-25 13:22:00
2017-01-25 13:23:00
2017-01-25 13:24:00
2017-01-25 13:25:00
2017-01-25 13:26:00
2017-01-25 13:27:00
2017-01-25 13:28:00
2017-01-25 13:29:00
2017-01-25 13:30:00
2017-01-25 13:31:00
2017-01-25 13:32:00
2017-01-25 13:33:00
2017-01-25 13:34:00
2017-01-25 13:35:00
2017-01-25 13:36:00
2017-01-25 13:37:00
2017-01-25 13:38:00
2017-01-25 13:39:00
2017-01-25 13:40:00
2017-01-25 13:41:00
2017-01-25 13:42:00
2017-01-25 13:43:00
2017-01-25 13:44:00
2017-01-25 13:45:00
2017-01-25 13:46:00
2017-01-25 13:47:00
2017-01-25 13:48:00


2017-01-27 13:37:00
2017-01-27 13:38:00
2017-01-27 13:39:00
2017-01-27 13:40:00
2017-01-27 13:41:00
2017-01-27 13:42:00
2017-01-27 13:43:00
2017-01-27 13:44:00
2017-01-27 13:45:00
2017-01-27 13:46:00
2017-01-27 13:47:00
2017-01-27 13:48:00
2017-01-27 13:49:00
2017-01-27 13:50:00
2017-01-27 13:51:00
2017-01-27 13:52:00
2017-01-27 13:53:00
2017-01-27 13:54:00
2017-01-27 13:55:00
2017-01-27 13:56:00
2017-01-27 13:57:00
2017-01-27 13:58:00
2017-01-27 13:59:00
2017-01-27 14:00:00
2017-01-27 14:01:00
2017-01-27 14:02:00
2017-01-27 14:03:00
2017-01-27 14:04:00
2017-01-27 14:05:00
2017-01-27 14:06:00
2017-01-27 14:07:00
2017-01-27 14:08:00
2017-01-27 14:09:00
2017-01-27 14:10:00
2017-01-27 14:11:00
2017-01-27 14:12:00
2017-01-27 14:13:00
2017-01-27 14:14:00
2017-01-27 14:15:00
2017-01-27 14:16:00
2017-01-27 14:17:00
2017-01-27 14:18:00
2017-01-27 14:19:00
2017-01-27 14:20:00
2017-01-27 14:21:00
2017-01-27 14:22:00
2017-01-27 14:23:00
2017-01-27 14:24:00
2017-01-27 14:25:00
2017-01-27 14:26:00


2017-01-30 14:15:00
2017-01-30 14:16:00
2017-01-30 14:17:00
2017-01-30 14:18:00
2017-01-30 14:19:00
2017-01-30 14:20:00
2017-01-30 14:21:00
2017-01-30 14:22:00
2017-01-30 14:23:00
2017-01-30 14:24:00
2017-01-30 14:25:00
2017-01-30 14:26:00
2017-01-30 14:27:00
2017-01-30 14:28:00
2017-01-30 14:29:00
2017-01-30 14:30:00
2017-01-30 14:31:00
2017-01-30 14:32:00
2017-01-30 14:33:00
2017-01-30 14:34:00
2017-01-30 14:35:00
2017-01-30 14:36:00
2017-01-30 14:37:00
2017-01-30 14:38:00
2017-01-30 14:39:00
2017-01-30 14:40:00
2017-01-30 14:41:00
2017-01-30 14:42:00
2017-01-30 14:43:00
2017-01-30 14:44:00
2017-01-30 14:45:00
2017-01-30 14:46:00
2017-01-30 14:47:00
2017-01-30 14:48:00
2017-01-30 14:49:00
2017-01-30 14:50:00
2017-01-30 14:51:00
2017-01-30 14:52:00
2017-01-30 14:53:00
2017-01-30 14:54:00
2017-01-30 14:55:00
2017-01-30 14:56:00
2017-01-30 14:57:00
2017-01-30 14:58:00
2017-01-30 14:59:00
2017-01-30 15:00:00
2017-01-30 15:01:00
2017-01-30 15:02:00
2017-01-30 15:03:00
2017-01-30 15:04:00


2017-01-31 14:57:00
2017-01-31 14:58:00
2017-01-31 14:59:00
Info: DCO:  Total Pnl: -0.00%  Profit/Loss Ratio: 0.91  Accuracy: 0.48  Score: 0.70 
Info: IMC:  Total Pnl: -0.04%  Profit/Loss Ratio: 0.96  Accuracy: 0.47  Score: 0.73 
Info: XYR:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.15  Accuracy: 0.43  Score: 0.70 
Info: WUT:  Total Pnl: 0.00%  Profit/Loss Ratio: nan  Accuracy: 0.00  Score: 0.69 
Info: QVE:  Total Pnl: 0.06%  Profit/Loss Ratio: 1.75  Accuracy: 0.45  Score: 0.69 
Info: FFS:  Total Pnl: 0.03%  Profit/Loss Ratio: 1.03  Accuracy: 0.49  Score: 0.76 
Info: IWU:  Total Pnl: 0.02%  Profit/Loss Ratio: 1.46  Accuracy: 0.53  Score: 0.70 
Info: LPQ:  Total Pnl: 0.02%  Profit/Loss Ratio: 1.76  Accuracy: 0.46  Score: 0.70 
Info: QTY:  Total Pnl: -0.02%  Profit/Loss Ratio: 0.80  Accuracy: 0.47  Score: 0.71 
Info: HZT:  Total Pnl: 0.00%  Profit/Loss Ratio: nan  Accuracy: 0.00  Score: 0.69 
Info: BSN:  Total Pnl: 0.00%  Profit/Loss Ratio: nan  Accuracy: 0.00  Score: 0.69 
Info: OMP:  Tota

In [2]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['BSN'
#  'DCO',
#  'DYE',
#  'FFA',
#  'FFS',
#  'HDK',
#  'HZT',
#  #'ILW',
#  'IMC',
#  'IWU',
#  #'IYU',
#  'KAA',
#  'KKG',
#  'LPQ',
#  'NNA',
#  #'NSL',
#  'OMP',
#  'QTY',
#  'QVE',
#  'RGG',
#  #'WTJ',
#  'WUT',
#  'XPV',
#  'XYR'
               ]
       # return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
       #  return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 20,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: BSN
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-25 09:17:00
2017-01-25 09:18:00
2017-01-25 09:19:00
2017-01-25 09:20:00
2017-01-25 09:21:00
2017-01-25 09:22:00
2017-01-25 09:23:00
2017-01-25 09:24:00
2017-01-25 09:25:00
2017-01-25 09:26:00
2017-01-25 09:27:00
2017-01-25 09:28:00
2017-01-25 09:29:00
2017-01-25 09:30:00
2017-01-25 09:31:00
2017-01-25 09:32:00
2017-01-25 09:33:00
2017-01-25 09:34:00
2017-01-25 09:35:00
2017-01-25 09:36:00
2017-01-25 09:37:00
2017-01-25 09:38:00
2017-01-25 09:39:00
2017-01-25 09:40:00
2017-01-25 09:41:00
2017-01-25 09:42:00
2017-01-25 09:43:00
2017-01-25 09:44:00
2017-01-25 09:45:00
2017-01-25 09:46:00
2017-01-25 09:47:00
2017-01-25 09:48:00
2017-01-25 09:49:00
2017-01-25 09:50:00
2017-01-25 09:51:00
2017-01-25 09:52:00
2017-01-25 09:53:00
2017-01-25 09:54:00
2017-01-25 09:55:00
2017-01-25 09:56:00
2017-01-25 09:57:00
2017-01-25 09:58:00

2017-01-26 09:48:00
2017-01-26 09:49:00
2017-01-26 09:50:00
2017-01-26 09:51:00
2017-01-26 09:52:00
2017-01-26 09:53:00
2017-01-26 09:54:00
2017-01-26 09:55:00
2017-01-26 09:56:00
2017-01-26 09:57:00
2017-01-26 09:58:00
2017-01-26 09:59:00
2017-01-26 10:00:00
2017-01-26 10:01:00
2017-01-26 10:02:00
2017-01-26 10:03:00
2017-01-26 10:04:00
2017-01-26 10:05:00
2017-01-26 10:06:00
2017-01-26 10:07:00
2017-01-26 10:08:00
2017-01-26 10:09:00
2017-01-26 10:10:00
2017-01-26 10:11:00
2017-01-26 10:12:00
2017-01-26 10:13:00
2017-01-26 10:14:00
2017-01-26 10:15:00
2017-01-26 10:16:00
2017-01-26 10:17:00
2017-01-26 10:18:00
2017-01-26 10:19:00
2017-01-26 10:20:00
2017-01-26 10:21:00
2017-01-26 10:22:00
2017-01-26 10:23:00
2017-01-26 10:24:00
2017-01-26 10:25:00
2017-01-26 10:26:00
2017-01-26 10:27:00
2017-01-26 10:28:00
2017-01-26 10:29:00
2017-01-26 10:30:00
2017-01-26 10:31:00
2017-01-26 10:32:00
2017-01-26 10:33:00
2017-01-26 10:34:00
2017-01-26 10:35:00
2017-01-26 10:36:00
2017-01-26 10:37:00


2017-01-27 10:27:00
2017-01-27 10:28:00
2017-01-27 10:29:00
2017-01-27 10:30:00
2017-01-27 10:31:00
2017-01-27 10:32:00
2017-01-27 10:33:00
2017-01-27 10:34:00
2017-01-27 10:35:00
2017-01-27 10:36:00
2017-01-27 10:37:00
2017-01-27 10:38:00
2017-01-27 10:39:00
2017-01-27 10:40:00
2017-01-27 10:41:00
2017-01-27 10:42:00
2017-01-27 10:43:00
2017-01-27 10:44:00
2017-01-27 10:45:00
2017-01-27 10:46:00
2017-01-27 10:47:00
2017-01-27 10:48:00
2017-01-27 10:49:00
2017-01-27 10:50:00
2017-01-27 10:51:00
2017-01-27 10:52:00
2017-01-27 10:53:00
2017-01-27 10:54:00
2017-01-27 10:55:00
2017-01-27 10:56:00
2017-01-27 10:57:00
2017-01-27 10:58:00
2017-01-27 10:59:00
2017-01-27 11:00:00
2017-01-27 11:01:00
2017-01-27 11:02:00
2017-01-27 11:03:00
2017-01-27 11:04:00
2017-01-27 11:05:00
2017-01-27 11:06:00
2017-01-27 11:07:00
2017-01-27 11:08:00
2017-01-27 11:09:00
2017-01-27 11:10:00
2017-01-27 11:11:00
2017-01-27 11:12:00
2017-01-27 11:13:00
2017-01-27 11:14:00
2017-01-27 11:15:00
2017-01-27 11:16:00


2017-01-30 11:05:00
2017-01-30 11:06:00
2017-01-30 11:07:00
2017-01-30 11:08:00
2017-01-30 11:09:00
2017-01-30 11:10:00
2017-01-30 11:11:00
2017-01-30 11:12:00
2017-01-30 11:13:00
2017-01-30 11:14:00
2017-01-30 11:15:00
2017-01-30 11:16:00
2017-01-30 11:17:00
2017-01-30 11:18:00
2017-01-30 11:19:00
2017-01-30 11:20:00
2017-01-30 11:21:00
2017-01-30 11:22:00
2017-01-30 11:23:00
2017-01-30 11:24:00
2017-01-30 11:25:00
2017-01-30 11:26:00
2017-01-30 11:27:00
2017-01-30 11:28:00
2017-01-30 11:29:00
2017-01-30 11:30:00
2017-01-30 11:31:00
2017-01-30 11:32:00
2017-01-30 11:33:00
2017-01-30 11:34:00
2017-01-30 11:35:00
2017-01-30 11:36:00
2017-01-30 11:37:00
2017-01-30 11:38:00
2017-01-30 11:39:00
2017-01-30 11:40:00
2017-01-30 11:41:00
2017-01-30 11:42:00
2017-01-30 11:43:00
2017-01-30 11:44:00
2017-01-30 11:45:00
2017-01-30 11:46:00
2017-01-30 11:47:00
2017-01-30 11:48:00
2017-01-30 11:49:00
2017-01-30 11:50:00
2017-01-30 11:51:00
2017-01-30 11:52:00
2017-01-30 11:53:00
2017-01-30 11:54:00


2017-01-31 11:47:00
2017-01-31 11:48:00
2017-01-31 11:49:00
2017-01-31 11:50:00
2017-01-31 11:51:00
2017-01-31 11:52:00
2017-01-31 11:53:00
2017-01-31 11:54:00
2017-01-31 11:55:00
2017-01-31 11:56:00
2017-01-31 11:57:00
2017-01-31 11:58:00
2017-01-31 11:59:00
2017-01-31 12:00:00
2017-01-31 12:01:00
2017-01-31 12:02:00
2017-01-31 12:03:00
2017-01-31 12:04:00
2017-01-31 12:05:00
2017-01-31 12:06:00
2017-01-31 12:07:00
2017-01-31 12:08:00
2017-01-31 12:09:00
2017-01-31 12:10:00
2017-01-31 12:11:00
2017-01-31 12:12:00
2017-01-31 12:13:00
2017-01-31 12:14:00
2017-01-31 12:15:00
2017-01-31 12:16:00
2017-01-31 12:17:00
2017-01-31 12:18:00
2017-01-31 12:19:00
2017-01-31 12:20:00
2017-01-31 12:21:00
2017-01-31 12:22:00
2017-01-31 12:23:00
2017-01-31 12:24:00
2017-01-31 12:25:00
2017-01-31 12:26:00
2017-01-31 12:27:00
2017-01-31 12:28:00
2017-01-31 12:29:00
2017-01-31 12:30:00
2017-01-31 12:31:00
2017-01-31 12:32:00
2017-01-31 12:33:00
2017-01-31 12:34:00
2017-01-31 12:35:00
2017-01-31 12:36:00


...

2017-03-02 12:16:00
2017-03-02 12:17:00
2017-03-02 12:18:00
2017-03-02 12:19:00
2017-03-02 12:20:00
2017-03-02 12:21:00
2017-03-02 12:22:00
2017-03-02 12:23:00
2017-03-02 12:24:00
2017-03-02 12:25:00
2017-03-02 12:26:00
2017-03-02 12:27:00
2017-03-02 12:28:00
2017-03-02 12:29:00
2017-03-02 12:30:00
2017-03-02 12:31:00
2017-03-02 12:32:00
2017-03-02 12:33:00
2017-03-02 12:34:00
2017-03-02 12:35:00
2017-03-02 12:36:00
2017-03-02 12:37:00
2017-03-02 12:38:00
2017-03-02 12:39:00
2017-03-02 12:40:00
2017-03-02 12:41:00
2017-03-02 12:42:00
2017-03-02 12:43:00
2017-03-02 12:44:00
2017-03-02 12:45:00
2017-03-02 12:46:00
2017-03-02 12:47:00
2017-03-02 12:48:00
2017-03-02 12:49:00
2017-03-02 12:50:00
2017-03-02 12:51:00
2017-03-02 12:52:00
2017-03-02 12:53:00
2017-03-02 12:54:00
2017-03-02 12:55:00
2017-03-02 12:56:00
2017-03-02 12:57:00
2017-03-02 12:58:00
2017-03-02 12:59:00
2017-03-02 13:00:00
2017-03-02 13:01:00
2017-03-02 13:02:00
2017-03-02 13:03:00
2017-03-02 13:04:00
2017-03-02 13:05:00


2017-03-03 12:54:00
2017-03-03 12:55:00
2017-03-03 12:56:00
2017-03-03 12:57:00
2017-03-03 12:58:00
2017-03-03 12:59:00
2017-03-03 13:00:00
2017-03-03 13:01:00
2017-03-03 13:02:00
2017-03-03 13:03:00
2017-03-03 13:04:00
2017-03-03 13:05:00
2017-03-03 13:06:00
2017-03-03 13:07:00
2017-03-03 13:08:00
2017-03-03 13:09:00
2017-03-03 13:10:00
2017-03-03 13:11:00
2017-03-03 13:12:00
2017-03-03 13:13:00
2017-03-03 13:14:00
2017-03-03 13:15:00
2017-03-03 13:16:00
2017-03-03 13:17:00
2017-03-03 13:18:00
2017-03-03 13:19:00
2017-03-03 13:20:00
2017-03-03 13:21:00
2017-03-03 13:22:00
2017-03-03 13:23:00
2017-03-03 13:24:00
2017-03-03 13:25:00
2017-03-03 13:26:00
2017-03-03 13:27:00
2017-03-03 13:28:00
2017-03-03 13:29:00
2017-03-03 13:30:00
2017-03-03 13:31:00
2017-03-03 13:32:00
2017-03-03 13:33:00
2017-03-03 13:34:00
2017-03-03 13:35:00
2017-03-03 13:36:00
2017-03-03 13:37:00
2017-03-03 13:38:00
2017-03-03 13:39:00
2017-03-03 13:40:00
2017-03-03 13:41:00
2017-03-03 13:42:00
2017-03-03 13:43:00


2017-03-06 13:36:00
2017-03-06 13:37:00
2017-03-06 13:38:00
2017-03-06 13:39:00
2017-03-06 13:40:00
2017-03-06 13:41:00
2017-03-06 13:42:00
2017-03-06 13:43:00
2017-03-06 13:44:00
2017-03-06 13:45:00
2017-03-06 13:46:00
2017-03-06 13:47:00
2017-03-06 13:48:00
2017-03-06 13:49:00
2017-03-06 13:50:00
2017-03-06 13:51:00
2017-03-06 13:52:00
2017-03-06 13:53:00
2017-03-06 13:54:00
2017-03-06 13:55:00
2017-03-06 13:56:00
2017-03-06 13:57:00
2017-03-06 13:58:00
2017-03-06 13:59:00
2017-03-06 14:00:00
2017-03-06 14:01:00
2017-03-06 14:02:00
2017-03-06 14:03:00
2017-03-06 14:04:00
2017-03-06 14:05:00
2017-03-06 14:06:00
2017-03-06 14:07:00
2017-03-06 14:08:00
2017-03-06 14:09:00
2017-03-06 14:10:00
2017-03-06 14:11:00
2017-03-06 14:12:00
2017-03-06 14:13:00
2017-03-06 14:14:00
2017-03-06 14:15:00
2017-03-06 14:16:00
2017-03-06 14:17:00
2017-03-06 14:18:00
2017-03-06 14:19:00
2017-03-06 14:20:00
2017-03-06 14:21:00
2017-03-06 14:22:00
2017-03-06 14:23:00
2017-03-06 14:24:00
2017-03-06 14:25:00


2017-03-07 14:17:00
2017-03-07 14:18:00
2017-03-07 14:19:00
2017-03-07 14:20:00
2017-03-07 14:21:00
2017-03-07 14:22:00
2017-03-07 14:23:00
2017-03-07 14:24:00
2017-03-07 14:25:00
2017-03-07 14:26:00
2017-03-07 14:27:00
2017-03-07 14:28:00
2017-03-07 14:29:00
2017-03-07 14:30:00
2017-03-07 14:31:00
2017-03-07 14:32:00
2017-03-07 14:33:00
2017-03-07 14:34:00
2017-03-07 14:35:00
2017-03-07 14:36:00
2017-03-07 14:37:00
2017-03-07 14:38:00
2017-03-07 14:39:00
2017-03-07 14:40:00
2017-03-07 14:41:00
2017-03-07 14:42:00
2017-03-07 14:43:00
2017-03-07 14:44:00
2017-03-07 14:45:00
2017-03-07 14:46:00
2017-03-07 14:47:00
2017-03-07 14:48:00
2017-03-07 14:49:00
2017-03-07 14:50:00
2017-03-07 14:51:00
2017-03-07 14:52:00
2017-03-07 14:53:00
2017-03-07 14:54:00
2017-03-07 14:55:00
2017-03-07 14:56:00
2017-03-07 14:57:00
2017-03-07 14:58:00
2017-03-07 14:59:00
2017-03-07 15:00:00
2017-03-07 15:01:00
2017-03-07 15:02:00
2017-03-07 15:03:00
2017-03-07 15:04:00
2017-03-07 15:05:00
2017-03-07 15:06:00


2017-03-08 15:00:00
2017-03-08 15:01:00
2017-03-08 15:02:00
2017-03-08 15:03:00
2017-03-08 15:04:00
2017-03-08 15:05:00
2017-03-08 15:06:00
2017-03-08 15:07:00
2017-03-08 15:08:00
2017-03-08 15:09:00
2017-03-08 15:10:00
2017-03-08 15:11:00
2017-03-08 15:12:00
2017-03-08 15:13:00
2017-03-08 15:14:00
2017-03-08 15:15:00
2017-03-08 15:16:00
2017-03-08 15:17:00
2017-03-08 15:18:00
2017-03-08 15:19:00
2017-03-08 15:20:00
2017-03-08 15:21:00
2017-03-08 15:22:00
2017-03-08 15:23:00
2017-03-08 15:24:00
2017-03-08 15:25:00
2017-03-08 15:26:00
2017-03-08 15:27:00
2017-03-08 15:28:00
2017-03-09 09:17:00
2017-03-09 09:18:00
2017-03-09 09:19:00
2017-03-09 09:20:00
2017-03-09 09:21:00
2017-03-09 09:22:00
2017-03-09 09:23:00
2017-03-09 09:24:00
2017-03-09 09:25:00
2017-03-09 09:26:00
2017-03-09 09:27:00
2017-03-09 09:28:00
2017-03-09 09:29:00
2017-03-09 09:30:00
2017-03-09 09:31:00
2017-03-09 09:32:00
2017-03-09 09:33:00
2017-03-09 09:34:00
2017-03-09 09:35:00
2017-03-09 09:36:00
2017-03-09 09:37:00


In [3]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
        return ['BSN'
#  'DCO',
#  'DYE',
#  'FFA',
#  'FFS',
#  'HDK',
#  'HZT',
#  #'ILW',
#  'IMC',
#  'IWU',
#  #'IYU',
#  'KAA',
#  'KKG',
#  'LPQ',
#  'NNA',
#  #'NSL',
#  'OMP',
#  'QTY',
#  'QVE',
#  'RGG',
#  #'WTJ',
#  'WUT',
#  'XPV',
#  'XYR'
               ]
       # return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
       #  return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 20,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: BSN
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-25 09:17:00
2017-01-25 09:18:00
2017-01-25 09:19:00
2017-01-25 09:20:00
2017-01-25 09:21:00
2017-01-25 09:22:00
2017-01-25 09:23:00
2017-01-25 09:24:00
2017-01-25 09:25:00
2017-01-25 09:26:00
2017-01-25 09:27:00
2017-01-25 09:28:00
2017-01-25 09:29:00
2017-01-25 09:30:00
2017-01-25 09:31:00
2017-01-25 09:32:00
2017-01-25 09:33:00
2017-01-25 09:34:00
2017-01-25 09:35:00
2017-01-25 09:36:00
2017-01-25 09:37:00
2017-01-25 09:38:00
2017-01-25 09:39:00
2017-01-25 09:40:00
2017-01-25 09:41:00
2017-01-25 09:42:00
2017-01-25 09:43:00
2017-01-25 09:44:00
2017-01-25 09:45:00
2017-01-25 09:46:00
2017-01-25 09:47:00
2017-01-25 09:48:00
2017-01-25 09:49:00
2017-01-25 09:50:00
2017-01-25 09:51:00
2017-01-25 09:52:00
2017-01-25 09:53:00
2017-01-25 09:54:00
2017-01-25 09:55:00
2017-01-25 09:56:00
2017-01-25 09:57:00
2017-01-25 09:58:00

2017-01-26 09:48:00
2017-01-26 09:49:00
2017-01-26 09:50:00
2017-01-26 09:51:00
2017-01-26 09:52:00
2017-01-26 09:53:00
2017-01-26 09:54:00
2017-01-26 09:55:00
2017-01-26 09:56:00
2017-01-26 09:57:00
2017-01-26 09:58:00
2017-01-26 09:59:00
2017-01-26 10:00:00
2017-01-26 10:01:00
2017-01-26 10:02:00
2017-01-26 10:03:00
2017-01-26 10:04:00
2017-01-26 10:05:00
2017-01-26 10:06:00
2017-01-26 10:07:00
2017-01-26 10:08:00
2017-01-26 10:09:00
2017-01-26 10:10:00
2017-01-26 10:11:00
2017-01-26 10:12:00
2017-01-26 10:13:00
2017-01-26 10:14:00
2017-01-26 10:15:00
2017-01-26 10:16:00
2017-01-26 10:17:00
2017-01-26 10:18:00
2017-01-26 10:19:00
2017-01-26 10:20:00
2017-01-26 10:21:00
2017-01-26 10:22:00
2017-01-26 10:23:00
2017-01-26 10:24:00
2017-01-26 10:25:00
2017-01-26 10:26:00
2017-01-26 10:27:00
2017-01-26 10:28:00
2017-01-26 10:29:00
2017-01-26 10:30:00
2017-01-26 10:31:00
2017-01-26 10:32:00
2017-01-26 10:33:00
2017-01-26 10:34:00
2017-01-26 10:35:00
2017-01-26 10:36:00
2017-01-26 10:37:00


2017-01-27 10:26:00
2017-01-27 10:27:00
2017-01-27 10:28:00
2017-01-27 10:29:00
2017-01-27 10:30:00
2017-01-27 10:31:00
2017-01-27 10:32:00
2017-01-27 10:33:00
2017-01-27 10:34:00
2017-01-27 10:35:00
2017-01-27 10:36:00
2017-01-27 10:37:00
2017-01-27 10:38:00
2017-01-27 10:39:00
2017-01-27 10:40:00
2017-01-27 10:41:00
2017-01-27 10:42:00
2017-01-27 10:43:00
2017-01-27 10:44:00
2017-01-27 10:45:00
2017-01-27 10:46:00
2017-01-27 10:47:00
2017-01-27 10:48:00
2017-01-27 10:49:00
2017-01-27 10:50:00
2017-01-27 10:51:00
2017-01-27 10:52:00
2017-01-27 10:53:00
2017-01-27 10:54:00
2017-01-27 10:55:00
2017-01-27 10:56:00
2017-01-27 10:57:00
2017-01-27 10:58:00
2017-01-27 10:59:00
2017-01-27 11:00:00
2017-01-27 11:01:00
2017-01-27 11:02:00
2017-01-27 11:03:00
2017-01-27 11:04:00
2017-01-27 11:05:00
2017-01-27 11:06:00
2017-01-27 11:07:00
2017-01-27 11:08:00
2017-01-27 11:09:00
2017-01-27 11:10:00
2017-01-27 11:11:00
2017-01-27 11:12:00
2017-01-27 11:13:00
2017-01-27 11:14:00
2017-01-27 11:15:00


2017-01-30 11:04:00
2017-01-30 11:05:00
2017-01-30 11:06:00
2017-01-30 11:07:00
2017-01-30 11:08:00
2017-01-30 11:09:00
2017-01-30 11:10:00
2017-01-30 11:11:00
2017-01-30 11:12:00
2017-01-30 11:13:00
2017-01-30 11:14:00
2017-01-30 11:15:00
2017-01-30 11:16:00
2017-01-30 11:17:00
2017-01-30 11:18:00
2017-01-30 11:19:00
2017-01-30 11:20:00
2017-01-30 11:21:00
2017-01-30 11:22:00
2017-01-30 11:23:00
2017-01-30 11:24:00
2017-01-30 11:25:00
2017-01-30 11:26:00
2017-01-30 11:27:00
2017-01-30 11:28:00
2017-01-30 11:29:00
2017-01-30 11:30:00
2017-01-30 11:31:00
2017-01-30 11:32:00
2017-01-30 11:33:00
2017-01-30 11:34:00
2017-01-30 11:35:00
2017-01-30 11:36:00
2017-01-30 11:37:00
2017-01-30 11:38:00
2017-01-30 11:39:00
2017-01-30 11:40:00
2017-01-30 11:41:00
2017-01-30 11:42:00
2017-01-30 11:43:00
2017-01-30 11:44:00
2017-01-30 11:45:00
2017-01-30 11:46:00
2017-01-30 11:47:00
2017-01-30 11:48:00
2017-01-30 11:49:00
2017-01-30 11:50:00
2017-01-30 11:51:00
2017-01-30 11:52:00
2017-01-30 11:53:00


2017-01-31 11:45:00
2017-01-31 11:46:00
2017-01-31 11:47:00
2017-01-31 11:48:00
2017-01-31 11:49:00
2017-01-31 11:50:00
2017-01-31 11:51:00
2017-01-31 11:52:00
2017-01-31 11:53:00
2017-01-31 11:54:00
2017-01-31 11:55:00
2017-01-31 11:56:00
2017-01-31 11:57:00
2017-01-31 11:58:00
2017-01-31 11:59:00
2017-01-31 12:00:00
2017-01-31 12:01:00
2017-01-31 12:02:00
2017-01-31 12:03:00
2017-01-31 12:04:00
2017-01-31 12:05:00
2017-01-31 12:06:00
2017-01-31 12:07:00
2017-01-31 12:08:00
2017-01-31 12:09:00
2017-01-31 12:10:00
2017-01-31 12:11:00
2017-01-31 12:12:00
2017-01-31 12:13:00
2017-01-31 12:14:00
2017-01-31 12:15:00
2017-01-31 12:16:00
2017-01-31 12:17:00
2017-01-31 12:18:00
2017-01-31 12:19:00
2017-01-31 12:20:00
2017-01-31 12:21:00
2017-01-31 12:22:00
2017-01-31 12:23:00
2017-01-31 12:24:00
2017-01-31 12:25:00
2017-01-31 12:26:00
2017-01-31 12:27:00
2017-01-31 12:28:00
2017-01-31 12:29:00
2017-01-31 12:30:00
2017-01-31 12:31:00
2017-01-31 12:32:00
2017-01-31 12:33:00
2017-01-31 12:34:00


...

2017-03-02 12:26:00
2017-03-02 12:27:00
2017-03-02 12:28:00
2017-03-02 12:29:00
2017-03-02 12:30:00
2017-03-02 12:31:00
2017-03-02 12:32:00
2017-03-02 12:33:00
2017-03-02 12:34:00
2017-03-02 12:35:00
2017-03-02 12:36:00
2017-03-02 12:37:00
2017-03-02 12:38:00
2017-03-02 12:39:00
2017-03-02 12:40:00
2017-03-02 12:41:00
2017-03-02 12:42:00
2017-03-02 12:43:00
2017-03-02 12:44:00
2017-03-02 12:45:00
2017-03-02 12:46:00
2017-03-02 12:47:00
2017-03-02 12:48:00
2017-03-02 12:49:00
2017-03-02 12:50:00
2017-03-02 12:51:00
2017-03-02 12:52:00
2017-03-02 12:53:00
2017-03-02 12:54:00
2017-03-02 12:55:00
2017-03-02 12:56:00
2017-03-02 12:57:00
2017-03-02 12:58:00
2017-03-02 12:59:00
2017-03-02 13:00:00
2017-03-02 13:01:00
2017-03-02 13:02:00
2017-03-02 13:03:00
2017-03-02 13:04:00
2017-03-02 13:05:00
2017-03-02 13:06:00
2017-03-02 13:07:00
2017-03-02 13:08:00
2017-03-02 13:09:00
2017-03-02 13:10:00
2017-03-02 13:11:00
2017-03-02 13:12:00
2017-03-02 13:13:00
2017-03-02 13:14:00
2017-03-02 13:15:00


2017-03-03 13:07:00
2017-03-03 13:08:00
2017-03-03 13:09:00
2017-03-03 13:10:00
2017-03-03 13:11:00
2017-03-03 13:12:00
2017-03-03 13:13:00
2017-03-03 13:14:00
2017-03-03 13:15:00
2017-03-03 13:16:00
2017-03-03 13:17:00
2017-03-03 13:18:00
2017-03-03 13:19:00
2017-03-03 13:20:00
2017-03-03 13:21:00
2017-03-03 13:22:00
2017-03-03 13:23:00
2017-03-03 13:24:00
2017-03-03 13:25:00
2017-03-03 13:26:00
2017-03-03 13:27:00
2017-03-03 13:28:00
2017-03-03 13:29:00
2017-03-03 13:30:00
2017-03-03 13:31:00
2017-03-03 13:32:00
2017-03-03 13:33:00
2017-03-03 13:34:00
2017-03-03 13:35:00
2017-03-03 13:36:00
2017-03-03 13:37:00
2017-03-03 13:38:00
2017-03-03 13:39:00
2017-03-03 13:40:00
2017-03-03 13:41:00
2017-03-03 13:42:00
2017-03-03 13:43:00
2017-03-03 13:44:00
2017-03-03 13:45:00
2017-03-03 13:46:00
2017-03-03 13:47:00
2017-03-03 13:48:00
2017-03-03 13:49:00
2017-03-03 13:50:00
2017-03-03 13:51:00
2017-03-03 13:52:00
2017-03-03 13:53:00
2017-03-03 13:54:00
2017-03-03 13:55:00
2017-03-03 13:56:00


2017-03-06 13:48:00
2017-03-06 13:49:00
2017-03-06 13:50:00
2017-03-06 13:51:00
2017-03-06 13:52:00
2017-03-06 13:53:00
2017-03-06 13:54:00
2017-03-06 13:55:00
2017-03-06 13:56:00
2017-03-06 13:57:00
2017-03-06 13:58:00
2017-03-06 13:59:00
2017-03-06 14:00:00
2017-03-06 14:01:00
2017-03-06 14:02:00
2017-03-06 14:03:00
2017-03-06 14:04:00
2017-03-06 14:05:00
2017-03-06 14:06:00
2017-03-06 14:07:00
2017-03-06 14:08:00
2017-03-06 14:09:00
2017-03-06 14:10:00
2017-03-06 14:11:00
2017-03-06 14:12:00
2017-03-06 14:13:00
2017-03-06 14:14:00
2017-03-06 14:15:00
2017-03-06 14:16:00
2017-03-06 14:17:00
2017-03-06 14:18:00
2017-03-06 14:19:00
2017-03-06 14:20:00
2017-03-06 14:21:00
2017-03-06 14:22:00
2017-03-06 14:23:00
2017-03-06 14:24:00
2017-03-06 14:25:00
2017-03-06 14:26:00
2017-03-06 14:27:00
2017-03-06 14:28:00
2017-03-06 14:29:00
2017-03-06 14:30:00
2017-03-06 14:31:00
2017-03-06 14:32:00
2017-03-06 14:33:00
2017-03-06 14:34:00
2017-03-06 14:35:00
2017-03-06 14:36:00
2017-03-06 14:37:00


2017-03-07 14:30:00
2017-03-07 14:31:00
2017-03-07 14:32:00
2017-03-07 14:33:00
2017-03-07 14:34:00
2017-03-07 14:35:00
2017-03-07 14:36:00
2017-03-07 14:37:00
2017-03-07 14:38:00
2017-03-07 14:39:00
2017-03-07 14:40:00
2017-03-07 14:41:00
2017-03-07 14:42:00
2017-03-07 14:43:00
2017-03-07 14:44:00
2017-03-07 14:45:00
2017-03-07 14:46:00
2017-03-07 14:47:00
2017-03-07 14:48:00
2017-03-07 14:49:00
2017-03-07 14:50:00
2017-03-07 14:51:00
2017-03-07 14:52:00
2017-03-07 14:53:00
2017-03-07 14:54:00
2017-03-07 14:55:00
2017-03-07 14:56:00
2017-03-07 14:57:00
2017-03-07 14:58:00
2017-03-07 14:59:00
2017-03-07 15:00:00
2017-03-07 15:01:00
2017-03-07 15:02:00
2017-03-07 15:03:00
2017-03-07 15:04:00
2017-03-07 15:05:00
2017-03-07 15:06:00
2017-03-07 15:07:00
2017-03-07 15:08:00
2017-03-07 15:09:00
2017-03-07 15:10:00
2017-03-07 15:11:00
2017-03-07 15:12:00
2017-03-07 15:13:00
2017-03-07 15:14:00
2017-03-07 15:15:00
2017-03-07 15:16:00
2017-03-07 15:17:00
2017-03-07 15:18:00
2017-03-07 15:19:00


2017-03-08 15:12:00
2017-03-08 15:13:00
2017-03-08 15:14:00
2017-03-08 15:15:00
2017-03-08 15:16:00
2017-03-08 15:17:00
2017-03-08 15:18:00
2017-03-08 15:19:00
2017-03-08 15:20:00
2017-03-08 15:21:00
2017-03-08 15:22:00
2017-03-08 15:23:00
2017-03-08 15:24:00
2017-03-08 15:25:00
2017-03-08 15:26:00
2017-03-08 15:27:00
2017-03-08 15:28:00
2017-03-09 09:17:00
2017-03-09 09:18:00
2017-03-09 09:19:00
2017-03-09 09:20:00
2017-03-09 09:21:00
2017-03-09 09:22:00
2017-03-09 09:23:00
2017-03-09 09:24:00
2017-03-09 09:25:00
2017-03-09 09:26:00
2017-03-09 09:27:00
2017-03-09 09:28:00
2017-03-09 09:29:00
2017-03-09 09:30:00
2017-03-09 09:31:00
2017-03-09 09:32:00
2017-03-09 09:33:00
2017-03-09 09:34:00
2017-03-09 09:35:00
2017-03-09 09:36:00
2017-03-09 09:37:00
2017-03-09 09:38:00
2017-03-09 09:39:00
2017-03-09 09:40:00
2017-03-09 09:41:00
2017-03-09 09:42:00
2017-03-09 09:43:00
2017-03-09 09:44:00
2017-03-09 09:45:00
2017-03-09 09:46:00
2017-03-09 09:47:00
2017-03-09 09:48:00
2017-03-09 09:49:00


In [ ]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
#         return ['BSN'
#  'DCO',
#  'DYE',
#  'FFA',
#  'FFS',
#  'HDK',
#  'HZT',
#  #'ILW',
#  'IMC',
#  'IWU',
#  #'IYU',
#  'KAA',
#  'KKG',
#  'LPQ',
#  'NNA',
#  #'NSL',
#  'OMP',
#  'QTY',
#  'QVE',
#  'RGG',
#  #'WTJ',
#  'WUT',
#  'XPV',
#  'XYR'
              ]
       # return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
         return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG'] 

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 20,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: VKE
Processing data for stock: UWC
Processing data for stock: HDK
Processing data for stock: IWU
Processing data for stock: IYU
Processing data for stock: HZT
Processing data for stock: TGI
Processing data for stock: AUZ
Processing data for stock: JSG
Processing data for stock: OMP
Processing data for stock: CYD
Processing data for stock: CHV
Processing data for stock: UBF
Processing data for stock: DCO
Processing data for stock: DVV
Processing data for stock: WUT
Processing data for stock: FKI
Processing data for stock: FFS
Processing data for stock: AIO
Processing data for stock: MQK
Processing data for stock: GGK
Processing data for stock: KFW
Processing data for stock: JYW
Processing data for stock: PLX
Processing data for stock: QVE
Processing data for stock: BLR
Processing data for stock: OGU
Processing data for stock: BSN
Processing data for stock: VML
Processing data for stock: KKG
Processing data for stock: VND
Processing data for stock: NDG
Processi

2017-01-25 13:32:00
2017-01-25 13:33:00
2017-01-25 13:34:00
2017-01-25 13:35:00
2017-01-25 13:36:00
2017-01-25 13:37:00
2017-01-25 13:38:00
2017-01-25 13:39:00
2017-01-25 13:40:00
2017-01-25 13:41:00
2017-01-25 13:42:00
2017-01-25 13:43:00
2017-01-25 13:44:00
2017-01-25 13:45:00
2017-01-25 13:46:00
2017-01-25 13:47:00
2017-01-25 13:48:00
2017-01-25 13:49:00
2017-01-25 13:50:00
2017-01-25 13:51:00
2017-01-25 13:52:00
2017-01-25 13:53:00
2017-01-25 13:54:00
2017-01-25 13:55:00
2017-01-25 13:56:00
2017-01-25 13:57:00
2017-01-25 13:58:00
2017-01-25 13:59:00
2017-01-25 14:00:00
2017-01-25 14:01:00
2017-01-25 14:02:00
2017-01-25 14:03:00
2017-01-25 14:04:00
2017-01-25 14:05:00
2017-01-25 14:06:00
2017-01-25 14:07:00
2017-01-25 14:08:00
2017-01-25 14:09:00
2017-01-25 14:10:00
2017-01-25 14:11:00
2017-01-25 14:12:00
2017-01-25 14:13:00
2017-01-25 14:14:00
2017-01-25 14:15:00
2017-01-25 14:16:00
2017-01-25 14:17:00
2017-01-25 14:18:00
2017-01-25 14:19:00
2017-01-25 14:20:00
2017-01-25 14:21:00


2017-01-26 14:06:00
2017-01-26 14:07:00
2017-01-26 14:08:00
2017-01-26 14:09:00
2017-01-26 14:10:00
2017-01-26 14:11:00
2017-01-26 14:12:00
2017-01-26 14:13:00
2017-01-26 14:14:00
2017-01-26 14:15:00
2017-01-26 14:16:00
2017-01-26 14:17:00
2017-01-26 14:18:00
2017-01-26 14:19:00
2017-01-26 14:20:00
2017-01-26 14:21:00
2017-01-26 14:22:00
2017-01-26 14:23:00
2017-01-26 14:24:00
2017-01-26 14:25:00
2017-01-26 14:26:00
2017-01-26 14:27:00
2017-01-26 14:28:00
2017-01-26 14:29:00
2017-01-26 14:30:00
2017-01-26 14:31:00
2017-01-26 14:32:00
2017-01-26 14:33:00
2017-01-26 14:34:00
2017-01-26 14:35:00
2017-01-26 14:36:00
2017-01-26 14:37:00
2017-01-26 14:38:00
2017-01-26 14:39:00
2017-01-26 14:40:00
2017-01-26 14:41:00
2017-01-26 14:42:00
2017-01-26 14:43:00
2017-01-26 14:44:00
2017-01-26 14:45:00
2017-01-26 14:46:00
2017-01-26 14:47:00
Warn: Not Enough Capital
2017-01-26 14:48:00
Warn: Not Enough Capital
2017-01-26 14:49:00
Warn: Not Enough Capital
2017-01-26 14:50:00
Warn: Not Enough Capital


2017-01-27 14:38:00
2017-01-27 14:39:00
2017-01-27 14:40:00
2017-01-27 14:41:00
2017-01-27 14:42:00
2017-01-27 14:43:00
2017-01-27 14:44:00
2017-01-27 14:45:00
2017-01-27 14:46:00
2017-01-27 14:47:00
2017-01-27 14:48:00
2017-01-27 14:49:00
2017-01-27 14:50:00
2017-01-27 14:51:00
2017-01-27 14:52:00
2017-01-27 14:53:00
2017-01-27 14:54:00
2017-01-27 14:55:00
2017-01-27 14:56:00
2017-01-27 14:57:00
2017-01-27 14:58:00
2017-01-27 14:59:00
2017-01-27 15:00:00
2017-01-27 15:01:00
2017-01-27 15:02:00
2017-01-27 15:03:00
2017-01-27 15:04:00
2017-01-27 15:05:00
2017-01-27 15:06:00
2017-01-27 15:07:00
2017-01-27 15:08:00
2017-01-27 15:09:00
2017-01-27 15:10:00
2017-01-27 15:11:00
2017-01-27 15:12:00
2017-01-27 15:13:00
2017-01-27 15:14:00
2017-01-27 15:15:00
2017-01-27 15:16:00
2017-01-27 15:17:00
2017-01-27 15:18:00
2017-01-27 15:19:00
2017-01-27 15:20:00
2017-01-27 15:21:00
2017-01-27 15:22:00
2017-01-27 15:23:00
2017-01-27 15:24:00
2017-01-27 15:25:00
2017-01-27 15:26:00
2017-01-27 15:27:00


2017-01-30 15:16:00
2017-01-30 15:17:00
2017-01-30 15:18:00
2017-01-30 15:19:00
2017-01-30 15:20:00
2017-01-30 15:21:00
2017-01-30 15:22:00
2017-01-30 15:23:00
2017-01-30 15:24:00
2017-01-30 15:25:00
2017-01-30 15:26:00
2017-01-30 15:27:00
2017-01-30 15:28:00
2017-01-31 09:17:00
2017-01-31 09:18:00
2017-01-31 09:19:00
2017-01-31 09:20:00
2017-01-31 09:21:00
2017-01-31 09:22:00
2017-01-31 09:23:00
2017-01-31 09:24:00
2017-01-31 09:25:00
2017-01-31 09:26:00
2017-01-31 09:27:00
2017-01-31 09:28:00
2017-01-31 09:29:00
2017-01-31 09:30:00
2017-01-31 09:31:00
2017-01-31 09:32:00
2017-01-31 09:33:00
2017-01-31 09:34:00
2017-01-31 09:35:00
2017-01-31 09:36:00
2017-01-31 09:37:00
2017-01-31 09:38:00
2017-01-31 09:39:00
2017-01-31 09:40:00
2017-01-31 09:41:00
2017-01-31 09:42:00
2017-01-31 09:43:00
2017-01-31 09:44:00
2017-01-31 09:45:00
2017-01-31 09:46:00
2017-01-31 09:47:00
2017-01-31 09:48:00
2017-01-31 09:49:00
2017-01-31 09:50:00
2017-01-31 09:51:00
2017-01-31 09:52:00
2017-01-31 09:53:00


...

2017-03-06 10:20:00
2017-03-06 10:21:00
2017-03-06 10:22:00
2017-03-06 10:23:00
2017-03-06 10:24:00
2017-03-06 10:25:00
2017-03-06 10:26:00
2017-03-06 10:27:00
2017-03-06 10:28:00
2017-03-06 10:29:00
2017-03-06 10:30:00
2017-03-06 10:31:00
2017-03-06 10:32:00
2017-03-06 10:33:00
2017-03-06 10:34:00
2017-03-06 10:35:00
2017-03-06 10:36:00
2017-03-06 10:37:00
2017-03-06 10:38:00
2017-03-06 10:39:00
2017-03-06 10:40:00
2017-03-06 10:41:00
2017-03-06 10:42:00
2017-03-06 10:43:00
2017-03-06 10:44:00
2017-03-06 10:45:00
2017-03-06 10:46:00
2017-03-06 10:47:00
2017-03-06 10:48:00
2017-03-06 10:49:00
2017-03-06 10:50:00
2017-03-06 10:51:00
2017-03-06 10:52:00
2017-03-06 10:53:00
2017-03-06 10:54:00
2017-03-06 10:55:00
2017-03-06 10:56:00
2017-03-06 10:57:00
2017-03-06 10:58:00
2017-03-06 10:59:00
2017-03-06 11:00:00
2017-03-06 11:01:00
2017-03-06 11:02:00
2017-03-06 11:03:00
2017-03-06 11:04:00
2017-03-06 11:05:00
2017-03-06 11:06:00
2017-03-06 11:07:00
2017-03-06 11:08:00
2017-03-06 11:09:00


2017-03-07 11:00:00
2017-03-07 11:01:00
2017-03-07 11:02:00
2017-03-07 11:03:00
2017-03-07 11:04:00
2017-03-07 11:05:00
2017-03-07 11:06:00
2017-03-07 11:07:00
2017-03-07 11:08:00
2017-03-07 11:09:00
2017-03-07 11:10:00
2017-03-07 11:11:00
2017-03-07 11:12:00
2017-03-07 11:13:00
2017-03-07 11:14:00
2017-03-07 11:15:00
2017-03-07 11:16:00
2017-03-07 11:17:00
2017-03-07 11:18:00
2017-03-07 11:19:00
2017-03-07 11:20:00
2017-03-07 11:21:00
2017-03-07 11:22:00
2017-03-07 11:23:00
2017-03-07 11:24:00
2017-03-07 11:25:00
2017-03-07 11:26:00
2017-03-07 11:27:00
2017-03-07 11:28:00
2017-03-07 11:29:00
2017-03-07 11:30:00
2017-03-07 11:31:00
2017-03-07 11:32:00
2017-03-07 11:33:00
2017-03-07 11:34:00
2017-03-07 11:35:00
2017-03-07 11:36:00
2017-03-07 11:37:00
2017-03-07 11:38:00
2017-03-07 11:39:00
2017-03-07 11:40:00
2017-03-07 11:41:00
2017-03-07 11:42:00
2017-03-07 11:43:00
2017-03-07 11:44:00
2017-03-07 11:45:00
2017-03-07 11:46:00
2017-03-07 11:47:00
2017-03-07 11:48:00
2017-03-07 11:49:00


2017-03-08 11:18:00
2017-03-08 11:19:00
2017-03-08 11:20:00
2017-03-08 11:21:00
2017-03-08 11:22:00
2017-03-08 11:23:00
2017-03-08 11:24:00
2017-03-08 11:25:00
2017-03-08 11:26:00
2017-03-08 11:27:00
2017-03-08 11:28:00
2017-03-08 11:29:00
2017-03-08 11:30:00
2017-03-08 11:31:00
2017-03-08 11:32:00
2017-03-08 11:33:00
2017-03-08 11:34:00
2017-03-08 11:35:00
2017-03-08 11:36:00
2017-03-08 11:37:00
2017-03-08 11:38:00
2017-03-08 11:39:00
2017-03-08 11:40:00
2017-03-08 11:41:00
2017-03-08 11:42:00
2017-03-08 11:43:00
2017-03-08 11:44:00
2017-03-08 11:45:00
2017-03-08 11:46:00
2017-03-08 11:47:00
2017-03-08 11:48:00
2017-03-08 11:49:00
2017-03-08 11:50:00
2017-03-08 11:51:00
2017-03-08 11:52:00
2017-03-08 11:53:00
2017-03-08 11:54:00
2017-03-08 11:55:00
2017-03-08 11:56:00
2017-03-08 11:57:00
2017-03-08 11:58:00
2017-03-08 11:59:00
2017-03-08 12:00:00
2017-03-08 12:01:00
2017-03-08 12:02:00
2017-03-08 12:03:00
2017-03-08 12:04:00
2017-03-08 12:05:00
2017-03-08 12:06:00
2017-03-08 12:07:00


2017-03-09 11:58:00
2017-03-09 11:59:00
2017-03-09 12:00:00
2017-03-09 12:01:00
2017-03-09 12:02:00
2017-03-09 12:03:00
2017-03-09 12:04:00
2017-03-09 12:05:00
2017-03-09 12:06:00
2017-03-09 12:07:00
2017-03-09 12:08:00
2017-03-09 12:09:00
2017-03-09 12:10:00
2017-03-09 12:11:00
2017-03-09 12:12:00
2017-03-09 12:13:00
2017-03-09 12:14:00
2017-03-09 12:15:00
2017-03-09 12:16:00
2017-03-09 12:17:00
2017-03-09 12:18:00
2017-03-09 12:19:00
2017-03-09 12:20:00
2017-03-09 12:21:00
2017-03-09 12:22:00
2017-03-09 12:23:00
2017-03-09 12:24:00
2017-03-09 12:25:00
2017-03-09 12:26:00
2017-03-09 12:27:00
2017-03-09 12:28:00
2017-03-09 12:29:00
2017-03-09 12:30:00
2017-03-09 12:31:00
2017-03-09 12:32:00
2017-03-09 12:33:00
2017-03-09 12:34:00
2017-03-09 12:35:00
2017-03-09 12:36:00
2017-03-09 12:37:00
2017-03-09 12:38:00
2017-03-09 12:39:00
2017-03-09 12:40:00
2017-03-09 12:41:00
2017-03-09 12:42:00
2017-03-09 12:43:00
2017-03-09 12:44:00
2017-03-09 12:45:00
2017-03-09 12:46:00
2017-03-09 12:47:00


Info: AUZ:  Total Pnl: -0.07%  Profit/Loss Ratio: 0.98  Accuracy: 0.47  Score: nan 
Info: VML:  Total Pnl: -0.08%  Profit/Loss Ratio: 0.85  Accuracy: 0.48  Score: 0.77 
Info: PUO:  Total Pnl: 0.07%  Profit/Loss Ratio: 1.06  Accuracy: 0.49  Score: nan 
Info: PLX:  Total Pnl: -0.06%  Profit/Loss Ratio: 0.95  Accuracy: 0.48  Score: 0.87 
Info: OMP:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.15  Accuracy: 0.42  Score: 0.70 
Info: ZEW:  Total Pnl: -0.11%  Profit/Loss Ratio: 0.92  Accuracy: 0.48  Score: 0.82 
Info: OED:  Total Pnl: 0.05%  Profit/Loss Ratio: 1.02  Accuracy: 0.47  Score: nan 
Info: JYW:  Total Pnl: -0.04%  Profit/Loss Ratio: 0.85  Accuracy: 0.50  Score: 0.72 
Info: IYU:  Total Pnl: -0.06%  Profit/Loss Ratio: 0.86  Accuracy: 0.49  Score: 0.76 
Info: AIO:  Total Pnl: -0.02%  Profit/Loss Ratio: 0.97  Accuracy: 0.50  Score: inf 
Info: ZSI:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.16  Accuracy: 0.52  Score: 0.70 
Info: KFW:  Total Pnl: 0.86%  Profit/Loss Ratio: 1.08  Accuracy: 0.47  Sc

In [3]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.feature_prediction_params import FeaturePredictionTradingParams
from backtester.version import updateCheck
import numpy as np
import scipy.stats as st


class Problem2Solver():

    '''
    Specifies which training data set to use. Right now support
    trainginDataP2_1, trainginDataP2_2.
    '''
    def getTrainingDataSet(self):
        return "trainingDataP2_3"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''
    def getSymbolsToTrade(self):
#         return ['BSN'
#  'DCO',
#  'DYE',
#  'FFA',
#  'FFS',
#  'HDK',
#  'HZT',
#  #'ILW',
#  'IMC',
#  'IWU',
#  #'IYU',
#  'KAA',
#  'KKG',
#  'LPQ',
#  'NNA',
#  #'NSL',
#  'OMP',
#  'QTY',
#  'QVE',
#  'RGG',
#  #'WTJ',
#  'WUT',
#  'XPV',
#  'XYR'
          #    ]
       # return ['HDK', 'IWU', 'IYU', 'HZT' ,'OMP','CYD','CHV','UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'MQK','PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','PFK', 'MUF', 'XIT','YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','PQS', 'KRZ', 'OED','QTY','XYR', 'LPQ', 'DUR', 'XAD','VSL', 'NYO', 'IUE','NNA', 'RGG', 'XZR','BWU', 'LDU', 'UWD','KAA', 'FFA', 'ILW', 'WTJ', 'CUN', 'IUQ', 'IMC', 'NSL','WAG']
       # return [ 'UWC', 'HDK', 'IWU', 'IYU', 'HZT' , 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS','MQK', 'GGK','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG','NDG', 'PFK', 'MUF', 'YHW', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV','ESY',  'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY','XYR', 'LPQ', 'DUR', 'XAD', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR','MAS','BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG']
       # return []
         return ['VKE', 'UWC', 'HDK', 'IWU', 'IYU', 'HZT', 'TGI', 'AUZ', 'JSG', 'OMP', 'CYD', 'CHV', 'UBF', 'DCO', 'DVV', 'WUT', 'FKI', 'FFS', 'AIO', 'MQK', 'GGK', 'KFW','JYW', 'PLX', 'QVE', 'BLR', 'OGU', 'BSN', 'VML', 'KKG', 'VND', 'NDG', 'PFK', 'MUF', 'QRK', 'GYV', 'CBT', 'YHW', 'HHK', 'XIT', 'GYJ', 'YUZ', 'DYE', 'ZEW', 'ZLX', 'FRE', 'GFQ', 'XPV', 'YGC', 'ESY', 'FUR', 'IFL', 'PQS', 'KRZ', 'OED', 'FCY', 'XCS', 'IES', 'QTY', 'CQD', 'XYR', 'LPQ', 'DUR', 'XAD', 'EGV', 'LKB', 'VSL', 'NYO', 'IUE', 'AGW', 'NNA', 'RGG', 'XZR', 'ROP', 'MAS', 'PUO', 'BWU', 'LDU', 'UWD', 'PMS', 'ZSI', 'NBQ', 'KAA', 'FFA', 'ILW', 'WTJ', 'VTN', 'XFD', 'CUN', 'IUQ', 'IMC', 'NSL', 'JCR', 'WAG'] 

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''
    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''
    def getFeatureConfigDicts(self):
        ma1Dict = {'featureKey': 'ma_30',
                   'featureId': 'moving_average',
                   'params': {'period': 20,
                              'featureName': 'stockVWAP'}}
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'stockVWAP'}}
        sdevDict = {'featureKey': 'sdev_30',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'stockVWAP'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, ma2Dict, sdevDict, customFeatureDict]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the probability as specified in the question.
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getClassifierProbability(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (exponential_moving_average in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        sdevDf = lookbackInstrumentFeatures.getFeatureDf('sdev_30')
        mavg30Df = lookbackInstrumentFeatures.getFeatureDf('ma_30')
        mavg5Df = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        z_score = (mavg30Df.iloc[-1] - mavg5Df.iloc[-1]) #/ sdevDf.iloc[-1]
        z_score.fillna(0, inplace=True)
        return st.norm.cdf(z_score)


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentVWAP = lookbackInstrumentFeatures.getFeatureDf('stockVWAP')

        # The last row of the previous dataframe gives the last calculated value for that feature (stockVWAP in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentVWAP = lookbackInstrumentVWAP.iloc[-1]

        if param1Value == 'value1':
            return currentVWAP * 0.1
        else:
            return currentVWAP * 0.4


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem2Solver = Problem2Solver()
        tsParams = FeaturePredictionTradingParams(problem2Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: VKE
Processing data for stock: UWC
Processing data for stock: HDK
Processing data for stock: IWU
Processing data for stock: IYU
Processing data for stock: HZT
Processing data for stock: TGI
Processing data for stock: AUZ
Processing data for stock: JSG
Processing data for stock: OMP
Processing data for stock: CYD
Processing data for stock: CHV
Processing data for stock: UBF
Processing data for stock: DCO
Processing data for stock: DVV
Processing data for stock: WUT
Processing data for stock: FKI
Processing data for stock: FFS
Processing data for stock: AIO
Processing data for stock: MQK
Processing data for stock: GGK
Processing data for stock: KFW
Processing data for stock: JYW
Processing data for stock: PLX
Processing data for stock: QVE
Processing data for stock: BLR
Processing data for stock: OGU
Processing data for stock: BSN
Processing data for stock: VML
Processing data for stock: KKG
Processing data for stock: VND
Processing data for stock: NDG
Processi

2017-01-02 13:32:00
2017-01-02 13:33:00
2017-01-02 13:34:00
2017-01-02 13:35:00
2017-01-02 13:36:00
2017-01-02 13:37:00
2017-01-02 13:38:00
2017-01-02 13:39:00
2017-01-02 13:40:00
2017-01-02 13:41:00
2017-01-02 13:42:00
2017-01-02 13:43:00
2017-01-02 13:44:00
2017-01-02 13:45:00
2017-01-02 13:46:00
2017-01-02 13:47:00
2017-01-02 13:48:00
2017-01-02 13:49:00
2017-01-02 13:50:00
2017-01-02 13:51:00
2017-01-02 13:52:00
2017-01-02 13:53:00
2017-01-02 13:54:00
2017-01-02 13:55:00
2017-01-02 13:56:00
2017-01-02 13:57:00
2017-01-02 13:58:00
2017-01-02 13:59:00
2017-01-02 14:00:00
2017-01-02 14:01:00
2017-01-02 14:02:00
2017-01-02 14:03:00
2017-01-02 14:04:00
2017-01-02 14:05:00
2017-01-02 14:06:00
2017-01-02 14:07:00
2017-01-02 14:08:00
2017-01-02 14:09:00
2017-01-02 14:10:00
2017-01-02 14:11:00
2017-01-02 14:12:00
2017-01-02 14:13:00
2017-01-02 14:14:00
2017-01-02 14:15:00
2017-01-02 14:16:00
2017-01-02 14:17:00
2017-01-02 14:18:00
2017-01-02 14:19:00
2017-01-02 14:20:00
2017-01-02 14:21:00


2017-01-03 14:11:00
2017-01-03 14:12:00
2017-01-03 14:13:00
2017-01-03 14:14:00
2017-01-03 14:15:00
2017-01-03 14:16:00
2017-01-03 14:17:00
2017-01-03 14:18:00
2017-01-03 14:19:00
2017-01-03 14:20:00
2017-01-03 14:21:00
2017-01-03 14:22:00
2017-01-03 14:23:00
2017-01-03 14:24:00
2017-01-03 14:25:00
2017-01-03 14:26:00
2017-01-03 14:27:00
2017-01-03 14:28:00
2017-01-03 14:29:00
2017-01-03 14:30:00
2017-01-03 14:31:00
2017-01-03 14:32:00
2017-01-03 14:33:00
2017-01-03 14:34:00
2017-01-03 14:35:00
2017-01-03 14:36:00
2017-01-03 14:37:00
2017-01-03 14:38:00
2017-01-03 14:39:00
2017-01-03 14:40:00
2017-01-03 14:41:00
2017-01-03 14:42:00
2017-01-03 14:43:00
2017-01-03 14:44:00
2017-01-03 14:45:00
2017-01-03 14:46:00
2017-01-03 14:47:00
2017-01-03 14:48:00
2017-01-03 14:49:00
2017-01-03 14:50:00
2017-01-03 14:51:00
2017-01-03 14:52:00
2017-01-03 14:53:00
2017-01-03 14:54:00
2017-01-03 14:55:00
2017-01-03 14:56:00
2017-01-03 14:57:00
2017-01-03 14:58:00
2017-01-03 14:59:00
2017-01-03 15:00:00


2017-01-04 14:49:00
2017-01-04 14:50:00
2017-01-04 14:51:00
2017-01-04 14:52:00
2017-01-04 14:53:00
2017-01-04 14:54:00
2017-01-04 14:55:00
2017-01-04 14:56:00
2017-01-04 14:57:00
2017-01-04 14:58:00
2017-01-04 14:59:00
2017-01-04 15:00:00
2017-01-04 15:01:00
2017-01-04 15:02:00
2017-01-04 15:03:00
2017-01-04 15:04:00
2017-01-04 15:05:00
2017-01-04 15:06:00
2017-01-04 15:07:00
2017-01-04 15:08:00
2017-01-04 15:09:00
2017-01-04 15:10:00
2017-01-04 15:11:00
2017-01-04 15:12:00
2017-01-04 15:13:00
2017-01-04 15:14:00
2017-01-04 15:15:00
2017-01-04 15:16:00
2017-01-04 15:17:00
2017-01-04 15:18:00
2017-01-04 15:19:00
2017-01-04 15:20:00
2017-01-04 15:21:00
2017-01-04 15:22:00
2017-01-04 15:23:00
2017-01-04 15:24:00
2017-01-04 15:25:00
2017-01-04 15:26:00
2017-01-04 15:27:00
2017-01-04 15:28:00
2017-01-05 09:17:00
2017-01-05 09:18:00
2017-01-05 09:19:00
2017-01-05 09:20:00
2017-01-05 09:21:00
2017-01-05 09:22:00
2017-01-05 09:23:00
2017-01-05 09:24:00
2017-01-05 09:25:00
2017-01-05 09:26:00


2017-01-05 15:27:00
2017-01-05 15:28:00
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-01-06 09:23:00
2017-01-06 09:24:00
2017-01-06 09:25:00
2017-01-06 09:26:00
2017-01-06 09:27:00
2017-01-06 09:28:00
2017-01-06 09:29:00
2017-01-06 09:30:00
2017-01-06 09:31:00
2017-01-06 09:32:00
2017-01-06 09:33:00
2017-01-06 09:34:00
2017-01-06 09:35:00
2017-01-06 09:36:00
2017-01-06 09:37:00
2017-01-06 09:38:00
2017-01-06 09:39:00
2017-01-06 09:40:00
2017-01-06 09:41:00
2017-01-06 09:42:00
2017-01-06 09:43:00
2017-01-06 09:44:00
2017-01-06 09:45:00
2017-01-06 09:46:00
2017-01-06 09:47:00
2017-01-06 09:48:00
2017-01-06 09:49:00
2017-01-06 09:50:00
2017-01-06 09:51:00
2017-01-06 09:52:00
2017-01-06 09:53:00
2017-01-06 09:54:00
2017-01-06 09:55:00
2017-01-06 09:56:00
2017-01-06 09:57:00
2017-01-06 09:58:00
2017-01-06 09:59:00
2017-01-06 10:00:00
2017-01-06 10:01:00
2017-01-06 10:02:00
2017-01-06 10:03:00
2017-01-06 10:04:00


...

2017-01-25 10:43:00
2017-01-25 10:44:00
2017-01-25 10:45:00
2017-01-25 10:46:00
2017-01-25 10:47:00
2017-01-25 10:48:00
2017-01-25 10:49:00
2017-01-25 10:50:00
2017-01-25 10:51:00
2017-01-25 10:52:00
2017-01-25 10:53:00
2017-01-25 10:54:00
2017-01-25 10:55:00
2017-01-25 10:56:00
2017-01-25 10:57:00
2017-01-25 10:58:00
2017-01-25 10:59:00
2017-01-25 11:00:00
2017-01-25 11:01:00
2017-01-25 11:02:00
2017-01-25 11:03:00
2017-01-25 11:04:00
2017-01-25 11:05:00
2017-01-25 11:06:00
2017-01-25 11:07:00
2017-01-25 11:08:00
2017-01-25 11:09:00
2017-01-25 11:10:00
2017-01-25 11:11:00
2017-01-25 11:12:00
2017-01-25 11:13:00
2017-01-25 11:14:00
2017-01-25 11:15:00
2017-01-25 11:16:00
2017-01-25 11:17:00
2017-01-25 11:18:00
2017-01-25 11:19:00
2017-01-25 11:20:00
2017-01-25 11:21:00
2017-01-25 11:22:00
2017-01-25 11:23:00
2017-01-25 11:24:00
2017-01-25 11:25:00
2017-01-25 11:26:00
2017-01-25 11:27:00
2017-01-25 11:28:00
2017-01-25 11:29:00
2017-01-25 11:30:00
2017-01-25 11:31:00
2017-01-25 11:32:00


2017-01-27 11:22:00
2017-01-27 11:23:00
2017-01-27 11:24:00
2017-01-27 11:25:00
2017-01-27 11:26:00
2017-01-27 11:27:00
2017-01-27 11:28:00
2017-01-27 11:29:00
2017-01-27 11:30:00
2017-01-27 11:31:00
2017-01-27 11:32:00
2017-01-27 11:33:00
2017-01-27 11:34:00
2017-01-27 11:35:00
2017-01-27 11:36:00
2017-01-27 11:37:00
2017-01-27 11:38:00
2017-01-27 11:39:00
2017-01-27 11:40:00
2017-01-27 11:41:00
2017-01-27 11:42:00
2017-01-27 11:43:00
2017-01-27 11:44:00
2017-01-27 11:45:00
2017-01-27 11:46:00
2017-01-27 11:47:00
2017-01-27 11:48:00
2017-01-27 11:49:00
2017-01-27 11:50:00
2017-01-27 11:51:00
2017-01-27 11:52:00
2017-01-27 11:53:00
2017-01-27 11:54:00
2017-01-27 11:55:00
2017-01-27 11:56:00
2017-01-27 11:57:00
2017-01-27 11:58:00
2017-01-27 11:59:00
2017-01-27 12:00:00
2017-01-27 12:01:00
2017-01-27 12:02:00
2017-01-27 12:03:00
2017-01-27 12:04:00
2017-01-27 12:05:00
2017-01-27 12:06:00
2017-01-27 12:07:00
2017-01-27 12:08:00
2017-01-27 12:09:00
2017-01-27 12:10:00
2017-01-27 12:11:00


2017-01-30 11:57:00
2017-01-30 11:58:00
2017-01-30 11:59:00
2017-01-30 12:00:00
2017-01-30 12:01:00
2017-01-30 12:02:00
2017-01-30 12:03:00
2017-01-30 12:04:00
2017-01-30 12:05:00
2017-01-30 12:06:00
2017-01-30 12:07:00
2017-01-30 12:08:00
2017-01-30 12:09:00
2017-01-30 12:10:00
2017-01-30 12:11:00
2017-01-30 12:12:00
2017-01-30 12:13:00
2017-01-30 12:14:00
2017-01-30 12:15:00
2017-01-30 12:16:00
2017-01-30 12:17:00
2017-01-30 12:18:00
2017-01-30 12:19:00
2017-01-30 12:20:00
2017-01-30 12:21:00
2017-01-30 12:22:00
2017-01-30 12:23:00
2017-01-30 12:24:00
2017-01-30 12:25:00
2017-01-30 12:26:00
2017-01-30 12:27:00
2017-01-30 12:28:00
2017-01-30 12:29:00
2017-01-30 12:30:00
2017-01-30 12:31:00
2017-01-30 12:32:00
2017-01-30 12:33:00
2017-01-30 12:34:00
2017-01-30 12:35:00
2017-01-30 12:36:00
2017-01-30 12:37:00
2017-01-30 12:38:00
2017-01-30 12:39:00
2017-01-30 12:40:00
2017-01-30 12:41:00
2017-01-30 12:42:00
2017-01-30 12:43:00
2017-01-30 12:44:00
2017-01-30 12:45:00
2017-01-30 12:46:00


2017-01-31 12:28:00
2017-01-31 12:29:00
2017-01-31 12:30:00
2017-01-31 12:31:00
2017-01-31 12:32:00
2017-01-31 12:33:00
2017-01-31 12:34:00
2017-01-31 12:35:00
2017-01-31 12:36:00
2017-01-31 12:37:00
2017-01-31 12:38:00
2017-01-31 12:39:00
2017-01-31 12:40:00
2017-01-31 12:41:00
2017-01-31 12:42:00
2017-01-31 12:43:00
2017-01-31 12:44:00
2017-01-31 12:45:00
2017-01-31 12:46:00
2017-01-31 12:47:00
2017-01-31 12:48:00
2017-01-31 12:49:00
2017-01-31 12:50:00
2017-01-31 12:51:00
2017-01-31 12:52:00
2017-01-31 12:53:00
2017-01-31 12:54:00
2017-01-31 12:55:00
2017-01-31 12:56:00
2017-01-31 12:57:00
2017-01-31 12:58:00
2017-01-31 12:59:00
2017-01-31 13:00:00
2017-01-31 13:01:00
2017-01-31 13:02:00
2017-01-31 13:03:00
2017-01-31 13:04:00
2017-01-31 13:05:00
2017-01-31 13:06:00
2017-01-31 13:07:00
2017-01-31 13:08:00
2017-01-31 13:09:00
2017-01-31 13:10:00
2017-01-31 13:11:00
2017-01-31 13:12:00
2017-01-31 13:13:00
2017-01-31 13:14:00
2017-01-31 13:15:00
2017-01-31 13:16:00
2017-01-31 13:17:00


Info: NSL:  Total Pnl: -0.02%  Profit/Loss Ratio: 0.60  Accuracy: 0.48  Score: 0.71 
Info: QRK:  Total Pnl: -0.28%  Profit/Loss Ratio: 0.98  Accuracy: 0.48  Score: nan 
Info: GYJ:  Total Pnl: -0.01%  Profit/Loss Ratio: 1.00  Accuracy: 0.47  Score: nan 
Info: GYV:  Total Pnl: 0.17%  Profit/Loss Ratio: 1.03  Accuracy: 0.48  Score: nan 
Info: CYD:  Total Pnl: -0.00%  Profit/Loss Ratio: 0.92  Accuracy: 0.46  Score: 0.71 
Info: DYE:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.07  Accuracy: 0.46  Score: 0.71 
Info: TGI:  Total Pnl: -0.57%  Profit/Loss Ratio: 0.94  Accuracy: 0.47  Score: nan 
Info: FKI:  Total Pnl: -0.02%  Profit/Loss Ratio: 0.99  Accuracy: 0.48  Score: 0.92 
Info: JCR:  Total Pnl: 0.09%  Profit/Loss Ratio: 5.34  Accuracy: 0.40  Score: nan 
Info: ESY:  Total Pnl: 0.00%  Profit/Loss Ratio: nan  Accuracy: 0.00  Score: 0.69 
Info: KAA:  Total Pnl: -0.01%  Profit/Loss Ratio: 0.94  Accuracy: 0.49  Score: 0.72 
Info: VKE:  Total Pnl: 0.09%  Profit/Loss Ratio: 1.03  Accuracy: 0.46  Scor